In [28]:
from rdflib import Graph
from tqdm import tqdm
from datasets import load_from_disk

import pandas as pd
import re

In [2]:
prefix = '''@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dbo: <http://dbpedia.org/ontology/> .
@prefix dct: <http://purl.org/dc/terms/> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix wd: <https://www.wikidata.org/wiki/> .
@prefix lexid-s: <https://w3id.org/lex-id/schema/> .
@prefix lexid: <https://w3id.org/lex-id/data/> .

'''

In [3]:
from rdflib import Graph, Namespace, URIRef
from rdflib.namespace import XSD, RDFS, RDF, OWL
from rdflib.exceptions import ParserError


def is_valid_triples(triple_str):
    ttl = prefix
    ttl += triple_str
    
#     print(ttl)
    
    g = Graph()
    DBO = Namespace("http://dbpedia.org/ontology/")
    DCT = Namespace("http://purl.org/dc/terms/")
    WD = Namespace("https://www.wikidata.org/wiki/")
    LEXID_S = Namespace("https://w3id.org/lex-id/schema/")
    LEXID = Namespace("https://w3id.org/lex-id/data/")

    g.bind("xsd", XSD)
    g.bind("rdfs", RDFS)
    g.bind("rdf", RDF)
    g.bind("dbo", DBO)
    g.bind("dct", DCT)
    g.bind("owl", OWL)
    g.bind("wd", WD)
    g.bind("lexid-s", LEXID_S)
    g.bind("lexid", LEXID)
    
    try:
        g.parse(data=ttl, format="turtle")
        return True
    except:
        return False

In [4]:
from rdflib import Graph, Namespace, URIRef
from rdflib.namespace import XSD, RDFS, RDF, OWL
from rdflib.exceptions import ParserError


def is_valid_ttl(triple_str):
    g = Graph()
    DBO = Namespace("http://dbpedia.org/ontology/")
    DCT = Namespace("http://purl.org/dc/terms/")
    WD = Namespace("https://www.wikidata.org/wiki/")
    LEXID_S = Namespace("https://w3id.org/lex-id/schema/")
    LEXID = Namespace("https://w3id.org/lex-id/data/")

    g.bind("xsd", XSD)
    g.bind("rdfs", RDFS)
    g.bind("rdf", RDF)
    g.bind("dbo", DBO)
    g.bind("dct", DCT)
    g.bind("owl", OWL)
    g.bind("wd", WD)
    g.bind("lexid-s", LEXID_S)
    g.bind("lexid", LEXID)
    
    try:
        g.parse(data=triple_str, format="turtle")
#         for subj, pred, obj in g:
#             print(f"Subject: {subj}, Predicate: {pred}, Object: {obj}")
        return True
    except:
        return False

In [34]:
is_valid_ttl(cc_gemma.at[0, '1'])

True

In [60]:
def evaluate_ttl(ttl_pred, ttl_gold):
    g_pred = Graph()
    g_pred.parse(data=ttl_pred, format="turtle")

    g_gold = Graph()
    g_gold.parse(data=ttl_gold, format="turtle")

    g_pred_total = len(g_pred)
    g_gold_total = len(g_gold)

    tp = len(set(g_pred).intersection(set(g_gold)))

    fp = g_pred_total - tp
    fn = g_gold_total - tp
    
    if tp + fp == 0:
        p = 0
    else:
        p = round(tp / (tp + fp), 3)
        
    if tp + fn == 0:
        r = 0
    else:
        r = round(tp / (tp + fn), 3)
    
    if p + r == 0:
        f1 = 0
    else:
        f1 = round((2 * p * r)/ (p + r), 3)
    
    return tp, fp, fn, p, r, f1

In [59]:
from rdflib import Graph, Namespace, Literal

def literals_case_insensitive_equal(lit1, lit2):
    return str(lit1).lower() == str(lit2).lower()

def triple_case_insensitive_equal(triple1, triple2):
    return (
        triple1[0] == triple2[0] and
        triple1[1] == triple2[1] and
        (
            (isinstance(triple1[2], Literal) and isinstance(triple2[2], Literal) and literals_case_insensitive_equal(triple1[2], triple2[2])) or
            (not isinstance(triple1[2], Literal) and not isinstance(triple2[2], Literal) and triple1[2] == triple2[2])
        )
    )

def evaluate_ttl_case_insensitive(ttl_pred, ttl_gold):
    g_pred = Graph()
    g_pred.parse(data=ttl_pred, format="turtle")

    g_gold = Graph()
    g_gold.parse(data=ttl_gold, format="turtle")

    g_pred_total = len(g_pred)
    g_gold_total = len(g_gold)

    tp = 0
    for triple in g_pred:
        if any(triple_case_insensitive_equal(triple, gold_triple) for gold_triple in g_gold):
            tp += 1

    fp = g_pred_total - tp
    fn = g_gold_total - tp

    if tp + fp == 0:
        p = 0
    else:
        p = round(tp / (tp + fp), 3)
        
    if tp + fn == 0:
        r = 0
    else:
        r = round(tp / (tp + fn), 3)
    
    if p + r == 0:
        f1 = 0
    else:
        f1 = round((2 * p * r) / (p + r), 3)
    
    return tp, fp, fn, p, r, f1

ttl_pred = """
@prefix ex: <http://example.org/> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .

ex:PP_2019 rdfs:label "TES"^^xsd:string .
ex:PP_2019 ex:tes "TES"^^xsd:string .
ex:PP_2019 ex:hasLegalBasis ex:PP_2017 .
"""

ttl_gold = """
@prefix ex: <http://example.org/> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .

ex:PP_2019 rdfs:label "Tes"^^xsd:string .
ex:PP_2019 ex:tes "Tes"^^xsd:string .
ex:PP_2019 ex:hasLegalBasis ex:pp_2017 .
"""

# ttl_pred = """
# @prefix ex: <http://example.org/> .
# @prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
# @prefix xsd: <http://www.w3.org/2001/XMLSchema#> .

# ex:PP_2019 rdfs:label "TES"^^xsd:string .
# """

# ttl_gold = """
# @prefix ex: <http://example.org/> .
# @prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
# @prefix xsd: <http://www.w3.org/2001/XMLSchema#> .

# ex:PP_2019 rdfs:label "Tes"^^xsd:string .
# """

# tp, fp, fn, p, r, f1 = evaluate_ttl(ttl_pred, ttl_gold)
# print(f"TP: {tp}, FP: {fp}, FN: {fn}, Precision: {p}, Recall: {r}, F1 Score: {f1}")

In [3]:
# def evaluate_ttl_case_insensitive(ttl_pred, ttl_gold):
#     g_pred = Graph()
#     g_pred.parse(data=ttl_pred.lower(), format="turtle")

#     g_gold = Graph()
#     g_gold.parse(data=ttl_gold.lower(), format="turtle")

#     g_pred_total = len(g_pred)
#     g_gold_total = len(g_gold)

#     tp = len(set(g_pred).intersection(set(g_gold)))

#     fp = g_pred_total - tp
#     fn = g_gold_total - tp
    
#     if tp + fp == 0:
#         p = 0
#     else:
#         p = tp / (tp + fp)
        
#     if tp + fn == 0:
#         r = 0
#     else:
#         r = tp / (tp + fn)
    
#     if p + r == 0:
#         f1 = 0
#     else:
#         f1 = (2 * p * r)/ (p + r)
    
#     return tp, fp, fn, p, r, f1

# Closing

In [61]:
results = pd.DataFrame()
results = pd.DataFrame(columns=['regulatory'
                                , 'ccg_s_p_1'
                                , 'ccg_s_r_1'
                                , 'ccg_s_f1_1'
                                , 'ccg_s_p_2'
                                , 'ccg_s_r_2'
                                , 'ccg_s_f1_2'
                                , 'ccl_s_p_1'
                                , 'ccl_s_r_1'
                                , 'ccl_s_f1_1'
                                , 'ccl_s_p_2'
                                , 'ccl_s_r_2'
                                , 'ccl_s_f1_2'
                                , 'ccp_s_p_1'
                                , 'ccp_s_r_1'
                                , 'ccp_s_f1_1'
                                , 'ccp_s_p_2'
                                , 'ccp_s_r_2'
                                , 'ccp_s_f1_2'
                                , 'ccg_i_p_1'
                                , 'ccg_i_r_1'
                                , 'ccg_i_f1_1'
                                , 'ccg_i_p_2'
                                , 'ccg_i_r_2'
                                , 'ccg_i_f1_2'
                                , 'ccl_i_p_1'
                                , 'ccl_i_r_1'
                                , 'ccl_i_f1_1'
                                , 'ccl_i_p_2'
                                , 'ccl_i_r_2'
                                , 'ccl_i_f1_2'
                                , 'ccp_i_p_1'
                                , 'ccp_i_r_1'
                                , 'ccp_i_f1_1'
                                , 'ccp_i_p_2'
                                , 'ccp_i_r_2'
                                , 'ccp_i_f1_2'
                               ])

In [62]:
def test_1(name, df, dataset, shot, results, part):
    print('tes')
    
    cnt = 0
    tp_s = 0
    fp_s = 0
    fn_s = 0
    tp_i = 0
    fp_i = 0
    fn_i = 0
    
    for i in range(len(df)):
        reg = df.at[i, 'regulatory']
        ttl_pred = df.at[i, f'ttl_{shot}']
        ttl_test = prefix + dataset[i]['triples']
        
        tp, fp, fn, p, r, f1 = evaluate_ttl(ttl_pred, ttl_test)
        tp_s += tp
        fp_s += fp
        fn_s += fn
        
        results.at[i, 'regulatory'] = reg
        results.at[i, f'{name}_s_p_{shot}'] = p
        results.at[i, f'{name}_s_r_{shot}'] = r
        results.at[i, f'{name}_s_f1_{shot}'] = f1
        
        print(cnt, reg)
        print(f'Case Sensitive   : P: {p} || R: {r} || F1: {f1}')     
        
        tp, fp, fn, p, r, f1 = evaluate_ttl_case_insensitive(ttl_pred, ttl_test)
        tp_i += tp
        fp_i += fp
        fn_i += fn
        
        results.at[i, 'regulatory'] = reg
        results.at[i, f'{name}_i_p_{shot}'] = p
        results.at[i, f'{name}_i_r_{shot}'] = r
        results.at[i, f'{name}_i_f1_{shot}'] = f1
        
        print(f'Case Insensitive : P: {p} || R: {r} || F1: {f1}') 
        
        cnt += 1
        
        if cnt % 100 == 0:
            results.to_csv(f'results/{part}_metrics_code.csv')
            
    results.to_csv(f'results/{part}_metrics_code.csv')
        
    p_s = round(tp_s / (tp_s + fp_s), 3)
    r_s = round(tp_s / (tp_s + fn_s), 3)
    f1_s = round((2 * p_s * r_s)/ (p_s + r_s), 3)
    
    p_i = round(tp_i / (tp_i + fp_i), 3)
    r_i = round(tp_i / (tp_i + fn_i), 3)
    f1_i = round((2 * p_i * r_i)/ (p_i + r_i), 3)
    
    print()
    print('####################################################')
    print()
    print(f'{name} {shot} Shot')

    print()
    print('Case Sensitive')
    print(f'Precision: {p_s}')    
    print(f'Recall: {r_s}')              
    print(f'F1 Score: {f1_s}') 
    
    print()
    print('Case Insensitive')
    print(f'Precision: {p_i}')    
    print(f'Recall: {r_i}')              
    print(f'F1 Score: {f1_i}') 

In [63]:
test_closing_name = "dataset-surface-info/new-closing/new-closing-1"
test_closing = load_from_disk(test_closing_name)

In [64]:
cc_gemma = pd.read_csv('results/new/CC_gemma_post.csv')
cc_llama = pd.read_csv('results/new/CC_llama_post.csv')
cc_phi = pd.read_csv('results/new/CC_phi_post.csv')

In [65]:
test_1('ccg', cc_gemma, test_closing, '1', results, 'cc')

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: 'diundangkan'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", lin

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.526 || R: 0.625 || F1: 0.571
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
1 Permen_KP_2013_5
Case Sensitive   : P: 0.526 || R: 0.769 || F1: 0.625
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.263 || R: 0.556 || F1: 0.357
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
3 Permen_Par_2015_14
Case Sensitive   : P: 0.684 || R: 1.0 || F1: 0.812
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
4 Perpres_2019_67
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.05 || R: 0.077 || F1: 0.061
Case Insensitive : P: 0.05 || R: 0.077 || F1: 0.061
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.789 || R: 0.789 || F1: 0.789
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.526 || R: 0.526 || F1: 0.526
Case Insensitive : P: 0.5

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: 'Cukup jelas'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", lin

57 Permen_Dikbud_2013_46
Case Sensitive   : P: 0.632 || R: 1.0 || F1: 0.775
Case Insensitive : P: 0.632 || R: 1.0 || F1: 0.775
58 Permen_Keu_2015_201
Case Sensitive   : P: 0.474 || R: 0.5 || F1: 0.487
Case Insensitive : P: 0.474 || R: 0.5 || F1: 0.487
59 Permen_Hub_2012_36
Case Sensitive   : P: 0.632 || R: 0.923 || F1: 0.75
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
60 Permen_Hut_2009_32
Case Sensitive   : P: 0.474 || R: 0.9 || F1: 0.621
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
61 Peraturan_KPU_2018_11
Case Sensitive   : P: 0.526 || R: 0.625 || F1: 0.571
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
62 Permen_Tan_2017_49
Case Sensitive   : P: 0.368 || R: 0.438 || F1: 0.4
Case Insensitive : P: 0.368 || R: 0.438 || F1: 0.4
63 Perkot_Sorong_2013_32
Case Sensitive   : P: 0.458 || R: 0.647 || F1: 0.536
Case Insensitive : P: 0.458 || R: 0.647 || F1: 0.536
64 Perkot_Bogor_2006_11
Case Sensitive   : P: 0.368 || R: 0.7 || F1: 0.482
Case Insensitive : P: 0.368 || R: 0.7

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: '8 April 1999'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", li

...

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: 'Cukup jelas'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", lin

2462 Perkab_Bulungan_2009_2
Case Sensitive   : P: 0.625 || R: 1.0 || F1: 0.769
Case Insensitive : P: 0.625 || R: 1.0 || F1: 0.769
2463 Permen_PUPR_2015_10
Case Sensitive   : P: 0.526 || R: 0.526 || F1: 0.526
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
2464 Perpres_2015_161
Case Sensitive   : P: 0.421 || R: 0.667 || F1: 0.516
Case Insensitive : P: 0.421 || R: 0.667 || F1: 0.516
2465 Peraturan_Bawaslu_2012_7
Case Sensitive   : P: 0.526 || R: 1.0 || F1: 0.689
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
2466 Permen_ESDM_2016_02
Case Sensitive   : P: 0.632 || R: 0.632 || F1: 0.632
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
2467 Perkot_Binjai_2001_5
Case Sensitive   : P: 0.077 || R: 1.0 || F1: 0.143
Case Insensitive : P: 0.077 || R: 1.0 || F1: 0.143
2468 Permenko_Polhukam_2016_4
Case Sensitive   : P: 0.5 || R: 0.562 || F1: 0.529
Case Insensitive : P: 0.5 || R: 0.562 || F1: 0.529
2469 UU_1998_13
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P:

2532 Perkab_Tanggamus_2012_01
Case Sensitive   : P: 0.5 || R: 0.769 || F1: 0.606
Case Insensitive : P: 0.5 || R: 0.769 || F1: 0.606
2533 Permen_Dag_2015_104
Case Sensitive   : P: 0.579 || R: 0.688 || F1: 0.629
Case Insensitive : P: 0.579 || R: 0.688 || F1: 0.629
2534 Peraturan_BNP2TKI_2017_06
Case Sensitive   : P: 0.684 || R: 1.0 || F1: 0.812
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2535 Permen_Dagri_2013_18
Case Sensitive   : P: 0.263 || R: 0.833 || F1: 0.4
Case Insensitive : P: 0.263 || R: 0.833 || F1: 0.4
2536 Permen_Tan_2013_50
Case Sensitive   : P: 0.632 || R: 1.0 || F1: 0.775
Case Insensitive : P: 0.632 || R: 1.0 || F1: 0.775
2537 Perprov_Jabar_2002_7
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2538 Peraturan_OJK_2016_13
Case Sensitive   : P: 0.789 || R: 0.789 || F1: 0.789
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
2539 PP_1961_127
Case Sensitive   : P: 0.263 || R: 0.833 || F1: 0.4
Case Insensitive : P: 0.263 || R:

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: 'GUBERNUR RIAU'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", l

2582 Peraturan_Polri_2008_8
Case Sensitive   : P: 0.444 || R: 0.889 || F1: 0.592
Case Insensitive : P: 0.444 || R: 0.889 || F1: 0.592
2583 Permen_KP_2019_4
Case Sensitive   : P: 0.6 || R: 0.632 || F1: 0.616
Case Insensitive : P: 0.65 || R: 0.684 || F1: 0.667
2584 Permen_Hut_2009_33
Case Sensitive   : P: 0.421 || R: 0.8 || F1: 0.552
Case Insensitive : P: 0.421 || R: 0.8 || F1: 0.552
2585 Perprov_Riau_2013_7
Case Sensitive   : P: 0.059 || R: 1.0 || F1: 0.111
Case Insensitive : P: 0.059 || R: 1.0 || F1: 0.111
2586 Permen_Dagri_2018_59
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
2587 Perpres_2015_149
Case Sensitive   : P: 0.474 || R: 0.692 || F1: 0.563
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
2588 PP_2006_10
Case Sensitive   : P: 0.75 || R: 0.938 || F1: 0.834
Case Insensitive : P: 0.75 || R: 0.938 || F1: 0.834
2589 Perkot_Sorong_2013_12
Case Sensitive   : P: 0.44 || R: 1.0 || F1: 0.611
Case Insensitive : P: 0.44 || R

In [66]:
test_1('ccg', cc_gemma, test_closing, '2', results, 'cc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.474 || R: 0.562 || F1: 0.514
Case Insensitive : P: 0.474 || R: 0.562 || F1: 0.514
1 Permen_KP_2013_5
Case Sensitive   : P: 0.526 || R: 0.769 || F1: 0.625
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.263 || R: 0.556 || F1: 0.357
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
3 Permen_Par_2015_14
Case Sensitive   : P: 0.632 || R: 0.923 || F1: 0.75
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
4 Perpres_2019_67
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.263 || R: 0.385 || F1: 0.313
Case Insensitive : P: 0.263 || R: 0.385 || F1: 0.313
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.789 || R: 0.789 || F1: 0.789
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.474 || R: 0.474 || F1: 0.474
Case Insensitive : P:

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueError: day is out of range for month
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueE

28 Perkot_Denpasar_2006_1
Case Sensitive   : P: 0.737 || R: 0.778 || F1: 0.757
Case Insensitive : P: 0.737 || R: 0.778 || F1: 0.757
29 Perkot_Cirebon_2007_4
Case Sensitive   : P: 0.667 || R: 0.769 || F1: 0.714
Case Insensitive : P: 0.667 || R: 0.769 || F1: 0.714
30 Permen_Hut_2008_68
Case Sensitive   : P: 0.579 || R: 0.917 || F1: 0.71
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
31 Perkab_Sukabumi_2012_21
Case Sensitive   : P: 0.526 || R: 1.0 || F1: 0.689
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
32 Perpres_2015_156
Case Sensitive   : P: 0.421 || R: 0.667 || F1: 0.516
Case Insensitive : P: 0.421 || R: 0.667 || F1: 0.516
33 Permen_Hub_2019_11
Case Sensitive   : P: 0.105 || R: 0.333 || F1: 0.16
Case Insensitive : P: 0.105 || R: 0.333 || F1: 0.16
34 PP_1978_31
Case Sensitive   : P: 0.316 || R: 0.5 || F1: 0.387
Case Insensitive : P: 0.316 || R: 0.5 || F1: 0.387
35 Permen_KP_2018_40
Case Sensitive   : P: 0.421 || R: 0.421 || F1: 0.421
Case Insensitive : P: 0.474 || R: 0.474 

98 Permen_Dagri_2018_92
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
99 Permen_Desa_2017_23
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
100 PP_2013_55
Case Sensitive   : P: 0.632 || R: 1.0 || F1: 0.775
Case Insensitive : P: 0.632 || R: 1.0 || F1: 0.775
101 Permen_LHK_2019_21
Case Sensitive   : P: 0.632 || R: 0.923 || F1: 0.75
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
102 Perpres_2018_45
Case Sensitive   : P: 0.789 || R: 0.833 || F1: 0.81
Case Insensitive : P: 0.789 || R: 0.833 || F1: 0.81
103 UU_2008_9
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
104 UU_1954_63
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
105 Permen_Tan_2014_36
Case Sensitive   : P: 0.474 || R: 0.9 || F1: 0.621
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
106 Permen_Keu_2017

179 PP_1961_79
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
180 Peraturan_BNP2TKI_2017_11
Case Sensitive   : P: 0.632 || R: 0.632 || F1: 0.632
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
181 Permen_Tan_2010_45
Case Sensitive   : P: 0.632 || R: 0.923 || F1: 0.75
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
182 Permen_Dikbud_2013_87
Case Sensitive   : P: 0.632 || R: 0.923 || F1: 0.75
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
183 Permen_Perin_2015_48
Case Sensitive   : P: 0.632 || R: 0.923 || F1: 0.75
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
184 Perprov_Sulteng_2002_06
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
185 PP_1990_46
Case Sensitive   : P: 0.316 || R: 1.0 || F1: 0.48
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
186 Permen_Ristekdikti_2016_57
Case Sensitive   : P: 0.474 || R: 0.692 || F1: 0.563
Case Insensitive : P: 0.474 || R: 0.692 || F

...

2340 Perkab_Karawang_2014_5
Case Sensitive   : P: 0.526 || R: 0.625 || F1: 0.571
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
2341 PP_2016_30
Case Sensitive   : P: 0.316 || R: 0.667 || F1: 0.429
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
2342 Permen_Ristekdikti_2017_67
Case Sensitive   : P: 0.474 || R: 0.562 || F1: 0.514
Case Insensitive : P: 0.474 || R: 0.562 || F1: 0.514
2343 Perkab_Mamuju_Utara_2006_14
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2344 Permen_Keu_2015_221
Case Sensitive   : P: 0.111 || R: 0.167 || F1: 0.133
Case Insensitive : P: 0.111 || R: 0.167 || F1: 0.133
2345 Permen_Keu_2019_119
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
2346 Permen_Tan_2017_12
Case Sensitive   : P: 0.632 || R: 0.632 || F1: 0.632
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
2347 PP_1961_132
Case Sensitive   : P: 0.316 || R: 0.667 || F1: 0.429
Case Insens

2434 Permen_PPPA_2011_4
Case Sensitive   : P: 0.421 || R: 0.8 || F1: 0.552
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
2435 Perkot_Malang_2007_4
Case Sensitive   : P: 0.737 || R: 0.737 || F1: 0.737
Case Insensitive : P: 0.737 || R: 0.737 || F1: 0.737
2436 Permen_Han_2015_35
Case Sensitive   : P: 0.632 || R: 0.632 || F1: 0.632
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
2437 Perkot_Bandung_2000_04
Case Sensitive   : P: 0.059 || R: 1.0 || F1: 0.111
Case Insensitive : P: 0.059 || R: 1.0 || F1: 0.111
2438 Permen_PR_2012_39
Case Sensitive   : P: 0.632 || R: 0.923 || F1: 0.75
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2439 Perpres_2014_75
Case Sensitive   : P: 0.474 || R: 1.0 || F1: 0.643
Case Insensitive : P: 0.474 || R: 1.0 || F1: 0.643
2440 Perpres_2017_28
Case Sensitive   : P: 0.421 || R: 0.667 || F1: 0.516
Case Insensitive : P: 0.421 || R: 0.667 || F1: 0.516
2441 Permen_Han_2014_64
Case Sensitive   : P: 0.474 || R: 0.9 || F1: 0.621
Case Insensitive : P: 0.474 ||

2515 Permen_Keu_2010_219
Case Sensitive   : P: 0.579 || R: 0.917 || F1: 0.71
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
2516 Permen_Tan_2015_59
Case Sensitive   : P: 0.632 || R: 0.632 || F1: 0.632
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
2517 Permen_ESDM_2016_16
Case Sensitive   : P: 0.579 || R: 0.579 || F1: 0.579
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
2518 Perkot_Mataram_2009_3
Case Sensitive   : P: 0.737 || R: 0.875 || F1: 0.8
Case Insensitive : P: 0.737 || R: 0.875 || F1: 0.8
2519 Perkot_Tasikmalaya_2008_9
Case Sensitive   : P: 0.579 || R: 0.688 || F1: 0.629
Case Insensitive : P: 0.579 || R: 0.688 || F1: 0.629
2520 Permen_Keu_2016_231
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
2521 Peraturan_BMKG_2015_23
Case Sensitive   : P: 0.316 || R: 0.375 || F1: 0.343
Case Insensitive : P: 0.316 || R: 0.375 || F1: 0.343
2522 Permen_Keu_2018_34
Case Sensitive   : P: 0.263 || R: 0.556 || F1: 0.357
Case

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: 'GUBERNUR RIAU'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", l

2576 Perkab_Musi_Rawas_2013_10
Case Sensitive   : P: 0.526 || R: 1.0 || F1: 0.689
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
2577 Permen_Perin_2017_07
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
2578 Permen_Desa_2016_25
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
2579 Permen_Keu_2014_58
Case Sensitive   : P: 0.421 || R: 0.889 || F1: 0.571
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
2580 PP_1990_24
Case Sensitive   : P: 0.158 || R: 1.0 || F1: 0.273
Case Insensitive : P: 0.158 || R: 1.0 || F1: 0.273
2581 Permen_Dag_2015_76
Case Sensitive   : P: 0.526 || R: 0.588 || F1: 0.555
Case Insensitive : P: 0.526 || R: 0.588 || F1: 0.555
2582 Peraturan_Polri_2008_8
Case Sensitive   : P: 0.421 || R: 0.889 || F1: 0.571
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
2583 Permen_KP_2019_4
Case Sensitive   : P: 0.4 || R: 0.421 || F1: 0.41
Case Insensitive : P: 0.

In [67]:
test_1('ccl', cc_llama, test_closing, '1', results, 'cc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.526 || R: 0.625 || F1: 0.571
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
1 Permen_KP_2013_5
Case Sensitive   : P: 0.684 || R: 1.0 || F1: 0.812
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.316 || R: 0.667 || F1: 0.429
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
3 Permen_Par_2015_14
Case Sensitive   : P: 0.316 || R: 0.462 || F1: 0.375
Case Insensitive : P: 0.316 || R: 0.462 || F1: 0.375
4 Perpres_2019_67
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.053 || R: 0.077 || F1: 0.063
Case Insensitive : P: 0.053 || R: 0.077 || F1: 0.063
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.789 || R: 0.789 || F1: 0.789
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.526 || R: 0.526 || F1: 0.526
Case Insensitive : P: 

67 Permen_Dikbud_2012_7
Case Sensitive   : P: 0.579 || R: 1.0 || F1: 0.733
Case Insensitive : P: 0.579 || R: 1.0 || F1: 0.733
68 Perpres_2013_103
Case Sensitive   : P: 0.421 || R: 0.889 || F1: 0.571
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
69 PP_2018_49
Case Sensitive   : P: 0.474 || R: 0.75 || F1: 0.581
Case Insensitive : P: 0.474 || R: 0.75 || F1: 0.581
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.5 || R: 1.0 || F1: 0.667
Case Insensitive : P: 0.5 || R: 1.0 || F1: 0.667
73 Perpres_2008_41
Case Sensitive   : P: 0.579 || R: 0.917 || F1: 0.71
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
74 Permen_PR_2009_03
Case Sensitive   : P: 0.368 || R: 1.0 || F1: 0.538
Case Insensitive : P: 0.368 || R: 1.0 || F1: 0.538
75 Pera

140 Permen_Keu_2015_108
Case Sensitive   : P: 0.579 || R: 0.917 || F1: 0.71
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
141 Permen_LHK_2019_13
Case Sensitive   : P: 0.474 || R: 0.474 || F1: 0.474
Case Insensitive : P: 0.474 || R: 0.474 || F1: 0.474
142 PP_1983_17
Case Sensitive   : P: 0.474 || R: 0.9 || F1: 0.621
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
143 Perpres_2015_82
Case Sensitive   : P: 0.684 || R: 1.0 || F1: 0.812
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
144 Permen_Naker_2016_17
Case Sensitive   : P: 0.368 || R: 0.368 || F1: 0.368
Case Insensitive : P: 0.368 || R: 0.368 || F1: 0.368
145 Permen_Hub_2015_114
Case Sensitive   : P: 0.316 || R: 1.0 || F1: 0.48
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
146 Perkab_Banyuwangi_2010_8
Case Sensitive   : P: 0.368 || R: 0.467 || F1: 0.412
Case Insensitive : P: 0.368 || R: 0.467 || F1: 0.412
147 PP_1985_33
Case Sensitive   : P: 0.316 || R: 0.5 || F1: 0.387
Case Insensitive : P: 0.316 || R: 0.5 || F1: 0.3

219 PP_1980_40
Case Sensitive   : P: 0.053 || R: 0.1 || F1: 0.069
Case Insensitive : P: 0.053 || R: 0.1 || F1: 0.069
220 PP_1984_27
Case Sensitive   : P: 0.263 || R: 0.625 || F1: 0.37
Case Insensitive : P: 0.263 || R: 0.625 || F1: 0.37
221 PP_1981_7
Case Sensitive   : P: 0.526 || R: 0.526 || F1: 0.526
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
222 Permen_Keu_2013_218
Case Sensitive   : P: 0.632 || R: 1.0 || F1: 0.775
Case Insensitive : P: 0.632 || R: 1.0 || F1: 0.775
223 Perkab_Garut_2008_2
Case Sensitive   : P: 0.067 || R: 1.0 || F1: 0.126
Case Insensitive : P: 0.067 || R: 1.0 || F1: 0.126
224 Permen_Humham_2012_26
Case Sensitive   : P: 0.733 || R: 1.0 || F1: 0.846
Case Insensitive : P: 0.733 || R: 1.0 || F1: 0.846
225 Perpres_2015_22
Case Sensitive   : P: 0.474 || R: 1.0 || F1: 0.643
Case Insensitive : P: 0.474 || R: 1.0 || F1: 0.643
226 Permen_Hub_2012_68
Case Sensitive   : P: 0.526 || R: 0.769 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
227 Perkab_Pu

300 Perprov_Jabar_2001_19
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
301 Perprov_Banten_2010_8
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
302 Permen_Kes_2013_89
Case Sensitive   : P: 0.421 || R: 0.615 || F1: 0.5
Case Insensitive : P: 0.421 || R: 0.615 || F1: 0.5
303 Permen_Keu_2014_47
Case Sensitive   : P: 0.474 || R: 1.0 || F1: 0.643
Case Insensitive : P: 0.474 || R: 1.0 || F1: 0.643
304 Permen_Keu_2009_86
Case Sensitive   : P: 0.474 || R: 1.0 || F1: 0.643
Case Insensitive : P: 0.474 || R: 1.0 || F1: 0.643
305 Permen_Keu_2016_33
Case Sensitive   : P: 0.474 || R: 0.6 || F1: 0.53
Case Insensitive : P: 0.474 || R: 0.6 || F1: 0.53
306 Peraturan_MA_2016_13
Case Sensitive   : P: 0.526 || R: 0.625 || F1: 0.571
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
307 UU_1971_11
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
308 Permen_ATRBPN_2018

...

2314 Permen_KP_2018_45
Case Sensitive   : P: 0.526 || R: 0.526 || F1: 0.526
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
2315 Peraturan_LIPI_2016_4
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.474 || R: 0.6 || F1: 0.53
2316 Permen_Parekraf_2012_144
Case Sensitive   : P: 0.684 || R: 1.0 || F1: 0.812
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2317 Perkab_Indragiri_Hilir_2010_21
Case Sensitive   : P: 0.211 || R: 0.333 || F1: 0.258
Case Insensitive : P: 0.211 || R: 0.333 || F1: 0.258
2318 Perpres_2019_38
Case Sensitive   : P: 0.632 || R: 0.8 || F1: 0.706
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
2319 Perkab_Ogan_Komering_Ilir_2010_29
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2320 Perprov_Riau_2013_15
Case Sensitive   : P: 0.053 || R: 0.143 || F1: 0.077
Case Insensitive : P: 0.053 || R: 0.143 || F1: 0.077
2321 Permen_Han_2014_19
Case Sensitive   : P: 0.526 || R: 0.769 || F1: 0.625
Case In

2400 Permen_ESDM_2013_19
Case Sensitive   : P: 0.368 || R: 0.538 || F1: 0.437
Case Insensitive : P: 0.368 || R: 0.538 || F1: 0.437
2401 Peraturan_LKPP_2019_14
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
2402 Permen_Hub_2017_87
Case Sensitive   : P: 0.316 || R: 0.4 || F1: 0.353
Case Insensitive : P: 0.316 || R: 0.4 || F1: 0.353
2403 Peraturan_Batan_2016_4
Case Sensitive   : P: 0.684 || R: 1.0 || F1: 0.812
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2404 PP_1957_13
Case Sensitive   : P: 0.158 || R: 0.5 || F1: 0.24
Case Insensitive : P: 0.158 || R: 0.5 || F1: 0.24
2405 Peraturan_BPJSTK_2018_1
Case Sensitive   : P: 0 || R: 0.0 || F1: 0
Case Insensitive : P: 0 || R: 0.0 || F1: 0
2406 Peraturan_LIPI_2017_1
Case Sensitive   : P: 0.474 || R: 0.6 || F1: 0.53
Case Insensitive : P: 0.474 || R: 0.6 || F1: 0.53
2407 Permen_Keu_2010_19
Case Sensitive   : P: 0.474 || R: 0.75 || F1: 0.581
Case Insensitive : P: 0.474 || R: 0.75 || F1:

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueError: day is out of range for month
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueE

2571 Peraturan_Basarnas_2016_2
Case Sensitive   : P: 0.474 || R: 0.474 || F1: 0.474
Case Insensitive : P: 0.474 || R: 0.474 || F1: 0.474
2572 Peraturan_Bapeten_2011_7
Case Sensitive   : P: 0.368 || R: 0.7 || F1: 0.482
Case Insensitive : P: 0.421 || R: 0.8 || F1: 0.552
2573 Perpres_2019_2
Case Sensitive   : P: 0.632 || R: 0.8 || F1: 0.706
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
2574 Perkab_Poso_2010_9
Case Sensitive   : P: 0.8 || R: 0.923 || F1: 0.857
Case Insensitive : P: 0.8 || R: 0.923 || F1: 0.857
2575 UU_2007_5
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2576 Perkab_Musi_Rawas_2013_10
Case Sensitive   : P: 0.474 || R: 0.9 || F1: 0.621
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
2577 Permen_Perin_2017_07
Case Sensitive   : P: 0.316 || R: 0.4 || F1: 0.353
Case Insensitive : P: 0.316 || R: 0.4 || F1: 0.353
2578 Permen_Desa_2016_25
Case Sensitive   : P: 0.474 || R: 0.6 || F1: 0.53
Case Insensitive : P: 0.474 ||


####################################################

ccl 1 Shot

Case Sensitive
Precision: 0.439
Recall: 0.68
F1 Score: 0.534

Case Insensitive
Precision: 0.44
Recall: 0.682
F1 Score: 0.535


In [69]:
test_1('ccl', cc_llama, test_closing, '2', results, 'cc')

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueError: day is out of range for month
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueE

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.684 || R: 0.812 || F1: 0.743
Case Insensitive : P: 0.684 || R: 0.812 || F1: 0.743
1 Permen_KP_2013_5
Case Sensitive   : P: 0.316 || R: 0.462 || F1: 0.375
Case Insensitive : P: 0.316 || R: 0.462 || F1: 0.375
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.158 || R: 0.333 || F1: 0.214
Case Insensitive : P: 0.158 || R: 0.333 || F1: 0.214
3 Permen_Par_2015_14
Case Sensitive   : P: 0.474 || R: 0.692 || F1: 0.563
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
4 Perpres_2019_67
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.263 || R: 0.385 || F1: 0.313
Case Insensitive : P: 0.263 || R: 0.385 || F1: 0.313
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.667 || R: 0.737 || F1: 0.7
Case Insensitive : P: 0.667 || R: 0.737 || F1: 0.7
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.526 || R: 0.526 || F1: 0.526
Case Insensitive : P: 

94 UU_2007_38
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
95 Permen_PANRB_2017_25
Case Sensitive   : P: 0.579 || R: 0.611 || F1: 0.595
Case Insensitive : P: 0.579 || R: 0.611 || F1: 0.595
96 Permen_Keu_2015_232
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
97 Permen_Dag_2017_82
Case Sensitive   : P: 0.474 || R: 0.6 || F1: 0.53
Case Insensitive : P: 0.474 || R: 0.6 || F1: 0.53
98 Permen_Dagri_2018_92
Case Sensitive   : P: 0.263 || R: 0.333 || F1: 0.294
Case Insensitive : P: 0.263 || R: 0.333 || F1: 0.294
99 Permen_Desa_2017_23
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
100 PP_2013_55
Case Sensitive   : P: 0.632 || R: 1.0 || F1: 0.775
Case Insensitive : P: 0.632 || R: 1.0 || F1: 0.775
101 Permen_LHK_2019_21
Case Sensitive   : P: 0.421 || R: 0.615 || F1: 0.5
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
10

200 Permen_Keu_2009_234
Case Sensitive   : P: 0.316 || R: 1.0 || F1: 0.48
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
201 PP_2009_78
Case Sensitive   : P: 0.421 || R: 0.889 || F1: 0.571
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
202 Peraturan_BPOM_2019_30
Case Sensitive   : P: 0.579 || R: 0.579 || F1: 0.579
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
203 Permen_Pora_2019_3
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
204 Perprov_Papua_2013_14
Case Sensitive   : P: 0.474 || R: 0.692 || F1: 0.563
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
205 Permen_PANRB_2013_32
Case Sensitive   : P: 0.474 || R: 0.692 || F1: 0.563
Case Insensitive : P: 0.579 || R: 0.846 || F1: 0.687
206 Permen_Dagri_2017_3
Case Sensitive   : P: 0.263 || R: 0.333 || F1: 0.294
Case Insensitive : P: 0.263 || R: 0.333 || F1: 0.294
207 UU_2012_8
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueError: day is out of range for month
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueE

...

Case Insensitive : P: 0.421 || R: 0.615 || F1: 0.5
2471 Permen_KP_2016_30
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
2472 Permen_Sos_2016_4
Case Sensitive   : P: 0.789 || R: 0.833 || F1: 0.81
Case Insensitive : P: 0.789 || R: 0.833 || F1: 0.81
2473 Permen_Keu_2010_64
Case Sensitive   : P: 0.474 || R: 0.75 || F1: 0.581
Case Insensitive : P: 0.474 || R: 0.75 || F1: 0.581
2474 Perpres_2018_107
Case Sensitive   : P: 0.474 || R: 0.692 || F1: 0.563
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
2475 Peraturan_BKKBN_2016_481
Case Sensitive   : P: 0.632 || R: 0.632 || F1: 0.632
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
2476 Peraturan_KY_2015_2
Case Sensitive   : P: 0.579 || R: 0.688 || F1: 0.629
Case Insensitive : P: 0.579 || R: 0.688 || F1: 0.629
2477 Perpres_2016_46
Case Sensitive   : P: 0.632 || R: 0.8 || F1: 0.706
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
2478 Peraturan_BKN_2012_9
Case Sensitive   : P:

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueError: day is out of range for month
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueE

2567 UU_1957_49
Case Sensitive   : P: 0.04 || R: 1.0 || F1: 0.077
Case Insensitive : P: 0.04 || R: 1.0 || F1: 0.077
2568 Permen_Dagri_2011_41
Case Sensitive   : P: 0.474 || R: 1.0 || F1: 0.643
Case Insensitive : P: 0.474 || R: 1.0 || F1: 0.643
2569 Permen_Agama_2016_2
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
2570 Permenko_Kesra_2014_9
Case Sensitive   : P: 0.421 || R: 0.615 || F1: 0.5
Case Insensitive : P: 0.421 || R: 0.615 || F1: 0.5
2571 Peraturan_Basarnas_2016_2
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.737 || R: 0.737 || F1: 0.737
2572 Peraturan_Bapeten_2011_7
Case Sensitive   : P: 0.316 || R: 0.6 || F1: 0.414
Case Insensitive : P: 0.316 || R: 0.6 || F1: 0.414
2573 Perpres_2019_2
Case Sensitive   : P: 0.632 || R: 0.8 || F1: 0.706
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
2574 Perkab_Poso_2010_9
Case Sensitive   : P: 0.867 || R: 1.0 || F1: 0.929
Case Insensitive : P: 0.867 ||

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueError: day is out of range for month
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 201, in parse_date
    return date(sign * int(groups['year']),
ValueE

2597 Perkab_Bantul_2008_15
Case Sensitive   : P: 0.316 || R: 0.6 || F1: 0.414
Case Insensitive : P: 0.316 || R: 0.6 || F1: 0.414
2598 Permen_Desa_2018_6
Case Sensitive   : P: 0.526 || R: 0.625 || F1: 0.571
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
2599 Permen_Hut_2010_41
Case Sensitive   : P: 0.316 || R: 0.667 || F1: 0.429
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
2600 PP_2015_69
Case Sensitive   : P: 0.111 || R: 0.333 || F1: 0.167
Case Insensitive : P: 0.111 || R: 0.333 || F1: 0.167
2601 Permen_LH_2012_20
Case Sensitive   : P: 0.526 || R: 0.769 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
2602 UU_1954_76
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2603 Perkab_Magelang_2010_12
Case Sensitive   : P: 0.316 || R: 0.6 || F1: 0.414
Case Insensitive : P: 0.316 || R: 0.6 || F1: 0.414
2604 Perpres_2016_68
Case Sensitive   : P: 0.316 || R: 0.667 || F1: 0.429
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.

In [70]:
test_1('ccp', cc_phi, test_closing, '1', results, 'cc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.526 || R: 0.625 || F1: 0.571
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
1 Permen_KP_2013_5
Case Sensitive   : P: 0.333 || R: 0.462 || F1: 0.387
Case Insensitive : P: 0.333 || R: 0.462 || F1: 0.387
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.158 || R: 0.333 || F1: 0.214
Case Insensitive : P: 0.158 || R: 0.333 || F1: 0.214
3 Permen_Par_2015_14
Case Sensitive   : P: 0.474 || R: 0.692 || F1: 0.563
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
4 Perpres_2019_67
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.8 || R: 0.421 || F1: 0.552
Case Insensitive : P: 0.8 || R: 0.421 || F1: 0.552
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.733 || R: 0.579 || F1: 0.647
Case Insensitive : P: 0.733 || R: 0.57

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: 'TBD'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, i

28 Perkot_Denpasar_2006_1
Case Sensitive   : P: 0.222 || R: 0.222 || F1: 0.222
Case Insensitive : P: 0.222 || R: 0.222 || F1: 0.222
29 Perkot_Cirebon_2007_4
Case Sensitive   : P: 0.7 || R: 0.538 || F1: 0.608
Case Insensitive : P: 0.7 || R: 0.538 || F1: 0.608
30 Permen_Hut_2008_68
Case Sensitive   : P: 0.444 || R: 0.667 || F1: 0.533
Case Insensitive : P: 0.444 || R: 0.667 || F1: 0.533
31 Perkab_Sukabumi_2012_21
Case Sensitive   : P: 0.526 || R: 1.0 || F1: 0.689
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
32 Perpres_2015_156
Case Sensitive   : P: 0.421 || R: 0.667 || F1: 0.516
Case Insensitive : P: 0.421 || R: 0.667 || F1: 0.516
33 Permen_Hub_2019_11
Case Sensitive   : P: 0.222 || R: 0.667 || F1: 0.333
Case Insensitive : P: 0.222 || R: 0.667 || F1: 0.333
34 PP_1978_31
Case Sensitive   : P: 0.133 || R: 0.167 || F1: 0.148
Case Insensitive : P: 0.133 || R: 0.167 || F1: 0.148
35 Permen_KP_2018_40
Case Sensitive   : P: 0.684 || R: 0.684 || F1: 0.684
Case Insensitive : P: 0.684 || R: 0.

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: '9 Desember 2006'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py",

54 Perpres_2006_98
Case Sensitive   : P: 0.267 || R: 0.364 || F1: 0.308


...

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: ''
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in p

2400 Permen_ESDM_2013_19
Case Sensitive   : P: 0.556 || R: 0.769 || F1: 0.645
Case Insensitive : P: 0.667 || R: 0.923 || F1: 0.774
2401 Peraturan_LKPP_2019_14
Case Sensitive   : P: 0.812 || R: 0.684 || F1: 0.743
Case Insensitive : P: 0.812 || R: 0.684 || F1: 0.743
2402 Permen_Hub_2017_87
Case Sensitive   : P: 0.368 || R: 0.467 || F1: 0.412
Case Insensitive : P: 0.368 || R: 0.467 || F1: 0.412
2403 Peraturan_Batan_2016_4
Case Sensitive   : P: 0.6 || R: 0.462 || F1: 0.522
Case Insensitive : P: 0.6 || R: 0.462 || F1: 0.522
2404 PP_1957_13
Case Sensitive   : P: 0.077 || R: 0.167 || F1: 0.105
Case Insensitive : P: 0.077 || R: 0.167 || F1: 0.105
2405 Peraturan_BPJSTK_2018_1
Case Sensitive   : P: 0 || R: 0.0 || F1: 0
Case Insensitive : P: 0 || R: 0.0 || F1: 0
2406 Peraturan_LIPI_2017_1
Case Sensitive   : P: 0.4 || R: 0.267 || F1: 0.32
Case Insensitive : P: 0.4 || R: 0.267 || F1: 0.32
2407 Permen_Keu_2010_19
Case Sensitive   : P: 0.316 || R: 0.5 || F1: 0.387
Case Insensitive : P: 0.316 || R: 0.

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: 'Not Specified'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", l

Case Insensitive : P: 0.632 || R: 0.667 || F1: 0.649
2452 Permen_Perin_2012_102
Case Sensitive   : P: 0.278 || R: 0.556 || F1: 0.371
Case Insensitive : P: 0.278 || R: 0.556 || F1: 0.371
2453 Perkab_Bengkayang_2005_2
Case Sensitive   : P: 0.389 || R: 0.636 || F1: 0.483
Case Insensitive : P: 0.389 || R: 0.636 || F1: 0.483
2454 Perkab_Banyuwangi_2011_3
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2455 Permen_Ristekdikti_2019_7
Case Sensitive   : P: 0.526 || R: 0.625 || F1: 0.571
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
2456 Perkab_Bantul_2008_18
Case Sensitive   : P: 0.4 || R: 0.333 || F1: 0.363
Case Insensitive : P: 0.4 || R: 0.333 || F1: 0.363
2457 Perkot_Bekasi_2013_09
Case Sensitive   : P: 0.526 || R: 1.0 || F1: 0.689
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
2458 Permen_Hut_2012_42
Case Sensitive   : P: 0.538 || R: 0.538 || F1: 0.538
Case Insensitive : P: 0.538 || R: 0.538 || F1: 0.538
2459 Permen_Keu_2019_118
Case Sen

2600 PP_2015_69
Case Sensitive   : P: 0.278 || R: 0.833 || F1: 0.417
Case Insensitive : P: 0.278 || R: 0.833 || F1: 0.417
2601 Permen_LH_2012_20
Case Sensitive   : P: 0.368 || R: 0.538 || F1: 0.437
Case Insensitive : P: 0.368 || R: 0.538 || F1: 0.437
2602 UU_1954_76
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2603 Perkab_Magelang_2010_12
Case Sensitive   : P: 0.562 || R: 0.9 || F1: 0.692
Case Insensitive : P: 0.562 || R: 0.9 || F1: 0.692
2604 Perpres_2016_68
Case Sensitive   : P: 0.316 || R: 0.667 || F1: 0.429
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
2605 Permen_Agama_2015_41
Case Sensitive   : P: 0.333 || R: 0.462 || F1: 0.387
Case Insensitive : P: 0.333 || R: 0.462 || F1: 0.387
2606 Peraturan_BKN_2012_16
Case Sensitive   : P: 0.263 || R: 0.385 || F1: 0.313
Case Insensitive : P: 0.316 || R: 0.462 || F1: 0.375
2607 Permen_Kes_2016_56
Case Sensitive   : P: 0.5 || R: 0.562 || F1: 0.529
Case Insensitive : P: 0.5 || R: 0.562 || F1: 

In [71]:
test_1('ccp', cc_phi, test_closing, '2', results, 'cc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.474 || R: 0.562 || F1: 0.514
Case Insensitive : P: 0.474 || R: 0.562 || F1: 0.514
1 Permen_KP_2013_5
Case Sensitive   : P: 0.526 || R: 0.769 || F1: 0.625
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.158 || R: 0.333 || F1: 0.214
Case Insensitive : P: 0.158 || R: 0.333 || F1: 0.214
3 Permen_Par_2015_14
Case Sensitive   : P: 0.632 || R: 0.923 || F1: 0.75
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
4 Perpres_2019_67
Case Sensitive   : P: 0.842 || R: 0.842 || F1: 0.842
Case Insensitive : P: 0.842 || R: 0.842 || F1: 0.842
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.158 || R: 0.231 || F1: 0.188
Case Insensitive : P: 0.158 || R: 0.231 || F1: 0.188
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.789 || R: 0.789 || F1: 0.789
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.769 || R: 0.526 || F1: 0.625
Case Insensitive : P:

75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.375 || R: 0.5 || F1: 0.429
Case Insensitive : P: 0.375 || R: 0.5 || F1: 0.429
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.526 || R: 0.833 || F1: 0.645
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
77 Perkab_Sleman_2012_9
Case Sensitive   : P: 1.0 || R: 1.0 || F1: 1.0
Case Insensitive : P: 1.0 || R: 1.0 || F1: 1.0
78 PP_1990_59
Case Sensitive   : P: 0.278 || R: 0.833 || F1: 0.417
Case Insensitive : P: 0.278 || R: 0.833 || F1: 0.417
79 Permen_Agama_2016_21
Case Sensitive   : P: 0.789 || R: 0.789 || F1: 0.789
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
80 Permen_PANRB_2018_15
Case Sensitive   : P: 0.611 || R: 0.579 || F1: 0.595
Case Insensitive : P: 0.611 || R: 0.579 || F1: 0.595
81 Peraturan_ANRI_2018_8
Case Sensitive   : P: 0.667 || R: 0.75 || F1: 0.706
Case Insensitive : P: 0.667 || R: 0.75 || F1: 0.706
82 Permen_PANRB_2014_5
Case Sensitive   : P: 0.278 || R: 0.385 || F1: 0.323
Case Insensitive : P: 0.278 || R: 0.385 

200 Permen_Keu_2009_234
Case Sensitive   : P: 0.105 || R: 0.333 || F1: 0.16
Case Insensitive : P: 0.105 || R: 0.333 || F1: 0.16
201 PP_2009_78
Case Sensitive   : P: 0.263 || R: 0.556 || F1: 0.357
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
202 Peraturan_BPOM_2019_30
Case Sensitive   : P: 0.667 || R: 0.632 || F1: 0.649
Case Insensitive : P: 0.722 || R: 0.684 || F1: 0.702
203 Permen_Pora_2019_3
Case Sensitive   : P: 0.737 || R: 0.737 || F1: 0.737
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
204 Perprov_Papua_2013_14
Case Sensitive   : P: 0.474 || R: 0.692 || F1: 0.563
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
205 Permen_PANRB_2013_32
Case Sensitive   : P: 0.438 || R: 0.538 || F1: 0.483
Case Insensitive : P: 0.438 || R: 0.538 || F1: 0.483
206 Permen_Dagri_2017_3
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
207 UU_2012_8
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R:

300 Perprov_Jabar_2001_19
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
301 Perprov_Banten_2010_8
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
302 Permen_Kes_2013_89
Case Sensitive   : P: 0.278 || R: 0.385 || F1: 0.323
Case Insensitive : P: 0.278 || R: 0.385 || F1: 0.323
303 Permen_Keu_2014_47
Case Sensitive   : P: 0.375 || R: 0.667 || F1: 0.48
Case Insensitive : P: 0.375 || R: 0.667 || F1: 0.48
304 Permen_Keu_2009_86
Case Sensitive   : P: 0.263 || R: 0.556 || F1: 0.357
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
305 Permen_Keu_2016_33
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
306 Peraturan_MA_2016_13
Case Sensitive   : P: 0.632 || R: 0.75 || F1: 0.686
Case Insensitive : P: 0.632 || R: 0.75 || F1: 0.686
307 UU_1971_11
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
308 Permen

425 Permen_Dagri_2013_55
Case Sensitive   : P: 0.368 || R: 0.538 || F1: 0.437
Case Insensitive : P: 0.368 || R: 0.538 || F1: 0.437
426 Perpres_2019_27
Case Sensitive   : P: 0.842 || R: 0.842 || F1: 0.842
Case Insensitive : P: 0.842 || R: 0.842 || F1: 0.842
427 Permen_Dag_2016_08
Case Sensitive   : P: 0.632 || R: 0.632 || F1: 0.632
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
428 Permen_KP_2011_14
Case Sensitive   : P: 0.889 || R: 0.842 || F1: 0.865
Case Insensitive : P: 1.0 || R: 0.947 || F1: 0.973
429 Perkab_Sleman_2001_13
Case Sensitive   : P: 0.692 || R: 0.5 || F1: 0.581
Case Insensitive : P: 0.692 || R: 0.5 || F1: 0.581
430 Permen_Naker_2015_2
Case Sensitive   : P: 0.333 || R: 0.462 || F1: 0.387
Case Insensitive : P: 0.333 || R: 0.462 || F1: 0.387
431 Permen_Agama_2016_4
Case Sensitive   : P: 0.737 || R: 0.778 || F1: 0.757
Case Insensitive : P: 0.737 || R: 0.778 || F1: 0.757
432 Peraturan_OJK_2019_6
Case Sensitive   : P: 0.579 || R: 0.579 || F1: 0.579
Case Insensitive : P: 

...

2361 Permen_Keu_2013_44
Case Sensitive   : P: 0.25 || R: 0.3 || F1: 0.273
Case Insensitive : P: 0.25 || R: 0.3 || F1: 0.273
2362 Perkab_Mamuju_Utara_2006_18
Case Sensitive   : P: 0.1 || R: 1.0 || F1: 0.182
Case Insensitive : P: 0.1 || R: 1.0 || F1: 0.182
2363 Permen_Hut_2014_38
Case Sensitive   : P: 0.333 || R: 0.6 || F1: 0.428
Case Insensitive : P: 0.333 || R: 0.6 || F1: 0.428
2364 Peraturan_Baznas_2019_3
Case Sensitive   : P: 0.632 || R: 0.632 || F1: 0.632
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
2365 Permen_Ristekdikti_2016_109
Case Sensitive   : P: 0.474 || R: 0.562 || F1: 0.514
Case Insensitive : P: 0.474 || R: 0.562 || F1: 0.514
2366 UU_2013_20
Case Sensitive   : P: 0.053 || R: 1.0 || F1: 0.101
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2367 Permen_Hut_2011_50
Case Sensitive   : P: 0.333 || R: 0.462 || F1: 0.387
Case Insensitive : P: 0.333 || R: 0.462 || F1: 0.387
2368 Permen_Kominfo_2013_26
Case Sensitive   : P: 0.278 || R: 0.385 || F1: 0.323
Case Insensitive

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: 'Not Specified'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7f82f0281000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", l

2444 Perprov_Kep_Riau_2011_8
Case Sensitive   : P: 0.526 || R: 1.0 || F1: 0.689
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
2445 Permen_Kes_2011_2356
Case Sensitive   : P: 0.111 || R: 0.222 || F1: 0.148
Case Insensitive : P: 0.111 || R: 0.222 || F1: 0.148
2446 Permen_Keu_2013_179
Case Sensitive   : P: 0.368 || R: 0.778 || F1: 0.5
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
2447 PP_2015_62
Case Sensitive   : P: 0.316 || R: 1.0 || F1: 0.48
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
2448 Permen_Keu_2009_180
Case Sensitive   : P: 0.462 || R: 0.6 || F1: 0.522
Case Insensitive : P: 0.462 || R: 0.6 || F1: 0.522
2449 Peraturan_BPH_Migas_2013_10
Case Sensitive   : P: 0.389 || R: 0.778 || F1: 0.519
Case Insensitive : P: 0.444 || R: 0.889 || F1: 0.592
2450 Permen_Dikbud_2018_28
Case Sensitive   : P: 0.421 || R: 0.533 || F1: 0.47
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
2451 Peraturan_BKN_2018_9
Case Sensitive   : P: 0.579 || R: 0.611 || F1: 0.595
Case Insensitive

2527 Permen_PPPA_2010_10
Case Sensitive   : P: 0.158 || R: 0.333 || F1: 0.214
Case Insensitive : P: 0.211 || R: 0.444 || F1: 0.286
2528 Peraturan_BSSN_2016_16
Case Sensitive   : P: 0.632 || R: 0.75 || F1: 0.686
Case Insensitive : P: 0.632 || R: 0.75 || F1: 0.686
2529 Perkab_Musi_Rawas_2005_7
Case Sensitive   : P: 0.684 || R: 1.0 || F1: 0.812
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2530 Permen_KP_2016_28
Case Sensitive   : P: 0.737 || R: 0.737 || F1: 0.737
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
2531 Peraturan_Ombudsman_2012_9
Case Sensitive   : P: 0.316 || R: 0.462 || F1: 0.375
Case Insensitive : P: 0.316 || R: 0.462 || F1: 0.375
2532 Perkab_Tanggamus_2012_01
Case Sensitive   : P: 0.684 || R: 1.0 || F1: 0.812
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2533 Permen_Dag_2015_104
Case Sensitive   : P: 0.667 || R: 0.75 || F1: 0.706
Case Insensitive : P: 0.667 || R: 0.75 || F1: 0.706
2534 Peraturan_BNP2TKI_2017_06
Case Sensitive   : P: 0.579 || R: 0.846 || F1:

2609 Permen_PANRB_2018_25
Case Sensitive   : P: 0.611 || R: 0.579 || F1: 0.595
Case Insensitive : P: 0.611 || R: 0.579 || F1: 0.595
2610 Permen_Humham_2018_04
Case Sensitive   : P: 0.474 || R: 0.75 || F1: 0.581
Case Insensitive : P: 0.526 || R: 0.833 || F1: 0.645
2611 Permen_Humham_2019_8
Case Sensitive   : P: 0.667 || R: 0.632 || F1: 0.649
Case Insensitive : P: 0.722 || R: 0.684 || F1: 0.702
2612 Peraturan_Basarnas_2017_3
Case Sensitive   : P: 0.667 || R: 0.667 || F1: 0.667
Case Insensitive : P: 0.722 || R: 0.722 || F1: 0.722
2613 Permenko_Polhukam_2018_2
Case Sensitive   : P: 0.579 || R: 0.733 || F1: 0.647
Case Insensitive : P: 0.579 || R: 0.733 || F1: 0.647
2614 Permen_Hub_2013_81
Case Sensitive   : P: 0.579 || R: 0.917 || F1: 0.71
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
2615 Perkab_Bantul_1995_8
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2616 Permen_Agama_2017_2
Case Sensitive   : P: 0.923 || R: 0.632 || F1: 0.75
Case Insen

In [63]:
print(test_closing[3]['triples'])
print()
print(test_closing[3]['text'])

lexid:Position_Menteri_Pariwisata_Republik_Indonesia rdfs:label "Menteri Pariwisata Republik Indonesia"^^xsd:string .
lexid:Permen_Par_2015_14 lexid-s:hasPromulgationPlace lexid:Berita_Negara .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:Permen_Par_2015_14 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:Permen_Par_2015_14 lexid-s:hasPromulgationLocation lexid:City_Jakarta .
lexid:Person_Arief_Yahya rdf:type lexid-s:Person .
lexid:Permen_Par_2015_14 lexid-s:hasEnactionDate "2015-10-08"^^xsd:date .
lexid:Position_Menteri_Pariwisata_Republik_Indonesia rdf:type lexid-s:Position .
lexid:Person_Arief_Yahya rdfs:label "Arief Yahya"^^xsd:string .
lexid:Permen_Par_2015_14 lexid-s:hasEnactionOfficial lexid:Person_Arief_Yahya .
lexid:Permen_Par_2015_14 lexid-s:hasEnactionOffice lexid:Position_Menteri_Pariwisata_Republik_Indonesia .
lexid:Permen_Par_2015_14 lexid-s:hasPromulgationDate "2015-10-28"^^xsd:date .
lexid:City_Jakarta rdf:type lexid-s:City .

Pasal 4

Peraturan Men

In [50]:
print(cc_gemma.at[2627, 'ttl_1'])
print('######################')
print(test_closing[2627]['triples'])

@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dbo: <http://dbpedia.org/ontology/> .
@prefix dct: <http://purl.org/dc/terms/> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix wd: <https://www.wikidata.org/wiki/> .
@prefix lexid-s: <https://w3id.org/lex-id/schema/> .
@prefix lexid: <https://w3id.org/lex-id/data/> .

lexid:Peraturan_LAN_2016_3 lexid-s:hasPromulgationPlace lexid:Berita_Negara .
lexid:Peraturan_LAN_2016_3 lexid-s:hasEnactionDate "2016-01-12"^^xsd:date .
lexid:Peraturan_LAN_2016_3 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:Peraturan_LAN_2016_3 lexid-s:hasEnactionOfficial lexid:Person_Adi_Suryanto .
lexid:Person_Adi_Suryanto rdf:type lexid-s:Person .
lexid:Person_Adi_Suryanto rdfs:label "Adi Suryanto"^^xsd:string .
lexid:Peraturan_L

In [18]:
print(cc_gemma.at[15, '1'])

@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dbo: <http://dbpedia.org/ontology/> .
@prefix dct: <http://purl.org/dc/terms/> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix wd: <https://www.wikidata.org/wiki/> .
@prefix lexid-s: <https://w3id.org/lex-id/schema/> .
@prefix lexid: <https://w3id.org/lex-id/data/> .

lexid:PP_1986_37 lexid-s:hasPromulgationPlace lexid:Lembaran_Negara .
lexid:PP_1986_37 lexid-s:hasEnactionDate "1986-08-23"^^xsd:date .
lexid:PP_1986_37 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:PP_1986_37 lexid-s:hasEnactionOfficial lexid:Person_Soeharto .
lexid:Person_Soeharto rdf:type lexid-s:Person .
lexid:Person_Soeharto rdfs:label "Soeharto"^^xsd:string .
lexid:PP_1986_37 lexid-s:hasEnactionOffice lexid:Position_Presiden_Repu

In [82]:
def print_info(df, dataset, idx, kol):
    print(df.at[idx, kol])
    print()
    print(dataset[idx]['triples'])
    print()
    print(dataset[idx]['text'])

In [81]:
metrics = pd.read_csv('results/metrics_code.csv')
metrics

Unnamed: 0                  regulatory   ccg_p_1   ccg_r_1  ccg_f1_1  \
0              0  Permen_Ristekdikti_2017_20  0.526316  0.625000  0.571429   
1              1            Permen_KP_2013_5  0.526316  0.769231  0.625000   
2              2         Permen_Keu_2011_249  0.263158  0.555556  0.357143   
3              3          Permen_Par_2015_14  0.684211  1.000000  0.812500   
4              4             Perpres_2019_67  0.684211  0.684211  0.684211   
...          ...                         ...       ...       ...       ...   
2634        2634       Peraturan_BPS_2012_49  0.684211  1.000000  0.812500   
2635        2635        Permen_Dagri_2019_15  0.315789  0.666667  0.428571   
2636        2636                  UU_2002_10  0.052632  1.000000  0.100000   
2637        2637         Peraturan_MA_2017_4  0.315789  0.500000  0.387097   
2638        2638            Perpres_2014_108  0.473684  1.000000  0.642857   

       ccg_p_2   ccg_r_2  ccg_f1_2   ccl_p_1   ccl_r_1  ccl_f1_1   ccl_p_2  \
0     0.473684  0.562500  0.514286  0.526316  0.625000  0.571429  0.684211   
1     0.526316  0.769231  0.625000  0.684211  1.000000  0.812500  0.315789   
2     0.263158  0.555556  0.357143  0.315789  0.666667  0.428571  0.157895   
3     0.631579  0.923077  0.750000  0.315789  0.461538  0.375000  0.473684   
4     0.684211  0.684211  0.684211  0.684211  0.684211  0.684211  0.684211   
...        ...       ...       ...       ...       ...       ...       ...   
2634  0.631579  0.923077  0.750000  0.684211  1.000000  0.812500  0.631579   
2635  0.263158  0.555556  0.357143  0.315789  0.666667  0.428571  0.315789   
2636  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.052632   
2637  0.263158  0.416667  0.322581  0.315789  0.500000  0.387097  0.315789   
2638  0.473684  1.000000  0.642857  0.473684  1.000000  0.642857  0.473684   

       ccl_r_2  ccl_f1_2   ccp_p_1   ccp_r_1  ccp_f1_1   ccp_p_2   ccp_r_2  \
0     0.812500  0.742857  0.526316  0.625000  0.571429  0.473684  0.562500   
1     0.461538  0.375000  0.333333  0.461538  0.387097  0.526316  0.769231   
2     0.333333  0.214286  0.157895  0.333333  0.214286  0.157895  0.333333   
3     0.692308  0.562500  0.473684  0.692308  0.562500  0.631579  0.923077   
4     0.684211  0.684211  0.684211  0.684211  0.684211  0.842105  0.842105   
...        ...       ...       ...       ...       ...       ...       ...   
2634  0.923077  0.750000  0.500000  0.692308  0.580645  0.473684  0.692308   
2635  0.666667  0.428571  0.368421  0.777778  0.500000  0.368421  0.777778   
2636  1.000000  0.100000  0.052632  1.000000  0.100000  0.052632  1.000000   
2637  0.500000  0.387097  0.473684  0.750000  0.580645  0.444444  0.666667   
2638  1.000000  0.642857  0.444444  0.888889  0.592593  0.473684  1.000000   

      ccp_f1_2  
0     0.514286  
1     0.625000  
2     0.214286  
3     0.750000  
4     0.842105  
...        ...  
2634  0.562500  
2635  0.500000  
2636  0.100000  
2637  0.533333  
2638  0.642857  

[2639 rows x 20 columns]

In [92]:
metrics = pd.read_csv('results/metrics_code.csv')
metrics

Unnamed: 0                  regulatory   ccg_p_1   ccg_r_1  ccg_f1_1  \
0              0  Permen_Ristekdikti_2017_20  0.526316  0.625000  0.571429   
1              1            Permen_KP_2013_5  0.526316  0.769231  0.625000   
2              2         Permen_Keu_2011_249  0.263158  0.555556  0.357143   
3              3          Permen_Par_2015_14  0.684211  1.000000  0.812500   
4              4             Perpres_2019_67  0.684211  0.684211  0.684211   
...          ...                         ...       ...       ...       ...   
2634        2634       Peraturan_BPS_2012_49  0.684211  1.000000  0.812500   
2635        2635        Permen_Dagri_2019_15  0.315789  0.666667  0.428571   
2636        2636                  UU_2002_10  0.052632  1.000000  0.100000   
2637        2637         Peraturan_MA_2017_4  0.315789  0.500000  0.387097   
2638        2638            Perpres_2014_108  0.473684  1.000000  0.642857   

       ccg_p_2   ccg_r_2  ccg_f1_2   ccl_p_1   ccl_r_1  ...  ocl_f1_1  \
0     0.473684  0.562500  0.514286  0.526316  0.625000  ...  0.692308   
1     0.526316  0.769231  0.625000  0.684211  1.000000  ...  0.611765   
2     0.263158  0.555556  0.357143  0.315789  0.666667  ...  0.666667   
3     0.631579  0.923077  0.750000  0.315789  0.461538  ...  0.635294   
4     0.684211  0.684211  0.684211  0.684211  0.684211  ...  0.705882   
...        ...       ...       ...       ...       ...  ...       ...   
2634  0.631579  0.923077  0.750000  0.684211  1.000000  ...  0.466667   
2635  0.263158  0.555556  0.357143  0.315789  0.666667  ...  0.346154   
2636  0.000000  0.000000  0.000000  0.000000  0.000000  ...  0.216867   
2637  0.263158  0.416667  0.322581  0.315789  0.500000  ...  0.571429   
2638  0.473684  1.000000  0.642857  0.473684  1.000000  ...  0.654206   

       ocl_p_2   ocl_r_2  ocl_f1_2   ocp_p_1   ocp_r_1  ocp_f1_1   ocp_p_2  \
0     0.743590  0.725000  0.734177  0.641026  0.625000  0.632911  0.466667   
1     0.571429  0.666667  0.615385  0.466667  0.583333  0.518519  0.533333   
2     0.619048  0.722222  0.666667  0.571429  0.666667  0.615385  0.692308   
3     0.690476  0.674419  0.682353  0.648649  0.558140  0.600000  0.642857   
4     0.629630  0.708333  0.666667  0.592593  0.666667  0.627451  0.518519   
...        ...       ...       ...       ...       ...       ...       ...   
2634  0.369231  0.705882  0.484848  0.290909  0.470588  0.359551  0.338028   
2635  0.571429  0.289855  0.384615  0.588235  0.289855  0.388350  0.485714   
2636  0.232558  0.243902  0.238095  0.700000  0.682927  0.691358  0.600000   
2637  0.777778  0.724138  0.750000  0.485714  0.586207  0.531250  0.629630   
2638  0.761905  0.744186  0.752941  0.717391  0.767442  0.741573  0.517241   

       ocp_r_2  ocp_f1_2  
0     0.175000  0.254545  
1     0.222222  0.313725  
2     0.500000  0.580645  
3     0.209302  0.315789  
4     0.583333  0.549020  
...        ...       ...  
2634  0.705882  0.457143  
2635  0.246377  0.326923  
2636  0.658537  0.627907  
2637  0.586207  0.607143  
2638  0.697674  0.594059  

[2639 rows x 38 columns]

In [83]:
print_info(cc_llama, test_closing, 2, '2')

lexid:Permen_Keu_2011_249 lexid-s:hasPromulgationPlace lexid:Berita_Negara .
lexid:Permen_Keu_2011_249 lexid-s:hasEnactionDate "2011-12-28"^^xsd:date .
lexid:Permen_Keu_2011_249 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:Permen_Keu_2011_249 lexid-s:hasEnactionOfficial lexid:Person_Agus_Dw_Martowardojo .
lexid:Person_Agus_Dw_Martowardojo rdf:type lexid-s:Person .
lexid:Person_Agus_Dw_Martowardojo rdfs:label "Agus D.W. Martowardojo"^^xsd:string .
lexid:Permen_Keu_2011_249 lexid-s:hasEnactionOffice lexid:Position_Menteri_Keuangan .
lexid:Position_Menteri_Keuangan rdf:type lexid-s:Position .
lexid:Position_Menteri_Keuangan rdfs:label "Menteri Keuangan"^^xsd:string .
lexid:Permen_Keu_2011_249 lexid-s:hasPromulgationDate "2011-12-28"^^xsd:date .
lexid:Permen_Keu_2011_249 lexid-s:hasPromulgationLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta 

# Opening

In [72]:
results = pd.DataFrame()
results = pd.DataFrame(columns=['regulatory'
                                , 'ocg_s_p_1'
                                , 'ocg_s_r_1'
                                , 'ocg_s_f1_1'
                                , 'ocg_s_p_2'
                                , 'ocg_s_r_2'
                                , 'ocg_s_f1_2'
                                , 'ocl_s_p_1'
                                , 'ocl_s_r_1'
                                , 'ocl_s_f1_1'
                                , 'ocl_s_p_2'
                                , 'ocl_s_r_2'
                                , 'ocl_s_f1_2'
                                , 'ocp_s_p_1'
                                , 'ocp_s_r_1'
                                , 'ocp_s_f1_1'
                                , 'ocp_s_p_2'
                                , 'ocp_s_r_2'
                                , 'ocp_s_f1_2'
                                , 'ocg_i_p_1'
                                , 'ocg_i_r_1'
                                , 'ocg_i_f1_1'
                                , 'ocg_i_p_2'
                                , 'ocg_i_r_2'
                                , 'ocg_i_f1_2'
                                , 'ocl_i_p_1'
                                , 'ocl_i_r_1'
                                , 'ocl_i_f1_1'
                                , 'ocl_i_p_2'
                                , 'ocl_i_r_2'
                                , 'ocl_i_f1_2'
                                , 'ocp_i_p_1'
                                , 'ocp_i_r_1'
                                , 'ocp_i_f1_1'
                                , 'ocp_i_p_2'
                                , 'ocp_i_r_2'
                                , 'ocp_i_f1_2'
                               ])

In [73]:
test_opening_name = "dataset-surface-info/new-opening/new-opening-1"
test_opening = load_from_disk(test_opening_name)

In [104]:
oc_gemma = pd.read_csv('results/new/OC_gemma_post.csv')
oc_llama = pd.read_csv('results/new/OC_llama_post.csv')
oc_phi = pd.read_csv('results/new/OC_phi_post.csv')

In [75]:
test_1('ocg', oc_gemma, test_opening, '1', results, 'oc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.725 || R: 0.725 || F1: 0.725
Case Insensitive : P: 0.725 || R: 0.725 || F1: 0.725
1 Permen_KP_2013_5
Case Sensitive   : P: 0.558 || R: 0.667 || F1: 0.608
Case Insensitive : P: 0.605 || R: 0.722 || F1: 0.658
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.591 || R: 0.722 || F1: 0.65
Case Insensitive : P: 0.682 || R: 0.833 || F1: 0.75
3 Permen_Par_2015_14
Case Sensitive   : P: 0.674 || R: 0.674 || F1: 0.674
Case Insensitive : P: 0.721 || R: 0.721 || F1: 0.721
4 Perpres_2019_67
Case Sensitive   : P: 0.571 || R: 0.667 || F1: 0.615
Case Insensitive : P: 0.643 || R: 0.75 || F1: 0.692
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.71 || R: 0.475 || F1: 0.569
Case Insensitive : P: 0.729 || R: 0.487 || F1: 0.584
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.406 || R: 0.531 || F1: 0.46
Case Insensitive : P: 0.422 || R: 0.551 || F1: 0.478
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.66 || R: 0.721 || F1: 0.689
Case Insensitive : P: 0.

67 Permen_Dikbud_2012_7
Case Sensitive   : P: 0.581 || R: 0.714 || F1: 0.641
Case Insensitive : P: 0.628 || R: 0.771 || F1: 0.692
68 Perpres_2013_103
Case Sensitive   : P: 0.744 || R: 0.744 || F1: 0.744
Case Insensitive : P: 0.795 || R: 0.795 || F1: 0.795
69 PP_2018_49
Case Sensitive   : P: 0.727 || R: 0.727 || F1: 0.727
Case Insensitive : P: 0.818 || R: 0.818 || F1: 0.818
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 0.686 || R: 0.667 || F1: 0.676
Case Insensitive : P: 0.743 || R: 0.722 || F1: 0.732
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.182 || R: 0.211 || F1: 0.195
Case Insensitive : P: 0.182 || R: 0.211 || F1: 0.195
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.723 || R: 0.716 || F1: 0.719
Case Insensitive : P: 0.743 || R: 0.735 || F1: 0.739
73 Perpres_2008_41
Case Sensitive   : P: 0.696 || R: 0.696 || F1: 0.696
Case Insensitive : P: 0.783 || R: 0.783 || F1: 0.783
74 Permen_PR_2009_03
Case Sensitive   : P: 0.222 || R: 0.381 || F1: 0.281
Case Insensitive : P: 0.

Case Insensitive : P: 0.733 || R: 0.786 || F1: 0.759
132 UU_1953_14
Case Sensitive   : P: 0.034 || R: 0.217 || F1: 0.059
Case Insensitive : P: 0.041 || R: 0.261 || F1: 0.071
133 Peraturan_Batan_2015_1
Case Sensitive   : P: 0.568 || R: 0.656 || F1: 0.609
Case Insensitive : P: 0.568 || R: 0.656 || F1: 0.609
134 Peraturan_LAN_2017_3
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.812 || R: 0.812 || F1: 0.812
135 Perkab_Badung_2013_5
Case Sensitive   : P: 0.462 || R: 0.585 || F1: 0.516
Case Insensitive : P: 0.5 || R: 0.634 || F1: 0.559
136 Peraturan_BNPB_2016_02
Case Sensitive   : P: 0.747 || R: 0.739 || F1: 0.743
Case Insensitive : P: 0.769 || R: 0.761 || F1: 0.765
137 Peraturan_Perpusnas_2018_8
Case Sensitive   : P: 0.5 || R: 0.622 || F1: 0.554
Case Insensitive : P: 0.543 || R: 0.676 || F1: 0.602
138 PP_1998_77
Case Sensitive   : P: 0.741 || R: 0.769 || F1: 0.755
Case Insensitive : P: 0.815 || R: 0.846 || F1: 0.83
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 0

199 Peraturan_LAN_2015_2
Case Sensitive   : P: 0.682 || R: 0.716 || F1: 0.699
Case Insensitive : P: 0.694 || R: 0.728 || F1: 0.711
200 Permen_Keu_2009_234
Case Sensitive   : P: 0.522 || R: 0.632 || F1: 0.572
Case Insensitive : P: 0.652 || R: 0.789 || F1: 0.714
201 PP_2009_78
Case Sensitive   : P: 0.611 || R: 0.71 || F1: 0.657
Case Insensitive : P: 0.639 || R: 0.742 || F1: 0.687
202 Peraturan_BPOM_2019_30
Case Sensitive   : P: 0.625 || R: 0.625 || F1: 0.625
Case Insensitive : P: 0.625 || R: 0.625 || F1: 0.625
203 Permen_Pora_2019_3
Case Sensitive   : P: 0.484 || R: 0.556 || F1: 0.518
Case Insensitive : P: 0.548 || R: 0.63 || F1: 0.586
204 Perprov_Papua_2013_14
Case Sensitive   : P: 0.683 || R: 0.651 || F1: 0.667
Case Insensitive : P: 0.692 || R: 0.661 || F1: 0.676
205 Permen_PANRB_2013_32
Case Sensitive   : P: 0.627 || R: 0.712 || F1: 0.667
Case Insensitive : P: 0.657 || R: 0.746 || F1: 0.699
206 Permen_Dagri_2017_3
Case Sensitive   : P: 0.722 || R: 0.722 || F1: 0.722
Case Insensitive :

Case Insensitive : P: 0.262 || R: 0.297 || F1: 0.278
267 PP_1957_42
Case Sensitive   : P: 0.333 || R: 0.357 || F1: 0.345
Case Insensitive : P: 0.4 || R: 0.429 || F1: 0.414
268 Permen_Keu_2011_178
Case Sensitive   : P: 0.481 || R: 0.65 || F1: 0.553
Case Insensitive : P: 0.5 || R: 0.675 || F1: 0.574
269 PP_1980_38
Case Sensitive   : P: 0.304 || R: 0.318 || F1: 0.311
Case Insensitive : P: 0.391 || R: 0.409 || F1: 0.4
270 Permen_Keu_2011_36
Case Sensitive   : P: 0.593 || R: 0.625 || F1: 0.609
Case Insensitive : P: 0.593 || R: 0.625 || F1: 0.609
271 Peraturan_BKN_2019_16
Case Sensitive   : P: 0.633 || R: 0.119 || F1: 0.2
Case Insensitive : P: 0.7 || R: 0.132 || F1: 0.222
272 Permen_Humham_2015_45
Case Sensitive   : P: 0.739 || R: 0.739 || F1: 0.739
Case Insensitive : P: 0.826 || R: 0.826 || F1: 0.826
273 Permen_KP_2018_13
Case Sensitive   : P: 0.659 || R: 0.094 || F1: 0.165
Case Insensitive : P: 0.705 || R: 0.1 || F1: 0.175
274 UU_1999_11
Case Sensitive   : P: 0.316 || R: 0.414 || F1: 0.358

...

2349 Permen_Dagri_2017_10
Case Sensitive   : P: 0.739 || R: 0.739 || F1: 0.739
Case Insensitive : P: 0.783 || R: 0.783 || F1: 0.783
2350 Permen_Dagri_2017_97
Case Sensitive   : P: 0.686 || R: 0.686 || F1: 0.686
Case Insensitive : P: 0.743 || R: 0.743 || F1: 0.743
2351 PP_2018_32
Case Sensitive   : P: 0.65 || R: 0.684 || F1: 0.667
Case Insensitive : P: 0.75 || R: 0.789 || F1: 0.769
2352 UU_2002_27
Case Sensitive   : P: 0.267 || R: 0.267 || F1: 0.267
Case Insensitive : P: 0.311 || R: 0.311 || F1: 0.311
2353 Permen_PUPR_2015_01
Case Sensitive   : P: 0.625 || R: 0.625 || F1: 0.625
Case Insensitive : P: 0.688 || R: 0.688 || F1: 0.688
2354 PP_2019_28
Case Sensitive   : P: 0.548 || R: 0.739 || F1: 0.629
Case Insensitive : P: 0.645 || R: 0.87 || F1: 0.741
2355 Perkot_Depok_2003_10
Case Sensitive   : P: 0.145 || R: 0.149 || F1: 0.147
Case Insensitive : P: 0.174 || R: 0.179 || F1: 0.176
2356 Permen_Hub_2013_16
Case Sensitive   : P: 0.282 || R: 0.306 || F1: 0.294
Case Insensitive : P: 0.282 || R:

2425 Perkot_Depok_2008_11
Case Sensitive   : P: 0.699 || R: 0.581 || F1: 0.635
Case Insensitive : P: 0.718 || R: 0.597 || F1: 0.652
2426 Permen_Hub_2014_20
Case Sensitive   : P: 0.514 || R: 0.101 || F1: 0.169
Case Insensitive : P: 0.571 || R: 0.112 || F1: 0.187
2427 Perkab_Pacitan_2010_6
Case Sensitive   : P: 0.615 || R: 0.615 || F1: 0.615
Case Insensitive : P: 0.667 || R: 0.667 || F1: 0.667
2428 Perkab_Bengkulu_Tengah_2011_12
Case Sensitive   : P: 0.623 || R: 0.611 || F1: 0.617
Case Insensitive : P: 0.66 || R: 0.648 || F1: 0.654
2429 Permen_KP_2018_64
Case Sensitive   : P: 0.589 || R: 0.688 || F1: 0.635
Case Insensitive : P: 0.625 || R: 0.729 || F1: 0.673
2430 Perprov_Kaltim_2011_08
Case Sensitive   : P: 0.667 || R: 0.426 || F1: 0.52
Case Insensitive : P: 0.676 || R: 0.432 || F1: 0.527
2431 Perkab_Jembrana_2011_4
Case Sensitive   : P: 0.167 || R: 0.727 || F1: 0.272
Case Insensitive : P: 0.208 || R: 0.909 || F1: 0.339
2432 PP_2016_59
Case Sensitive   : P: 0.789 || R: 0.75 || F1: 0.769


2494 Perkot_Samarinda_2008_18
Case Sensitive   : P: 0.684 || R: 0.643 || F1: 0.663
Case Insensitive : P: 0.709 || R: 0.667 || F1: 0.687
2495 UU_1974_4
Case Sensitive   : P: 0.206 || R: 0.368 || F1: 0.264
Case Insensitive : P: 0.235 || R: 0.421 || F1: 0.302
2496 Peraturan_BPKP_2017_6
Case Sensitive   : P: 0.449 || R: 0.579 || F1: 0.506
Case Insensitive : P: 0.49 || R: 0.632 || F1: 0.552
2497 Permen_Perin_2019_35
Case Sensitive   : P: 0.747 || R: 0.779 || F1: 0.763
Case Insensitive : P: 0.768 || R: 0.8 || F1: 0.784
2498 PP_2007_35
Case Sensitive   : P: 0.778 || R: 0.778 || F1: 0.778
Case Insensitive : P: 0.889 || R: 0.889 || F1: 0.889
2499 Permen_Dagri_2016_75
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.833 || R: 0.833 || F1: 0.833
2500 Permen_ESDM_2014_36
Case Sensitive   : P: 0.533 || R: 0.667 || F1: 0.593
Case Insensitive : P: 0.578 || R: 0.722 || F1: 0.642
2501 Peraturan_Polri_2015_18
Case Sensitive   : P: 0.742 || R: 0.719 || F1: 0.73
Case Insensitive :

2558 Perkot_Bogor_2011_4
Case Sensitive   : P: 0.719 || R: 0.464 || F1: 0.564
Case Insensitive : P: 0.742 || R: 0.478 || F1: 0.581
2559 Perkot_Madiun_2008_07
Case Sensitive   : P: 0.65 || R: 0.639 || F1: 0.644
Case Insensitive : P: 0.667 || R: 0.656 || F1: 0.661
2560 Permen_Dagri_2016_32
Case Sensitive   : P: 0.605 || R: 0.722 || F1: 0.658
Case Insensitive : P: 0.628 || R: 0.75 || F1: 0.684
2561 Permen_Kopukm_2013_09
Case Sensitive   : P: 0.662 || R: 0.697 || F1: 0.679
Case Insensitive : P: 0.688 || R: 0.724 || F1: 0.706
2562 Perkot_Samarinda_2006_09
Case Sensitive   : P: 0.588 || R: 0.58 || F1: 0.584
Case Insensitive : P: 0.618 || R: 0.609 || F1: 0.613
2563 Perkab_Rokan_Hilir_2014_6
Case Sensitive   : P: 0.545 || R: 0.585 || F1: 0.564
Case Insensitive : P: 0.591 || R: 0.634 || F1: 0.612
2564 UU_2007_36
Case Sensitive   : P: 0.66 || R: 0.689 || F1: 0.674
Case Insensitive : P: 0.681 || R: 0.711 || F1: 0.696
2565 Permen_Keu_2015_229
Case Sensitive   : P: 0.5 || R: 0.625 || F1: 0.556
Case

2625 Permen_Dikbud_2014_36
Case Sensitive   : P: 0.605 || R: 0.676 || F1: 0.639
Case Insensitive : P: 0.684 || R: 0.765 || F1: 0.722
2626 Perkab_Hulu_Sungai_Tengah_2012_2
Case Sensitive   : P: 0.538 || R: 0.079 || F1: 0.138
Case Insensitive : P: 0.692 || R: 0.101 || F1: 0.176
2627 Peraturan_LAN_2016_3
Case Sensitive   : P: 0.513 || R: 0.714 || F1: 0.597
Case Insensitive : P: 0.564 || R: 0.786 || F1: 0.657
2628 Permen_Tan_2013_08
Case Sensitive   : P: 0.679 || R: 0.594 || F1: 0.634
Case Insensitive : P: 0.702 || R: 0.615 || F1: 0.656
2629 Peraturan_OJK_2014_37
Case Sensitive   : P: 0.7 || R: 0.7 || F1: 0.7
Case Insensitive : P: 0.8 || R: 0.8 || F1: 0.8
2630 Permen_Dag_2015_115
Case Sensitive   : P: 0.704 || R: 0.746 || F1: 0.724
Case Insensitive : P: 0.718 || R: 0.761 || F1: 0.739
2631 Perpres_2011_24
Case Sensitive   : P: 0.65 || R: 0.684 || F1: 0.667
Case Insensitive : P: 0.7 || R: 0.737 || F1: 0.718
2632 PP_1954_4
Case Sensitive   : P: 0.286 || R: 0.5 || F1: 0.364
Case Insensitive : 

In [76]:
test_1('ocg', oc_gemma, test_opening, '2', results, 'oc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.725 || R: 0.725 || F1: 0.725
Case Insensitive : P: 0.725 || R: 0.725 || F1: 0.725
1 Permen_KP_2013_5
Case Sensitive   : P: 0.535 || R: 0.639 || F1: 0.582
Case Insensitive : P: 0.581 || R: 0.694 || F1: 0.632
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.591 || R: 0.722 || F1: 0.65
Case Insensitive : P: 0.682 || R: 0.833 || F1: 0.75
3 Permen_Par_2015_14
Case Sensitive   : P: 0.674 || R: 0.674 || F1: 0.674
Case Insensitive : P: 0.721 || R: 0.721 || F1: 0.721
4 Perpres_2019_67
Case Sensitive   : P: 0.643 || R: 0.75 || F1: 0.692
Case Insensitive : P: 0.714 || R: 0.833 || F1: 0.769
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.734 || R: 0.362 || F1: 0.485
Case Insensitive : P: 0.759 || R: 0.375 || F1: 0.502
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.391 || R: 0.51 || F1: 0.443
Case Insensitive : P: 0.406 || R: 0.531 || F1: 0.46
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.583 || R: 0.651 || F1: 0.615
Case Insensitive : P: 0

Case Insensitive : P: 0.761 || R: 0.574 || F1: 0.654
65 Perprov_Jateng_2001_10
Case Sensitive   : P: 0.326 || R: 0.385 || F1: 0.353
Case Insensitive : P: 0.348 || R: 0.41 || F1: 0.376
66 PP_2008_70
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.792 || R: 0.792 || F1: 0.792
67 Permen_Dikbud_2012_7
Case Sensitive   : P: 0.605 || R: 0.743 || F1: 0.667
Case Insensitive : P: 0.651 || R: 0.8 || F1: 0.718
68 Perpres_2013_103
Case Sensitive   : P: 0.744 || R: 0.744 || F1: 0.744
Case Insensitive : P: 0.795 || R: 0.795 || F1: 0.795
69 PP_2018_49
Case Sensitive   : P: 0.682 || R: 0.682 || F1: 0.682
Case Insensitive : P: 0.773 || R: 0.773 || F1: 0.773
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 0.667 || R: 0.667 || F1: 0.667
Case Insensitive : P: 0.75 || R: 0.75 || F1: 0.75
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.385 || R: 0.526 || F1: 0.445
Case Insensitive : P: 0.385 || R: 0.526 || F1: 0.445
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.691 || R:

Case Insensitive : P: 0.558 || R: 0.707 || F1: 0.624
136 Peraturan_BNPB_2016_02
Case Sensitive   : P: 0.739 || R: 0.739 || F1: 0.739
Case Insensitive : P: 0.75 || R: 0.75 || F1: 0.75
137 Peraturan_Perpusnas_2018_8
Case Sensitive   : P: 0.565 || R: 0.703 || F1: 0.626
Case Insensitive : P: 0.609 || R: 0.757 || F1: 0.675
138 PP_1998_77
Case Sensitive   : P: 0.296 || R: 0.308 || F1: 0.302
Case Insensitive : P: 0.37 || R: 0.385 || F1: 0.377
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 0.605 || R: 0.667 || F1: 0.634
Case Insensitive : P: 0.651 || R: 0.718 || F1: 0.683
140 Permen_Keu_2015_108
Case Sensitive   : P: 0.714 || R: 0.714 || F1: 0.714
Case Insensitive : P: 0.786 || R: 0.786 || F1: 0.786
141 Permen_LHK_2019_13
Case Sensitive   : P: 0.575 || R: 0.535 || F1: 0.554
Case Insensitive : P: 0.625 || R: 0.581 || F1: 0.602
142 PP_1983_17
Case Sensitive   : P: 0.344 || R: 0.407 || F1: 0.373
Case Insensitive : P: 0.406 || R: 0.481 || F1: 0.44
143 Perpres_2015_82
Case Sensitive   : P: 0.714 ||

210 Perkot_Depok_2011_07
Case Sensitive   : P: 0.557 || R: 0.582 || F1: 0.569
Case Insensitive : P: 0.571 || R: 0.597 || F1: 0.584
211 PP_2012_13
Case Sensitive   : P: 0.742 || R: 0.742 || F1: 0.742
Case Insensitive : P: 0.806 || R: 0.806 || F1: 0.806
212 Permen_Dikbud_2011_50
Case Sensitive   : P: 0.407 || R: 0.478 || F1: 0.44
Case Insensitive : P: 0.481 || R: 0.565 || F1: 0.52
213 Permen_LH_2012_10
Case Sensitive   : P: 0.625 || R: 0.714 || F1: 0.667
Case Insensitive : P: 0.656 || R: 0.75 || F1: 0.7
214 Permen_PANRB_2015_12
Case Sensitive   : P: 0.636 || R: 0.7 || F1: 0.666
Case Insensitive : P: 0.682 || R: 0.75 || F1: 0.714
215 Permen_KP_2016_6
Case Sensitive   : P: 0.645 || R: 0.741 || F1: 0.69
Case Insensitive : P: 0.677 || R: 0.778 || F1: 0.724
216 Perkab_Pontianak_2010_18
Case Sensitive   : P: 0.65 || R: 0.634 || F1: 0.642
Case Insensitive : P: 0.7 || R: 0.683 || F1: 0.691
217 Permen_PANRB_2013_45
Case Sensitive   : P: 0.658 || R: 0.735 || F1: 0.694
Case Insensitive : P: 0.684 |

Case Insensitive : P: 0.59 || R: 0.78 || F1: 0.672
281 Peraturan_OJK_2018_32
Case Sensitive   : P: 0.773 || R: 0.773 || F1: 0.773
Case Insensitive : P: 0.864 || R: 0.864 || F1: 0.864
282 Perkot_Binjai_2000_5
Case Sensitive   : P: 0.125 || R: 0.562 || F1: 0.205
Case Insensitive : P: 0.153 || R: 0.688 || F1: 0.25
283 Peraturan_BKN_2015_47
Case Sensitive   : P: 0.657 || R: 0.174 || F1: 0.275
Case Insensitive : P: 0.686 || R: 0.181 || F1: 0.286
284 Peraturan_BPIP_2018_3
Case Sensitive   : P: 0.571 || R: 0.667 || F1: 0.615
Case Insensitive : P: 0.643 || R: 0.75 || F1: 0.692
285 Permenko_Kesra_2012_03
Case Sensitive   : P: 0.677 || R: 0.677 || F1: 0.677
Case Insensitive : P: 0.742 || R: 0.742 || F1: 0.742
286 Perkab_Jayapura_2001_3
Case Sensitive   : P: 0.468 || R: 0.55 || F1: 0.506
Case Insensitive : P: 0.553 || R: 0.65 || F1: 0.598
287 PP_2009_62
Case Sensitive   : P: 0.679 || R: 0.655 || F1: 0.667
Case Insensitive : P: 0.75 || R: 0.724 || F1: 0.737
288 Permen_Hub_2018_12
Case Sensitive   

...

Case Insensitive : P: 0.563 || R: 0.598 || F1: 0.58
2338 Permen_Dagri_2016_44
Case Sensitive   : P: 0.706 || R: 0.706 || F1: 0.706
Case Insensitive : P: 0.735 || R: 0.735 || F1: 0.735
2339 Perprov_Banten_2005_7
Case Sensitive   : P: 0.926 || R: 0.913 || F1: 0.919
Case Insensitive : P: 0.971 || R: 0.957 || F1: 0.964
2340 Perkab_Karawang_2014_5
Case Sensitive   : P: 0.466 || R: 0.495 || F1: 0.48
Case Insensitive : P: 0.474 || R: 0.505 || F1: 0.489
2341 PP_2016_30
Case Sensitive   : P: 0.577 || R: 0.682 || F1: 0.625
Case Insensitive : P: 0.654 || R: 0.773 || F1: 0.709
2342 Permen_Ristekdikti_2017_67
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.775 || R: 0.775 || F1: 0.775
2343 Perkab_Mamuju_Utara_2006_14
Case Sensitive   : P: 0.596 || R: 0.633 || F1: 0.614
Case Insensitive : P: 0.635 || R: 0.673 || F1: 0.653
2344 Permen_Keu_2015_221
Case Sensitive   : P: 0.72 || R: 0.72 || F1: 0.72
Case Insensitive : P: 0.8 || R: 0.8 || F1: 0.8
2345 Permen_Keu_2019_119
Case Se

2412 Peraturan_Polri_2018_4
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.875 || R: 0.875 || F1: 0.875
2413 UU_1953_7
Case Sensitive   : P: 0.4 || R: 0.6 || F1: 0.48
Case Insensitive : P: 0.533 || R: 0.8 || F1: 0.64
2414 Permen_Kes_2016_1
Case Sensitive   : P: 0.719 || R: 0.719 || F1: 0.719
Case Insensitive : P: 0.781 || R: 0.781 || F1: 0.781
2415 Perkot_Tasikmalaya_2007_8
Case Sensitive   : P: 0.063 || R: 0.5 || F1: 0.112
Case Insensitive : P: 0.089 || R: 0.7 || F1: 0.158
2416 PP_1994_8
Case Sensitive   : P: 0.316 || R: 0.333 || F1: 0.324
Case Insensitive : P: 0.316 || R: 0.333 || F1: 0.324
2417 Permen_Hub_2018_27
Case Sensitive   : P: 0.63 || R: 0.63 || F1: 0.63
Case Insensitive : P: 0.704 || R: 0.704 || F1: 0.704
2418 PP_1996_14
Case Sensitive   : P: 0.519 || R: 0.538 || F1: 0.528
Case Insensitive : P: 0.556 || R: 0.577 || F1: 0.566
2419 Peraturan_LKPP_2018_11
Case Sensitive   : P: 0.636 || R: 0.304 || F1: 0.411
Case Insensitive : P: 0.727 || R: 0.348 || 

2484 Permen_Keu_2014_59
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.875 || R: 0.875 || F1: 0.875
2485 Peraturan_BPOM_2013_29
Case Sensitive   : P: 0.346 || R: 0.643 || F1: 0.45
Case Insensitive : P: 0.365 || R: 0.679 || F1: 0.475
2486 PP_1961_166
Case Sensitive   : P: 0.175 || R: 0.318 || F1: 0.226
Case Insensitive : P: 0.225 || R: 0.409 || F1: 0.29
2487 Permen_Humham_2016_66
Case Sensitive   : P: 0.714 || R: 0.714 || F1: 0.714
Case Insensitive : P: 0.786 || R: 0.786 || F1: 0.786
2488 PP_2007_62
Case Sensitive   : P: 0.609 || R: 0.737 || F1: 0.667
Case Insensitive : P: 0.696 || R: 0.842 || F1: 0.762
2489 Permen_Dikbud_2013_1
Case Sensitive   : P: 0.471 || R: 0.593 || F1: 0.525
Case Insensitive : P: 0.559 || R: 0.704 || F1: 0.623
2490 Perkab_Kotabaru_2013_01
Case Sensitive   : P: 0.645 || R: 0.635 || F1: 0.64
Case Insensitive : P: 0.645 || R: 0.635 || F1: 0.64
2491 Perkot_Depok_2012_02
Case Sensitive   : P: 0.657 || R: 0.634 || F1: 0.645
Case Insensitive : 

2551 Perkab_Serdang_Bedagai_2012_14
Case Sensitive   : P: 0.667 || R: 0.667 || F1: 0.667
Case Insensitive : P: 0.706 || R: 0.706 || F1: 0.706
2552 PP_2003_34
Case Sensitive   : P: 0.346 || R: 0.36 || F1: 0.353
Case Insensitive : P: 0.385 || R: 0.4 || F1: 0.392
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.68 || R: 0.68 || F1: 0.68
Case Insensitive : P: 0.72 || R: 0.72 || F1: 0.72
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.781 || R: 0.781 || F1: 0.781
2555 Peraturan_OJK_2019_13
Case Sensitive   : P: 0.571 || R: 0.667 || F1: 0.615
Case Insensitive : P: 0.643 || R: 0.75 || F1: 0.692
2556 Permen_Kes_2013_75
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.8 || R: 0.8 || F1: 0.8
2557 Permen_Dagri_2012_16
Case Sensitive   : P: 0.725 || R: 0.725 || F1: 0.725
Case Insensitive : P: 0.775 || R: 0.775 || F1: 0.775
2558 Perkot_Bogor_2011_4
Case Sensitive   : P: 0.613 || R: 0.609 || F1: 0.611
Case Insensitive

2621 Permen_Nakertrans_2009_22
Case Sensitive   : P: 0.553 || R: 0.583 || F1: 0.568
Case Insensitive : P: 0.605 || R: 0.639 || F1: 0.622
2622 Peraturan_LAN_2017_2
Case Sensitive   : P: 0.73 || R: 0.742 || F1: 0.736
Case Insensitive : P: 0.746 || R: 0.758 || F1: 0.752
2623 Peraturan_BPJSKES_2018_6
Case Sensitive   : P: 0.692 || R: 0.692 || F1: 0.692
Case Insensitive : P: 0.692 || R: 0.692 || F1: 0.692
2624 Permen_Dikbud_2011_56
Case Sensitive   : P: 0.724 || R: 0.75 || F1: 0.737
Case Insensitive : P: 0.733 || R: 0.759 || F1: 0.746
2625 Permen_Dikbud_2014_36
Case Sensitive   : P: 0.632 || R: 0.706 || F1: 0.667
Case Insensitive : P: 0.711 || R: 0.794 || F1: 0.75
2626 Perkab_Hulu_Sungai_Tengah_2012_2
Case Sensitive   : P: 0.443 || R: 0.483 || F1: 0.462
Case Insensitive : P: 0.464 || R: 0.506 || F1: 0.484
2627 Peraturan_LAN_2016_3
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.821 || R: 0.821 || F1: 0.821
2628 Permen_Tan_2013_08
Case Sensitive   : P: 0.667 || R: 0

In [77]:
test_1('ocl', oc_llama, test_opening, '1', results, 'oc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.744 || R: 0.725 || F1: 0.734
Case Insensitive : P: 0.744 || R: 0.725 || F1: 0.734
1 Permen_KP_2013_5
Case Sensitive   : P: 0.52 || R: 0.722 || F1: 0.605
Case Insensitive : P: 0.56 || R: 0.778 || F1: 0.651
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.591 || R: 0.722 || F1: 0.65
Case Insensitive : P: 0.682 || R: 0.833 || F1: 0.75
3 Permen_Par_2015_14
Case Sensitive   : P: 0.628 || R: 0.628 || F1: 0.628
Case Insensitive : P: 0.674 || R: 0.674 || F1: 0.674
4 Perpres_2019_67
Case Sensitive   : P: 0.5 || R: 0.75 || F1: 0.6
Case Insensitive : P: 0.611 || R: 0.917 || F1: 0.733
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.421 || R: 0.05 || F1: 0.089
Case Insensitive : P: 0.526 || R: 0.062 || F1: 0.111
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.35 || R: 0.143 || F1: 0.203
Case Insensitive : P: 0.45 || R: 0.184 || F1: 0.261
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.526 || R: 0.698 || F1: 0.6
Case Insensitive : P: 0.596 || R

67 Permen_Dikbud_2012_7
Case Sensitive   : P: 0.558 || R: 0.686 || F1: 0.615
Case Insensitive : P: 0.581 || R: 0.714 || F1: 0.641
68 Perpres_2013_103
Case Sensitive   : P: 0.821 || R: 0.821 || F1: 0.821
Case Insensitive : P: 0.872 || R: 0.872 || F1: 0.872
69 PP_2018_49
Case Sensitive   : P: 0.552 || R: 0.727 || F1: 0.628
Case Insensitive : P: 0.621 || R: 0.818 || F1: 0.706
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 0.5 || R: 0.667 || F1: 0.572
Case Insensitive : P: 0.562 || R: 0.75 || F1: 0.643
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.423 || R: 0.579 || F1: 0.489
Case Insensitive : P: 0.423 || R: 0.579 || F1: 0.489
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.664 || R: 0.755 || F1: 0.707
Case Insensitive : P: 0.681 || R: 0.775 || F1: 0.725
73 Perpres_2008_41
Case Sensitive   : P: 0.739 || R: 0.739 || F1: 0.739
Case Insensitive : P: 0.826 || R: 0.826 || F1: 0.826
74 Permen_PR_2009_03
Case Sensitive   : P: 0.381 || R: 0.381 || F1: 0.381
Case Insensitive : P: 0.381

Case Insensitive : P: 0.721 || R: 0.738 || F1: 0.729
132 UU_1953_14
Case Sensitive   : P: 0.167 || R: 0.174 || F1: 0.17
Case Insensitive : P: 0.167 || R: 0.174 || F1: 0.17
133 Peraturan_Batan_2015_1
Case Sensitive   : P: 0.512 || R: 0.656 || F1: 0.575
Case Insensitive : P: 0.537 || R: 0.688 || F1: 0.603
134 Peraturan_LAN_2017_3
Case Sensitive   : P: 0.583 || R: 0.656 || F1: 0.617
Case Insensitive : P: 0.667 || R: 0.75 || F1: 0.706
135 Perkab_Badung_2013_5
Case Sensitive   : P: 0.3 || R: 0.293 || F1: 0.296
Case Insensitive : P: 0.375 || R: 0.366 || F1: 0.37
136 Peraturan_BNPB_2016_02
Case Sensitive   : P: 0.677 || R: 0.728 || F1: 0.702
Case Insensitive : P: 0.687 || R: 0.739 || F1: 0.712
137 Peraturan_Perpusnas_2018_8
Case Sensitive   : P: 0.431 || R: 0.676 || F1: 0.526
Case Insensitive : P: 0.483 || R: 0.757 || F1: 0.59
138 PP_1998_77
Case Sensitive   : P: 0.63 || R: 0.654 || F1: 0.642
Case Insensitive : P: 0.741 || R: 0.769 || F1: 0.755
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 0

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "57', 'number"
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "2016', 'number"
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLex

179 PP_1961_79
Case Sensitive   : P: 0.393 || R: 0.579 || F1: 0.468
Case Insensitive : P: 0.429 || R: 0.632 || F1: 0.511
180 Peraturan_BNP2TKI_2017_11
Case Sensitive   : P: 0.667 || R: 0.737 || F1: 0.7
Case Insensitive : P: 0.714 || R: 0.789 || F1: 0.75
181 Permen_Tan_2010_45
Case Sensitive   : P: 0.292 || R: 0.525 || F1: 0.375
Case Insensitive : P: 0.319 || R: 0.575 || F1: 0.41
182 Permen_Dikbud_2013_87
Case Sensitive   : P: 0.645 || R: 0.714 || F1: 0.678
Case Insensitive : P: 0.71 || R: 0.786 || F1: 0.746
183 Permen_Perin_2015_48
Case Sensitive   : P: 0.531 || R: 0.667 || F1: 0.591
Case Insensitive : P: 0.571 || R: 0.718 || F1: 0.636
184 Perprov_Sulteng_2002_06
Case Sensitive   : P: 0.111 || R: 0.636 || F1: 0.189
Case Insensitive : P: 0.143 || R: 0.818 || F1: 0.243
185 PP_1990_46
Case Sensitive   : P: 0.516 || R: 0.533 || F1: 0.524
Case Insensitive : P: 0.581 || R: 0.6 || F1: 0.59
186 Permen_Ristekdikti_2016_57
Case Sensitive   : P: 0.475 || R: 0.543 || F1: 0.507
Case Insensitive : P

...

Case Insensitive : P: 0.576 || R: 0.653 || F1: 0.612
2334 Peraturan_Polri_2013_2
Case Sensitive   : P: 0.609 || R: 0.583 || F1: 0.596
Case Insensitive : P: 0.696 || R: 0.667 || F1: 0.681
2335 Peraturan_KY_2016_4
Case Sensitive   : P: 0.562 || R: 0.621 || F1: 0.59
Case Insensitive : P: 0.625 || R: 0.69 || F1: 0.656
2336 Permen_Dag_2016_85
Case Sensitive   : P: 0.618 || R: 0.723 || F1: 0.666
Case Insensitive : P: 0.655 || R: 0.766 || F1: 0.706
2337 Perkab_Purwakarta_2012_6
Case Sensitive   : P: 0.551 || R: 0.608 || F1: 0.578
Case Insensitive : P: 0.57 || R: 0.629 || F1: 0.598
2338 Permen_Dagri_2016_44
Case Sensitive   : P: 0.571 || R: 0.706 || F1: 0.631
Case Insensitive : P: 0.595 || R: 0.735 || F1: 0.658
2339 Perprov_Banten_2005_7
Case Sensitive   : P: 0.84 || R: 0.913 || F1: 0.875
Case Insensitive : P: 0.867 || R: 0.942 || F1: 0.903
2340 Perkab_Karawang_2014_5
Case Sensitive   : P: 0.421 || R: 0.073 || F1: 0.124
Case Insensitive : P: 0.526 || R: 0.092 || F1: 0.157
2341 PP_2016_30
Case 

Case Insensitive : P: 0.64 || R: 0.842 || F1: 0.727
2400 Permen_ESDM_2013_19
Case Sensitive   : P: 0.629 || R: 0.71 || F1: 0.667
Case Insensitive : P: 0.657 || R: 0.742 || F1: 0.697
2401 Peraturan_LKPP_2019_14
Case Sensitive   : P: 0.476 || R: 0.357 || F1: 0.408
Case Insensitive : P: 0.5 || R: 0.375 || F1: 0.429
2402 Permen_Hub_2017_87
Case Sensitive   : P: 0.524 || R: 0.598 || F1: 0.559
Case Insensitive : P: 0.533 || R: 0.609 || F1: 0.568
2403 Peraturan_Batan_2016_4
Case Sensitive   : P: 0.654 || R: 0.773 || F1: 0.709
Case Insensitive : P: 0.692 || R: 0.818 || F1: 0.75
2404 PP_1957_13
Case Sensitive   : P: 0.229 || R: 0.421 || F1: 0.297
Case Insensitive : P: 0.257 || R: 0.474 || F1: 0.333
2405 Peraturan_BPJSTK_2018_1
Case Sensitive   : P: 0.571 || R: 0.645 || F1: 0.606
Case Insensitive : P: 0.6 || R: 0.677 || F1: 0.636
2406 Peraturan_LIPI_2017_1
Case Sensitive   : P: 0.423 || R: 0.611 || F1: 0.5
Case Insensitive : P: 0.462 || R: 0.667 || F1: 0.546
2407 Permen_Keu_2010_19
Case Sensitiv

Case Insensitive : P: 0.462 || R: 0.6 || F1: 0.522
2469 UU_1998_13
Case Sensitive   : P: 0.182 || R: 0.118 || F1: 0.143
Case Insensitive : P: 0.273 || R: 0.176 || F1: 0.214
2470 Peraturan_BNPP_2012_3
Case Sensitive   : P: 0.725 || R: 0.725 || F1: 0.725
Case Insensitive : P: 0.745 || R: 0.745 || F1: 0.745
2471 Permen_KP_2016_30
Case Sensitive   : P: 0.615 || R: 0.667 || F1: 0.64
Case Insensitive : P: 0.667 || R: 0.722 || F1: 0.693
2472 Permen_Sos_2016_4
Case Sensitive   : P: 0.629 || R: 0.737 || F1: 0.679
Case Insensitive : P: 0.652 || R: 0.763 || F1: 0.703
2473 Permen_Keu_2010_64
Case Sensitive   : P: 0.643 || R: 0.711 || F1: 0.675
Case Insensitive : P: 0.69 || R: 0.763 || F1: 0.725
2474 Perpres_2018_107
Case Sensitive   : P: 0.583 || R: 0.667 || F1: 0.622
Case Insensitive : P: 0.625 || R: 0.714 || F1: 0.667
2475 Peraturan_BKKBN_2016_481
Case Sensitive   : P: 0.5 || R: 0.722 || F1: 0.591
Case Insensitive : P: 0.577 || R: 0.833 || F1: 0.682
2476 Peraturan_KY_2015_2
Case Sensitive   : P:

Case Insensitive : P: 0.667 || R: 0.722 || F1: 0.693
2541 Permen_Dagri_2018_48
Case Sensitive   : P: 0.667 || R: 0.722 || F1: 0.693
Case Insensitive : P: 0.718 || R: 0.778 || F1: 0.747
2542 Peraturan_BPOM_2017_13
Case Sensitive   : P: 0.493 || R: 0.712 || F1: 0.583
Case Insensitive : P: 0.507 || R: 0.731 || F1: 0.599
2543 Permen_Hut_2010_12
Case Sensitive   : P: 0.507 || R: 0.627 || F1: 0.561
Case Insensitive : P: 0.521 || R: 0.644 || F1: 0.576
2544 Peraturan_KPU_2017_9
Case Sensitive   : P: 0.5 || R: 0.526 || F1: 0.513
Case Insensitive : P: 0.5 || R: 0.526 || F1: 0.513
2545 Permen_Pora_2017_15
Case Sensitive   : P: 0.698 || R: 0.698 || F1: 0.698
Case Insensitive : P: 0.698 || R: 0.698 || F1: 0.698
2546 Peraturan_MA_2018_6
Case Sensitive   : P: 0.5 || R: 0.621 || F1: 0.554
Case Insensitive : P: 0.556 || R: 0.69 || F1: 0.616
2547 Permen_Kes_2014_72
Case Sensitive   : P: 0.149 || R: 0.636 || F1: 0.241
Case Insensitive : P: 0.191 || R: 0.818 || F1: 0.31
2548 Permen_Hub_2016_2
Case Sensiti

Case Insensitive : P: 0.701 || R: 0.734 || F1: 0.717
2608 Perkab_Indramayu_2005_1
Case Sensitive   : P: 0.4 || R: 0.311 || F1: 0.35
Case Insensitive : P: 0.429 || R: 0.333 || F1: 0.375
2609 Permen_PANRB_2018_25
Case Sensitive   : P: 0.543 || R: 0.613 || F1: 0.576
Case Insensitive : P: 0.6 || R: 0.677 || F1: 0.636
2610 Permen_Humham_2018_04
Case Sensitive   : P: 0.619 || R: 0.605 || F1: 0.612
Case Insensitive : P: 0.643 || R: 0.628 || F1: 0.635
2611 Permen_Humham_2019_8
Case Sensitive   : P: 0.625 || R: 0.714 || F1: 0.667
Case Insensitive : P: 0.688 || R: 0.786 || F1: 0.734
2612 Peraturan_Basarnas_2017_3
Case Sensitive   : P: 0.387 || R: 0.444 || F1: 0.414
Case Insensitive : P: 0.452 || R: 0.519 || F1: 0.483
2613 Permenko_Polhukam_2018_2
Case Sensitive   : P: 0.722 || R: 0.722 || F1: 0.722
Case Insensitive : P: 0.778 || R: 0.778 || F1: 0.778
2614 Permen_Hub_2013_81
Case Sensitive   : P: 0.305 || R: 0.273 || F1: 0.288
Case Insensitive : P: 0.339 || R: 0.303 || F1: 0.32
2615 Perkab_Bantul

In [78]:
test_1('ocl', oc_llama, test_opening, '2', results, 'oc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.725 || R: 0.725 || F1: 0.725
Case Insensitive : P: 0.75 || R: 0.75 || F1: 0.75
1 Permen_KP_2013_5
Case Sensitive   : P: 0.558 || R: 0.667 || F1: 0.608
Case Insensitive : P: 0.605 || R: 0.722 || F1: 0.658
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.591 || R: 0.722 || F1: 0.65
Case Insensitive : P: 0.682 || R: 0.833 || F1: 0.75
3 Permen_Par_2015_14
Case Sensitive   : P: 0.674 || R: 0.674 || F1: 0.674
Case Insensitive : P: 0.721 || R: 0.721 || F1: 0.721
4 Perpres_2019_67
Case Sensitive   : P: 0.607 || R: 0.708 || F1: 0.654
Case Insensitive : P: 0.679 || R: 0.792 || F1: 0.731
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.599 || R: 0.569 || F1: 0.584
Case Insensitive : P: 0.612 || R: 0.581 || F1: 0.596
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.438 || R: 0.571 || F1: 0.496
Case Insensitive : P: 0.469 || R: 0.612 || F1: 0.531
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.66 || R: 0.721 || F1: 0.689
Case Insensitive : P: 0.

72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.693 || R: 0.686 || F1: 0.689
Case Insensitive : P: 0.713 || R: 0.706 || F1: 0.709
73 Perpres_2008_41
Case Sensitive   : P: 0.739 || R: 0.739 || F1: 0.739
Case Insensitive : P: 0.826 || R: 0.826 || F1: 0.826
74 Permen_PR_2009_03
Case Sensitive   : P: 0.276 || R: 0.381 || F1: 0.32
Case Insensitive : P: 0.276 || R: 0.381 || F1: 0.32
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.692 || R: 0.692 || F1: 0.692
Case Insensitive : P: 0.769 || R: 0.769 || F1: 0.769
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.538 || R: 0.731 || F1: 0.62
Case Insensitive : P: 0.56 || R: 0.761 || F1: 0.645
77 Perkab_Sleman_2012_9
Case Sensitive   : P: 0.562 || R: 0.551 || F1: 0.556
Case Insensitive : P: 0.604 || R: 0.592 || F1: 0.598
78 PP_1990_59
Case Sensitive   : P: 0.484 || R: 0.5 || F1: 0.492
Case Insensitive : P: 0.548 || R: 0.567 || F1: 0.557
79 Permen_Agama_2016_21
Case Sensitive   : P: 0.731 || R: 0.679 || F1: 0.704
Case Insensitive : P: 0.769 || R

Case Insensitive : P: 0.739 || R: 0.707 || F1: 0.723
137 Peraturan_Perpusnas_2018_8
Case Sensitive   : P: 0.5 || R: 0.73 || F1: 0.593
Case Insensitive : P: 0.537 || R: 0.784 || F1: 0.637
138 PP_1998_77
Case Sensitive   : P: 0.667 || R: 0.692 || F1: 0.679
Case Insensitive : P: 0.704 || R: 0.731 || F1: 0.717
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 0.605 || R: 0.667 || F1: 0.634
Case Insensitive : P: 0.651 || R: 0.718 || F1: 0.683
140 Permen_Keu_2015_108
Case Sensitive   : P: 0.677 || R: 0.75 || F1: 0.712
Case Insensitive : P: 0.774 || R: 0.857 || F1: 0.813
141 Permen_LHK_2019_13
Case Sensitive   : P: 0.575 || R: 0.535 || F1: 0.554
Case Insensitive : P: 0.625 || R: 0.581 || F1: 0.602
142 PP_1983_17
Case Sensitive   : P: 0.429 || R: 0.444 || F1: 0.436
Case Insensitive : P: 0.5 || R: 0.519 || F1: 0.509
143 Perpres_2015_82
Case Sensitive   : P: 0.714 || R: 0.714 || F1: 0.714
Case Insensitive : P: 0.786 || R: 0.786 || F1: 0.786
144 Permen_Naker_2016_17
Case Sensitive   : P: 0.708 || R:

Case Insensitive : P: 0.613 || R: 0.704 || F1: 0.655
204 Perprov_Papua_2013_14
Case Sensitive   : P: 0.685 || R: 0.679 || F1: 0.682
Case Insensitive : P: 0.694 || R: 0.688 || F1: 0.691
205 Permen_PANRB_2013_32
Case Sensitive   : P: 0.388 || R: 0.441 || F1: 0.413
Case Insensitive : P: 0.418 || R: 0.475 || F1: 0.445
206 Permen_Dagri_2017_3
Case Sensitive   : P: 0.694 || R: 0.694 || F1: 0.694
Case Insensitive : P: 0.75 || R: 0.75 || F1: 0.75
207 UU_2012_8
Case Sensitive   : P: 0.625 || R: 0.588 || F1: 0.606
Case Insensitive : P: 0.625 || R: 0.588 || F1: 0.606
208 Permen_Keu_2010_262
Case Sensitive   : P: 0.192 || R: 0.625 || F1: 0.294
Case Insensitive : P: 0.269 || R: 0.875 || F1: 0.411
209 PP_1998_25
Case Sensitive   : P: 0.438 || R: 0.452 || F1: 0.445
Case Insensitive : P: 0.531 || R: 0.548 || F1: 0.539
210 Perkot_Depok_2011_07
Case Sensitive   : P: 0.136 || R: 0.09 || F1: 0.108
Case Insensitive : P: 0.159 || R: 0.104 || F1: 0.126
211 PP_2012_13
Case Sensitive   : P: 0.742 || R: 0.742 |

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "38', 'number"
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "1980', 'year"
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexic

...

Case Insensitive : P: 0.75 || R: 0.75 || F1: 0.75
2343 Perkab_Mamuju_Utara_2006_14
Case Sensitive   : P: 0.615 || R: 0.653 || F1: 0.633
Case Insensitive : P: 0.654 || R: 0.694 || F1: 0.673
2344 Permen_Keu_2015_221
Case Sensitive   : P: 0.545 || R: 0.72 || F1: 0.62
Case Insensitive : P: 0.606 || R: 0.8 || F1: 0.69
2345 Permen_Keu_2019_119
Case Sensitive   : P: 0.692 || R: 0.726 || F1: 0.709
Case Insensitive : P: 0.723 || R: 0.758 || F1: 0.74
2346 Permen_Tan_2017_12
Case Sensitive   : P: 0.662 || R: 0.7 || F1: 0.68
Case Insensitive : P: 0.689 || R: 0.729 || F1: 0.708
2347 PP_1961_132
Case Sensitive   : P: 0.478 || R: 0.5 || F1: 0.489
Case Insensitive : P: 0.565 || R: 0.591 || F1: 0.578
2348 Perprov_Jabar_2011_20
Case Sensitive   : P: 0.761 || R: 0.794 || F1: 0.777
Case Insensitive : P: 0.789 || R: 0.824 || F1: 0.806
2349 Permen_Dagri_2017_10
Case Sensitive   : P: 0.593 || R: 0.696 || F1: 0.64
Case Insensitive : P: 0.63 || R: 0.739 || F1: 0.68
2350 Permen_Dagri_2017_97
Case Sensitive   : 

2407 Permen_Keu_2010_19
Case Sensitive   : P: 0.548 || R: 0.68 || F1: 0.607
Case Insensitive : P: 0.613 || R: 0.76 || F1: 0.679
2408 Permen_Dikbud_2012_72
Case Sensitive   : P: 0.61 || R: 0.735 || F1: 0.667
Case Insensitive : P: 0.659 || R: 0.794 || F1: 0.72
2409 Perkab_Sinjai_2012_14
Case Sensitive   : P: 0.773 || R: 0.761 || F1: 0.767
Case Insensitive : P: 0.803 || R: 0.791 || F1: 0.797
2410 Permen_Keu_2011_210
Case Sensitive   : P: 0.65 || R: 0.722 || F1: 0.684
Case Insensitive : P: 0.7 || R: 0.778 || F1: 0.737
2411 Peraturan_Bapeten_2019_3
Case Sensitive   : P: 0.467 || R: 0.609 || F1: 0.529
Case Insensitive : P: 0.5 || R: 0.652 || F1: 0.566
2412 Peraturan_Polri_2018_4
Case Sensitive   : P: 0.45 || R: 0.562 || F1: 0.5
Case Insensitive : P: 0.55 || R: 0.688 || F1: 0.611
2413 UU_1953_7
Case Sensitive   : P: 0.364 || R: 0.4 || F1: 0.381
Case Insensitive : P: 0.455 || R: 0.5 || F1: 0.476
2414 Permen_Kes_2016_1
Case Sensitive   : P: 0.719 || R: 0.719 || F1: 0.719
Case Insensitive : P: 0

2480 PP_2003_9
Case Sensitive   : P: 0.333 || R: 0.345 || F1: 0.339
Case Insensitive : P: 0.4 || R: 0.414 || F1: 0.407
2481 Perpres_2017_70
Case Sensitive   : P: 0.65 || R: 0.703 || F1: 0.675
Case Insensitive : P: 0.7 || R: 0.757 || F1: 0.727
2482 PP_1978_10
Case Sensitive   : P: 0.4 || R: 0.435 || F1: 0.417
Case Insensitive : P: 0.48 || R: 0.522 || F1: 0.5
2483 PP_1981_6
Case Sensitive   : P: 0.281 || R: 0.29 || F1: 0.285
Case Insensitive : P: 0.312 || R: 0.323 || F1: 0.317
2484 Permen_Keu_2014_59
Case Sensitive   : P: 0.6 || R: 0.75 || F1: 0.667
Case Insensitive : P: 0.7 || R: 0.875 || F1: 0.778
2485 Peraturan_BPOM_2013_29
Case Sensitive   : P: 0.259 || R: 0.5 || F1: 0.341
Case Insensitive : P: 0.296 || R: 0.571 || F1: 0.39
2486 PP_1961_166
Case Sensitive   : P: 0.24 || R: 0.273 || F1: 0.255
Case Insensitive : P: 0.32 || R: 0.364 || F1: 0.341
2487 Permen_Humham_2016_66
Case Sensitive   : P: 0.625 || R: 0.714 || F1: 0.667
Case Insensitive : P: 0.688 || R: 0.786 || F1: 0.734
2488 PP_20

Case Insensitive : P: 0.673 || R: 0.617 || F1: 0.644
2550 PP_2005_15
Case Sensitive   : P: 0.722 || R: 0.722 || F1: 0.722
Case Insensitive : P: 0.833 || R: 0.833 || F1: 0.833
2551 Perkab_Serdang_Bedagai_2012_14
Case Sensitive   : P: 0.667 || R: 0.667 || F1: 0.667
Case Insensitive : P: 0.706 || R: 0.706 || F1: 0.706
2552 PP_2003_34
Case Sensitive   : P: 0.333 || R: 0.4 || F1: 0.363
Case Insensitive : P: 0.4 || R: 0.48 || F1: 0.436
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.68 || R: 0.68 || F1: 0.68
Case Insensitive : P: 0.72 || R: 0.72 || F1: 0.72
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 0.625 || R: 0.625 || F1: 0.625
Case Insensitive : P: 0.656 || R: 0.656 || F1: 0.656
2555 Peraturan_OJK_2019_13
Case Sensitive   : P: 0.533 || R: 0.667 || F1: 0.593
Case Insensitive : P: 0.6 || R: 0.75 || F1: 0.667
2556 Permen_Kes_2013_75
Case Sensitive   : P: 0.682 || R: 0.75 || F1: 0.714
Case Insensitive : P: 0.727 || R: 0.8 || F1: 0.762
2557 Permen_Dagri_2012_16
Case Sensitive   : P

Case Insensitive : P: 0.742 || R: 0.742 || F1: 0.742
2623 Peraturan_BPJSKES_2018_6
Case Sensitive   : P: 0.692 || R: 0.692 || F1: 0.692
Case Insensitive : P: 0.692 || R: 0.692 || F1: 0.692
2624 Permen_Dikbud_2011_56
Case Sensitive   : P: 0.716 || R: 0.741 || F1: 0.728
Case Insensitive : P: 0.724 || R: 0.75 || F1: 0.737
2625 Permen_Dikbud_2014_36
Case Sensitive   : P: 0.615 || R: 0.706 || F1: 0.657
Case Insensitive : P: 0.667 || R: 0.765 || F1: 0.713
2626 Perkab_Hulu_Sungai_Tengah_2012_2
Case Sensitive   : P: 0.426 || R: 0.517 || F1: 0.467
Case Insensitive : P: 0.454 || R: 0.551 || F1: 0.498
2627 Peraturan_LAN_2016_3
Case Sensitive   : P: 0.714 || R: 0.714 || F1: 0.714
Case Insensitive : P: 0.786 || R: 0.786 || F1: 0.786
2628 Permen_Tan_2013_08
Case Sensitive   : P: 0.69 || R: 0.719 || F1: 0.704
Case Insensitive : P: 0.71 || R: 0.74 || F1: 0.725
2629 Peraturan_OJK_2014_37
Case Sensitive   : P: 0.7 || R: 0.7 || F1: 0.7
Case Insensitive : P: 0.8 || R: 0.8 || F1: 0.8
2630 Permen_Dag_2015_1

In [79]:
test_1('ocp', oc_phi, test_opening, '1', results, 'oc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.625 || R: 0.625 || F1: 0.625
Case Insensitive : P: 0.65 || R: 0.65 || F1: 0.65
1 Permen_KP_2013_5
Case Sensitive   : P: 0.457 || R: 0.583 || F1: 0.512
Case Insensitive : P: 0.5 || R: 0.639 || F1: 0.561
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.545 || R: 0.667 || F1: 0.6
Case Insensitive : P: 0.636 || R: 0.778 || F1: 0.7
3 Permen_Par_2015_14
Case Sensitive   : P: 0.632 || R: 0.558 || F1: 0.593
Case Insensitive : P: 0.658 || R: 0.581 || F1: 0.617
4 Perpres_2019_67
Case Sensitive   : P: 0.571 || R: 0.667 || F1: 0.615
Case Insensitive : P: 0.643 || R: 0.75 || F1: 0.692
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.326 || R: 0.194 || F1: 0.243
Case Insensitive : P: 0.347 || R: 0.206 || F1: 0.259
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.109 || R: 0.122 || F1: 0.115
Case Insensitive : P: 0.145 || R: 0.163 || F1: 0.153
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.612 || R: 0.698 || F1: 0.652
Case Insensitive : P: 0.633 

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "2019', 'tahun"
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "81', 'regulatory_number"
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, i

Case Insensitive : P: 0.708 || R: 0.63 || F1: 0.667
21 Perpres_2012_88
Case Sensitive   : P: 0.733 || R: 0.71 || F1: 0.721
Case Insensitive : P: 0.767 || R: 0.742 || F1: 0.754
22 Permen_Ristekdikti_2016_110
Case Sensitive   : P: 0.538 || R: 0.583 || F1: 0.56
Case Insensitive : P: 0.564 || R: 0.611 || F1: 0.587
23 Perpres_2013_42
Case Sensitive   : P: 0.722 || R: 0.619 || F1: 0.667
Case Insensitive : P: 0.833 || R: 0.714 || F1: 0.769
24 PP_2019_81
Case Sensitive   : P: 0.517 || R: 0.652 || F1: 0.577
Case Insensitive : P: 0.552 || R: 0.696 || F1: 0.616
25 Peraturan_BKN_2019_34
Case Sensitive   : P: 0.618 || R: 0.618 || F1: 0.618
Case Insensitive : P: 0.676 || R: 0.676 || F1: 0.676
26 PP_2015_59
Case Sensitive   : P: 0.667 || R: 0.667 || F1: 0.667
Case Insensitive : P: 0.722 || R: 0.722 || F1: 0.722
27 Perprov_Jabar_2000_3
Case Sensitive   : P: 0.091 || R: 0.5 || F1: 0.154
Case Insensitive : P: 0.114 || R: 0.625 || F1: 0.193
28 Perkot_Denpasar_2006_1
Case Sensitive   : P: 0.136 || R: 0.16

93 PP_1999_88
Case Sensitive   : P: 0.556 || R: 0.588 || F1: 0.572
Case Insensitive : P: 0.611 || R: 0.647 || F1: 0.628
94 UU_2007_38
Case Sensitive   : P: 0.868 || R: 0.805 || F1: 0.835
Case Insensitive : P: 0.895 || R: 0.829 || F1: 0.861
95 Permen_PANRB_2017_25
Case Sensitive   : P: 0.324 || R: 0.16 || F1: 0.214
Case Insensitive : P: 0.378 || R: 0.187 || F1: 0.25
96 Permen_Keu_2015_232
Case Sensitive   : P: 0.711 || R: 0.711 || F1: 0.711
Case Insensitive : P: 0.737 || R: 0.737 || F1: 0.737
97 Permen_Dag_2017_82
Case Sensitive   : P: 0.364 || R: 0.271 || F1: 0.311
Case Insensitive : P: 0.386 || R: 0.288 || F1: 0.33
98 Permen_Dagri_2018_92
Case Sensitive   : P: 0.45 || R: 0.643 || F1: 0.529
Case Insensitive : P: 0.475 || R: 0.679 || F1: 0.559
99 Permen_Desa_2017_23
Case Sensitive   : P: 0.574 || R: 0.562 || F1: 0.568
Case Insensitive : P: 0.574 || R: 0.562 || F1: 0.568
100 PP_2013_55
Case Sensitive   : P: 0.68 || R: 0.708 || F1: 0.694
Case Insensitive : P: 0.76 || R: 0.792 || F1: 0.776

Case Insensitive : P: 0.37 || R: 0.256 || F1: 0.303
161 Permen_Han_2014_83
Case Sensitive   : P: 0.606 || R: 0.714 || F1: 0.656
Case Insensitive : P: 0.636 || R: 0.75 || F1: 0.688
162 Permen_Humham_2015_16
Case Sensitive   : P: 0.545 || R: 0.6 || F1: 0.571
Case Insensitive : P: 0.576 || R: 0.633 || F1: 0.603
163 Perkab_Indramayu_2006_1
Case Sensitive   : P: 0.185 || R: 0.077 || F1: 0.109
Case Insensitive : P: 0.259 || R: 0.108 || F1: 0.152
164 Perkot_Tasikmalaya_2007_6
Case Sensitive   : P: 0.4 || R: 0.125 || F1: 0.19
Case Insensitive : P: 0.45 || R: 0.141 || F1: 0.215
165 Peraturan_OJK_2014_28
Case Sensitive   : P: 0.562 || R: 0.6 || F1: 0.58
Case Insensitive : P: 0.688 || R: 0.733 || F1: 0.71
166 Permen_Par_2014_2
Case Sensitive   : P: 0.553 || R: 0.591 || F1: 0.571
Case Insensitive : P: 0.574 || R: 0.614 || F1: 0.593
167 Perkab_Cilacap_2012_13
Case Sensitive   : P: 0.594 || R: 0.623 || F1: 0.608
Case Insensitive : P: 0.625 || R: 0.656 || F1: 0.64
168 PP_2013_67
Case Sensitive   : P:

...

Case Insensitive : P: 0.721 || R: 0.705 || F1: 0.713
2382 Permen_PR_2012_24
Case Sensitive   : P: 0.794 || R: 0.643 || F1: 0.711
Case Insensitive : P: 0.824 || R: 0.667 || F1: 0.737
2383 Permen_Keu_2011_232
Case Sensitive   : P: 0.583 || R: 0.656 || F1: 0.617
Case Insensitive : P: 0.611 || R: 0.688 || F1: 0.647
2384 Perkab_Ciamis_2011_22
Case Sensitive   : P: 0.25 || R: 0.183 || F1: 0.211
Case Insensitive : P: 0.275 || R: 0.202 || F1: 0.233
2385 Permen_Humham_2019_7
Case Sensitive   : P: 0.588 || R: 0.541 || F1: 0.564
Case Insensitive : P: 0.618 || R: 0.568 || F1: 0.592
2386 Permen_Hub_2017_68
Case Sensitive   : P: 0.484 || R: 0.484 || F1: 0.484
Case Insensitive : P: 0.548 || R: 0.548 || F1: 0.548
2387 PP_2010_50
Case Sensitive   : P: 0.433 || R: 0.684 || F1: 0.53
Case Insensitive : P: 0.5 || R: 0.789 || F1: 0.612
2388 Peraturan_PPATK_2017_20
Case Sensitive   : P: 0.5 || R: 0.606 || F1: 0.548
Case Insensitive : P: 0.55 || R: 0.667 || F1: 0.603
2389 Perkab_Sleman_2001_15
Case Sensitive 

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "2008', 'tahun"
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "2008', 'tahun"


2456 Perkab_Bantul_2008_18
Case Sensitive   : P: 0.185 || R: 0.5 || F1: 0.27
Case Insensitive : P: 0.222 || R: 0.6 || F1: 0.324
2457 Perkot_Bekasi_2013_09
Case Sensitive   : P: 0.333 || R: 0.106 || F1: 0.161
Case Insensitive : P: 0.4 || R: 0.128 || F1: 0.194
2458 Permen_Hut_2012_42
Case Sensitive   : P: 0.644 || R: 0.604 || F1: 0.623
Case Insensitive : P: 0.667 || R: 0.625 || F1: 0.645
2459 Permen_Keu_2019_118
Case Sensitive   : P: 0.627 || R: 0.593 || F1: 0.61
Case Insensitive : P: 0.647 || R: 0.611 || F1: 0.628
2460 Permen_Naker_2018_2
Case Sensitive   : P: 0.559 || R: 0.704 || F1: 0.623
Case Insensitive : P: 0.618 || R: 0.778 || F1: 0.689
2461 Perkab_Way_Kanan_2001_4
Case Sensitive   : P: 0.442 || R: 0.442 || F1: 0.442
Case Insensitive : P: 0.481 || R: 0.481 || F1: 0.481
2462 Perkab_Bulungan_2009_2
Case Sensitive   : P: 0.317 || R: 0.188 || F1: 0.236
Case Insensitive : P: 0.366 || R: 0.217 || F1: 0.272
2463 Permen_PUPR_2015_10
Case Sensitive   : P: 0.615 || R: 0.649 || F1: 0.632
Cas

Case Insensitive : P: 0.559 || R: 0.679 || F1: 0.613
2524 Permen_Dag_2019_16
Case Sensitive   : P: 0.763 || R: 0.763 || F1: 0.763
Case Insensitive : P: 0.816 || R: 0.816 || F1: 0.816
2525 Permen_Keu_2015_237
Case Sensitive   : P: 0.593 || R: 0.533 || F1: 0.561
Case Insensitive : P: 0.63 || R: 0.567 || F1: 0.597
2526 Perprov_Riau_2013_17
Case Sensitive   : P: 0.75 || R: 0.7 || F1: 0.724
Case Insensitive : P: 0.821 || R: 0.767 || F1: 0.793
2527 Permen_PPPA_2010_10
Case Sensitive   : P: 0.121 || R: 0.308 || F1: 0.174
Case Insensitive : P: 0.152 || R: 0.385 || F1: 0.218
2528 Peraturan_BSSN_2016_16
Case Sensitive   : P: 0.364 || R: 0.211 || F1: 0.267
Case Insensitive : P: 0.409 || R: 0.237 || F1: 0.3
2529 Perkab_Musi_Rawas_2005_7
Case Sensitive   : P: 0.208 || R: 0.455 || F1: 0.285
Case Insensitive : P: 0.292 || R: 0.636 || F1: 0.4
2530 Permen_KP_2016_28
Case Sensitive   : P: 0.655 || R: 0.633 || F1: 0.644
Case Insensitive : P: 0.69 || R: 0.667 || F1: 0.678
2531 Peraturan_Ombudsman_2012_9
C

Case Insensitive : P: 0.294 || R: 0.096 || F1: 0.145
2599 Permen_Hut_2010_41
Case Sensitive   : P: 0.5 || R: 0.605 || F1: 0.548
Case Insensitive : P: 0.522 || R: 0.632 || F1: 0.572
2600 PP_2015_69
Case Sensitive   : P: 0.565 || R: 0.722 || F1: 0.634
Case Insensitive : P: 0.652 || R: 0.833 || F1: 0.731
2601 Permen_LH_2012_20
Case Sensitive   : P: 0.536 || R: 0.6 || F1: 0.566
Case Insensitive : P: 0.571 || R: 0.64 || F1: 0.604
2602 UU_1954_76
Case Sensitive   : P: 0.417 || R: 0.357 || F1: 0.385
Case Insensitive : P: 0.5 || R: 0.429 || F1: 0.462
2603 Perkab_Magelang_2010_12
Case Sensitive   : P: 0.467 || R: 0.491 || F1: 0.479
Case Insensitive : P: 0.5 || R: 0.526 || F1: 0.513
2604 Perpres_2016_68
Case Sensitive   : P: 0.619 || R: 0.619 || F1: 0.619
Case Insensitive : P: 0.667 || R: 0.667 || F1: 0.667
2605 Permen_Agama_2015_41
Case Sensitive   : P: 0.55 || R: 0.234 || F1: 0.328
Case Insensitive : P: 0.65 || R: 0.277 || F1: 0.388
2606 Peraturan_BKN_2012_16
Case Sensitive   : P: 0.74 || R: 0

In [80]:
test_1('ocp', oc_phi, test_opening, '2', results, 'oc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.438 || R: 0.175 || F1: 0.25
Case Insensitive : P: 0.5 || R: 0.2 || F1: 0.286
1 Permen_KP_2013_5
Case Sensitive   : P: 0.5 || R: 0.222 || F1: 0.307
Case Insensitive : P: 0.625 || R: 0.278 || F1: 0.385
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.643 || R: 0.5 || F1: 0.563
Case Insensitive : P: 0.786 || R: 0.611 || F1: 0.688
3 Permen_Par_2015_14
Case Sensitive   : P: 0.6 || R: 0.209 || F1: 0.31
Case Insensitive : P: 0.733 || R: 0.256 || F1: 0.379
4 Perpres_2019_67
Case Sensitive   : P: 0.5 || R: 0.583 || F1: 0.538
Case Insensitive : P: 0.571 || R: 0.667 || F1: 0.615
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.61 || R: 0.469 || F1: 0.53
Case Insensitive : P: 0.626 || R: 0.481 || F1: 0.544
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.675 || R: 0.551 || F1: 0.607
Case Insensitive : P: 0.725 || R: 0.592 || F1: 0.652
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.692 || R: 0.628 || F1: 0.658
Case Insensitive : P: 0.718 || R: 

71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.385 || R: 0.526 || F1: 0.445
Case Insensitive : P: 0.385 || R: 0.526 || F1: 0.445
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.69 || R: 0.676 || F1: 0.683
Case Insensitive : P: 0.71 || R: 0.696 || F1: 0.703
73 Perpres_2008_41
Case Sensitive   : P: 0.652 || R: 0.652 || F1: 0.652
Case Insensitive : P: 0.739 || R: 0.739 || F1: 0.739
74 Permen_PR_2009_03
Case Sensitive   : P: 0.276 || R: 0.381 || F1: 0.32
Case Insensitive : P: 0.276 || R: 0.381 || F1: 0.32
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.654 || R: 0.654 || F1: 0.654
Case Insensitive : P: 0.731 || R: 0.731 || F1: 0.731
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.571 || R: 0.716 || F1: 0.635
Case Insensitive : P: 0.583 || R: 0.731 || F1: 0.649
77 Perkab_Sleman_2012_9
Case Sensitive   : P: 0.625 || R: 0.408 || F1: 0.494
Case Insensitive : P: 0.688 || R: 0.449 || F1: 0.543
78 PP_1990_59
Case Sensitive   : P: 0.436 || R: 0.567 || F1: 0.493
Case Insensitive : P: 0.487

Case Insensitive : P: 0.595 || R: 0.61 || F1: 0.602
136 Peraturan_BNPB_2016_02
Case Sensitive   : P: 0.702 || R: 0.641 || F1: 0.67
Case Insensitive : P: 0.714 || R: 0.652 || F1: 0.682
137 Peraturan_Perpusnas_2018_8
Case Sensitive   : P: 0.533 || R: 0.649 || F1: 0.585
Case Insensitive : P: 0.556 || R: 0.676 || F1: 0.61
138 PP_1998_77
Case Sensitive   : P: 0.556 || R: 0.577 || F1: 0.566
Case Insensitive : P: 0.63 || R: 0.654 || F1: 0.642
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 0.6 || R: 0.231 || F1: 0.334
Case Insensitive : P: 0.733 || R: 0.282 || F1: 0.407
140 Permen_Keu_2015_108
Case Sensitive   : P: 0.607 || R: 0.607 || F1: 0.607
Case Insensitive : P: 0.643 || R: 0.643 || F1: 0.643
141 Permen_LHK_2019_13
Case Sensitive   : P: 0.581 || R: 0.419 || F1: 0.487
Case Insensitive : P: 0.645 || R: 0.465 || F1: 0.54
142 PP_1983_17
Case Sensitive   : P: 0.536 || R: 0.556 || F1: 0.546
Case Insensitive : P: 0.607 || R: 0.63 || F1: 0.618
143 Perpres_2015_82
Case Sensitive   : P: 0.536 || R:

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "1961', 'TAHUN"
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#int, Converter=<class 'int'>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
ValueError: invalid literal for int() with base 10: "1961', 'TAHUN"


Case Insensitive : P: 0.77 || R: 0.77 || F1: 0.77
173 Perkab_Tanggamus_2004_8
Case Sensitive   : P: 0.047 || R: 0.4 || F1: 0.084
Case Insensitive : P: 0.059 || R: 0.5 || F1: 0.106
174 Peraturan_Komnas_HAM_2015_003
Case Sensitive   : P: 0.577 || R: 0.682 || F1: 0.625
Case Insensitive : P: 0.615 || R: 0.727 || F1: 0.666
175 Perkot_Sorong_2013_14
Case Sensitive   : P: 0.479 || R: 0.648 || F1: 0.551
Case Insensitive : P: 0.493 || R: 0.667 || F1: 0.567
176 Permen_ATRBPN_2018_12
Case Sensitive   : P: 0.492 || R: 0.66 || F1: 0.564
Case Insensitive : P: 0.492 || R: 0.66 || F1: 0.564
177 Permen_Kes_2012_003
Case Sensitive   : P: 0.577 || R: 0.682 || F1: 0.625
Case Insensitive : P: 0.615 || R: 0.727 || F1: 0.666
178 Permen_Hub_2013_23
Case Sensitive   : P: 0.571 || R: 0.308 || F1: 0.4
Case Insensitive : P: 0.643 || R: 0.346 || F1: 0.45
179 PP_1961_79
Case Sensitive   : P: 0.391 || R: 0.474 || F1: 0.429
Case Insensitive : P: 0.391 || R: 0.474 || F1: 0.429
180 Peraturan_BNP2TKI_2017_11
Case Sensit

...

Case Insensitive : P: 0.613 || R: 0.594 || F1: 0.603
2319 Perkab_Ogan_Komering_Ilir_2010_29
Case Sensitive   : P: 0.5 || R: 0.5 || F1: 0.5
Case Insensitive : P: 0.556 || R: 0.556 || F1: 0.556
2320 Perprov_Riau_2013_15
Case Sensitive   : P: 0.412 || R: 0.424 || F1: 0.418
Case Insensitive : P: 0.471 || R: 0.485 || F1: 0.478
2321 Permen_Han_2014_19
Case Sensitive   : P: 0.625 || R: 0.625 || F1: 0.625
Case Insensitive : P: 0.656 || R: 0.656 || F1: 0.656
2322 Peraturan_BNPP_2011_1
Case Sensitive   : P: 0.706 || R: 0.655 || F1: 0.68
Case Insensitive : P: 0.725 || R: 0.673 || F1: 0.698
2323 Perkab_Cilacap_2013_11
Case Sensitive   : P: 0.558 || R: 0.547 || F1: 0.552
Case Insensitive : P: 0.596 || R: 0.585 || F1: 0.59
2324 Perprov_Jateng_2002_13
Case Sensitive   : P: 0.52 || R: 0.542 || F1: 0.531
Case Insensitive : P: 0.56 || R: 0.583 || F1: 0.571
2325 Perprov_DKI_Jakarta_2018_8
Case Sensitive   : P: 0.703 || R: 0.738 || F1: 0.72
Case Insensitive : P: 0.734 || R: 0.77 || F1: 0.752
2326 Permen_D

Case Insensitive : P: 0.639 || R: 0.667 || F1: 0.653
2390 Peraturan_BNN_2017_2
Case Sensitive   : P: 0.604 || R: 0.659 || F1: 0.63
Case Insensitive : P: 0.625 || R: 0.682 || F1: 0.652
2391 UU_1957_53
Case Sensitive   : P: 0.2 || R: 0.167 || F1: 0.182
Case Insensitive : P: 0.3 || R: 0.25 || F1: 0.273
2392 Peraturan_BNPB_2010_15
Case Sensitive   : P: 0.72 || R: 0.692 || F1: 0.706
Case Insensitive : P: 0.76 || R: 0.731 || F1: 0.745
2393 Permen_Han_2014_56
Case Sensitive   : P: 0.656 || R: 0.656 || F1: 0.656
Case Insensitive : P: 0.719 || R: 0.719 || F1: 0.719
2394 Peraturan_BPOM_2017_12
Case Sensitive   : P: 0.447 || R: 0.457 || F1: 0.452
Case Insensitive : P: 0.468 || R: 0.478 || F1: 0.473
2395 Permen_ESDM_2014_25
Case Sensitive   : P: 0.574 || R: 0.628 || F1: 0.6
Case Insensitive : P: 0.596 || R: 0.651 || F1: 0.622
2396 Permen_Dagri_2016_63
Case Sensitive   : P: 0.571 || R: 0.308 || F1: 0.4
Case Insensitive : P: 0.643 || R: 0.346 || F1: 0.45
2397 Peraturan_BMKG_2014_4
Case Sensitive   :

2453 Perkab_Bengkayang_2005_2
Case Sensitive   : P: 0.711 || R: 0.692 || F1: 0.701
Case Insensitive : P: 0.737 || R: 0.718 || F1: 0.727
2454 Perkab_Banyuwangi_2011_3
Case Sensitive   : P: 0.258 || R: 0.523 || F1: 0.346
Case Insensitive : P: 0.273 || R: 0.554 || F1: 0.366
2455 Permen_Ristekdikti_2019_7
Case Sensitive   : P: 0.535 || R: 0.59 || F1: 0.561
Case Insensitive : P: 0.558 || R: 0.615 || F1: 0.585
2456 Perkab_Bantul_2008_18
Case Sensitive   : P: 0.057 || R: 0.5 || F1: 0.102
Case Insensitive : P: 0.08 || R: 0.7 || F1: 0.144
2457 Perkot_Bekasi_2013_09
Case Sensitive   : P: 0.58 || R: 0.543 || F1: 0.561
Case Insensitive : P: 0.591 || R: 0.553 || F1: 0.571
2458 Permen_Hut_2012_42
Case Sensitive   : P: 0.634 || R: 0.542 || F1: 0.584
Case Insensitive : P: 0.659 || R: 0.562 || F1: 0.607
2459 Permen_Keu_2019_118
Case Sensitive   : P: 0.545 || R: 0.667 || F1: 0.6
Case Insensitive : P: 0.561 || R: 0.685 || F1: 0.617
2460 Permen_Naker_2018_2
Case Sensitive   : P: 0.6 || R: 0.333 || F1: 0.4

Case Insensitive : P: 0.746 || R: 0.746 || F1: 0.746
2517 Permen_ESDM_2016_16
Case Sensitive   : P: 0.66 || R: 0.717 || F1: 0.687
Case Insensitive : P: 0.7 || R: 0.761 || F1: 0.729
2518 Perkot_Mataram_2009_3
Case Sensitive   : P: 0.539 || R: 0.562 || F1: 0.55
Case Insensitive : P: 0.566 || R: 0.589 || F1: 0.577
2519 Perkot_Tasikmalaya_2008_9
Case Sensitive   : P: 0.621 || R: 0.631 || F1: 0.626
Case Insensitive : P: 0.636 || R: 0.646 || F1: 0.641
2520 Permen_Keu_2016_231
Case Sensitive   : P: 0.5 || R: 0.522 || F1: 0.511
Case Insensitive : P: 0.5 || R: 0.522 || F1: 0.511
2521 Peraturan_BMKG_2015_23
Case Sensitive   : P: 0.328 || R: 0.525 || F1: 0.404
Case Insensitive : P: 0.328 || R: 0.525 || F1: 0.404
2522 Permen_Keu_2018_34
Case Sensitive   : P: 0.471 || R: 0.471 || F1: 0.471
Case Insensitive : P: 0.529 || R: 0.529 || F1: 0.529
2523 Permen_Dag_2019_41
Case Sensitive   : P: 0.5 || R: 0.464 || F1: 0.481
Case Insensitive : P: 0.519 || R: 0.482 || F1: 0.5
2524 Permen_Dag_2019_16
Case Sens

Case Insensitive : P: 0.49 || R: 0.649 || F1: 0.558
2582 Peraturan_Polri_2008_8
Case Sensitive   : P: 0.562 || R: 0.281 || F1: 0.375
Case Insensitive : P: 0.625 || R: 0.312 || F1: 0.416
2583 Permen_KP_2019_4
Case Sensitive   : P: 0.489 || R: 0.59 || F1: 0.535
Case Insensitive : P: 0.532 || R: 0.641 || F1: 0.581
2584 Permen_Hut_2009_33
Case Sensitive   : P: 0.509 || R: 0.443 || F1: 0.474
Case Insensitive : P: 0.528 || R: 0.459 || F1: 0.491
2585 Perprov_Riau_2013_7
Case Sensitive   : P: 0.658 || R: 0.685 || F1: 0.671
Case Insensitive : P: 0.684 || R: 0.712 || F1: 0.698
2586 Permen_Dagri_2018_59
Case Sensitive   : P: 0.354 || R: 0.607 || F1: 0.447
Case Insensitive : P: 0.375 || R: 0.643 || F1: 0.474
2587 Perpres_2015_149
Case Sensitive   : P: 0.588 || R: 0.698 || F1: 0.638
Case Insensitive : P: 0.627 || R: 0.744 || F1: 0.681
2588 PP_2006_10
Case Sensitive   : P: 0.625 || R: 0.625 || F1: 0.625
Case Insensitive : P: 0.656 || R: 0.656 || F1: 0.656
2589 Perkot_Sorong_2013_12
Case Sensitive   

# Body

In [92]:
results = pd.DataFrame()
results = pd.DataFrame(columns=['regulatory'
                                , 'bcg_s_p_1'
                                , 'bcg_s_r_1'
                                , 'bcg_s_f1_1'
                                , 'bcg_s_p_2'
                                , 'bcg_s_r_2'
                                , 'bcg_s_f1_2'
                                , 'bcl_s_p_1'
                                , 'bcl_s_r_1'
                                , 'bcl_s_f1_1'
                                , 'bcl_s_p_2'
                                , 'bcl_s_r_2'
                                , 'bcl_s_f1_2'
                                , 'bcp_s_p_1'
                                , 'bcp_s_r_1'
                                , 'bcp_s_f1_1'
                                , 'bcp_s_p_2'
                                , 'bcp_s_r_2'
                                , 'bcp_s_f1_2'
                                , 'bcg_i_p_1'
                                , 'bcg_i_r_1'
                                , 'bcg_i_f1_1'
                                , 'bcg_i_p_2'
                                , 'bcg_i_r_2'
                                , 'bcg_i_f1_2'
                                , 'bcl_i_p_1'
                                , 'bcl_i_r_1'
                                , 'bcl_i_f1_1'
                                , 'bcl_i_p_2'
                                , 'bcl_i_r_2'
                                , 'bcl_i_f1_2'
                                , 'bcp_i_p_1'
                                , 'bcp_i_r_1'
                                , 'bcp_i_f1_1'
                                , 'bcp_i_p_2'
                                , 'bcp_i_r_2'
                                , 'bcp_i_f1_2'
                               ])

In [93]:
test_body_name = "dataset-surface-info/body-struktur/body-struktur-1"
test_body = load_from_disk(test_body_name)

In [99]:
bc_gemma = pd.read_csv('results/new/BC_gemma_post.csv')
bc_llama = pd.read_csv('results/new/BC_llama_post.csv')
bc_phi = pd.read_csv('results/new/BC_phi_post.csv')

In [96]:
test_1('bcg', bc_gemma, test_body, '1', results, 'bc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.947 || R: 0.667 || F1: 0.783
Case Insensitive : P: 0.947 || R: 0.667 || F1: 0.783
1 Permen_KP_2013_5
Case Sensitive   : P: 1.0 || R: 0.658 || F1: 0.794
Case Insensitive : P: 1.0 || R: 0.658 || F1: 0.794
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.963 || R: 0.778 || F1: 0.861
Case Insensitive : P: 0.975 || R: 0.788 || F1: 0.872
3 Permen_Par_2015_14
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
4 Perpres_2019_67
Case Sensitive   : P: 1.0 || R: 0.754 || F1: 0.86
Case Insensitive : P: 1.0 || R: 0.754 || F1: 0.86
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.413 || R: 0.143 || F1: 0.212
Case Insensitive : P: 0.413 || R: 0.143 || F1: 0.212
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.939 || R: 0.66 || F1: 0.775
Case Insensitive : P: 0.939 || R: 0.66 || F1: 0.775
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.979 || R: 0.643 || F1: 0.776
Case Insensitive : P: 0.979 || R: 0.64

69 PP_2018_49
Case Sensitive   : P: 1.0 || R: 0.312 || F1: 0.476
Case Insensitive : P: 1.0 || R: 0.312 || F1: 0.476
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.848 || R: 0.629 || F1: 0.722
Case Insensitive : P: 0.848 || R: 0.629 || F1: 0.722
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.492 || R: 0.278 || F1: 0.355
Case Insensitive : P: 0.492 || R: 0.278 || F1: 0.355
73 Perpres_2008_41
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
74 Permen_PR_2009_03
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.832 || R: 0.633 || F1: 0.719
Case Insensitive : P: 0.832 || R: 0.633 || F1: 0.719
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.895 || R: 0.667 || F1: 0.764
Case Insensitive : P: 0.895 || R: 0.667 || F1:

136 Peraturan_BNPB_2016_02
Case Sensitive   : P: 0.357 || R: 0.12 || F1: 0.18
Case Insensitive : P: 0.357 || R: 0.12 || F1: 0.18
137 Peraturan_Perpusnas_2018_8
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
138 PP_1998_77
Case Sensitive   : P: 0.98 || R: 0.778 || F1: 0.867
Case Insensitive : P: 1.0 || R: 0.794 || F1: 0.885
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
140 Permen_Keu_2015_108
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
141 Permen_LHK_2019_13
Case Sensitive   : P: 0.983 || R: 0.792 || F1: 0.877
Case Insensitive : P: 1.0 || R: 0.806 || F1: 0.893
142 PP_1983_17
Case Sensitive   : P: 0.948 || R: 0.77 || F1: 0.85
Case Insensitive : P: 0.955 || R: 0.776 || F1: 0.856
143 Perpres_2015_82
Case Sensitive   : P: 0.891 || R: 0.778 || F1: 0.831
Case Insensitive : P: 0.909 || R: 0.794 || F1: 0.848
144 Per

Case Insensitive : P: 0.908 || R: 0.621 || F1: 0.738
206 Permen_Dagri_2017_3
Case Sensitive   : P: 0.609 || R: 0.467 || F1: 0.529
Case Insensitive : P: 0.609 || R: 0.467 || F1: 0.529
207 UU_2012_8
Case Sensitive   : P: 0.503 || R: 0.055 || F1: 0.099
Case Insensitive : P: 0.503 || R: 0.055 || F1: 0.099
208 Permen_Keu_2010_262
Case Sensitive   : P: 1.0 || R: 0.747 || F1: 0.855
Case Insensitive : P: 1.0 || R: 0.747 || F1: 0.855
209 PP_1998_25
Case Sensitive   : P: 1.0 || R: 0.792 || F1: 0.884
Case Insensitive : P: 1.0 || R: 0.792 || F1: 0.884
210 Perkot_Depok_2011_07
Case Sensitive   : P: 0.962 || R: 0.662 || F1: 0.784
Case Insensitive : P: 0.962 || R: 0.662 || F1: 0.784
211 PP_2012_13
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
212 Permen_Dikbud_2011_50
Case Sensitive   : P: 1.0 || R: 0.739 || F1: 0.85
Case Insensitive : P: 1.0 || R: 0.739 || F1: 0.85
213 Permen_LH_2012_10
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensit

Case Insensitive : P: 0.838 || R: 0.653 || F1: 0.734
274 UU_1999_11
Case Sensitive   : P: 0.964 || R: 0.75 || F1: 0.844
Case Insensitive : P: 0.964 || R: 0.75 || F1: 0.844
275 Peraturan_BPS_2019_1
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
276 Permen_PU_2013_11
Case Sensitive   : P: 0.867 || R: 0.788 || F1: 0.826
Case Insensitive : P: 0.867 || R: 0.788 || F1: 0.826
277 Perkot_Tangerang_2009_3
Case Sensitive   : P: 0.611 || R: 0.566 || F1: 0.588
Case Insensitive : P: 0.619 || R: 0.574 || F1: 0.596
278 Permen_Hub_2018_110
Case Sensitive   : P: 0.988 || R: 0.563 || F1: 0.717
Case Insensitive : P: 0.988 || R: 0.563 || F1: 0.717
279 Peraturan_BKPM_2009_5
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
280 Permen_Dag_2012_82
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
281 Peraturan_OJK_2018_32
Case Sensitive   : P: 1.0 || R: 0.571 || F

...

2346 Permen_Tan_2017_12
Case Sensitive   : P: 0.981 || R: 0.722 || F1: 0.832
Case Insensitive : P: 1.0 || R: 0.736 || F1: 0.848
2347 PP_1961_132
Case Sensitive   : P: 0.491 || R: 0.491 || F1: 0.491
Case Insensitive : P: 0.491 || R: 0.491 || F1: 0.491
2348 Perprov_Jabar_2011_20
Case Sensitive   : P: 0.981 || R: 0.831 || F1: 0.9
Case Insensitive : P: 0.981 || R: 0.831 || F1: 0.9
2349 Permen_Dagri_2017_10
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2350 Permen_Dagri_2017_97
Case Sensitive   : P: 0.955 || R: 0.667 || F1: 0.785
Case Insensitive : P: 0.955 || R: 0.667 || F1: 0.785
2351 PP_2018_32
Case Sensitive   : P: 0.532 || R: 0.255 || F1: 0.345
Case Insensitive : P: 0.532 || R: 0.255 || F1: 0.345
2352 UU_2002_27
Case Sensitive   : P: 0.719 || R: 0.651 || F1: 0.683
Case Insensitive : P: 0.737 || R: 0.667 || F1: 0.7
2353 Permen_PUPR_2015_01
Case Sensitive   : P: 0.672 || R: 0.59 || F1: 0.628
Case Insensitive : P: 0.672 || R: 0.59 || F1:

2412 Peraturan_Polri_2018_4
Case Sensitive   : P: 0.806 || R: 0.643 || F1: 0.715
Case Insensitive : P: 0.821 || R: 0.655 || F1: 0.729
2413 UU_1953_7
Case Sensitive   : P: 0.807 || R: 0.28 || F1: 0.416
Case Insensitive : P: 0.807 || R: 0.28 || F1: 0.416
2414 Permen_Kes_2016_1
Case Sensitive   : P: 1.0 || R: 0.762 || F1: 0.865
Case Insensitive : P: 1.0 || R: 0.762 || F1: 0.865
2415 Perkot_Tasikmalaya_2007_8
Case Sensitive   : P: 0.517 || R: 0.412 || F1: 0.459
Case Insensitive : P: 0.525 || R: 0.419 || F1: 0.466
2416 PP_1994_8
Case Sensitive   : P: 0.722 || R: 0.765 || F1: 0.743
Case Insensitive : P: 0.722 || R: 0.765 || F1: 0.743
2417 Permen_Hub_2018_27
Case Sensitive   : P: 0.779 || R: 0.267 || F1: 0.398
Case Insensitive : P: 0.779 || R: 0.267 || F1: 0.398
2418 PP_1996_14
Case Sensitive   : P: 1.0 || R: 0.762 || F1: 0.865
Case Insensitive : P: 1.0 || R: 0.762 || F1: 0.865
2419 Peraturan_LKPP_2018_11
Case Sensitive   : P: 0.754 || R: 0.406 || F1: 0.528
Case Insensitive : P: 0.754 || R: 0

2481 Perpres_2017_70
Case Sensitive   : P: 1.0 || R: 0.765 || F1: 0.867
Case Insensitive : P: 1.0 || R: 0.765 || F1: 0.867
2482 PP_1978_10
Case Sensitive   : P: 0.92 || R: 0.767 || F1: 0.837
Case Insensitive : P: 0.92 || R: 0.767 || F1: 0.837
2483 PP_1981_6
Case Sensitive   : P: 0.875 || R: 0.667 || F1: 0.757
Case Insensitive : P: 0.875 || R: 0.667 || F1: 0.757
2484 Permen_Keu_2014_59
Case Sensitive   : P: 0.986 || R: 0.763 || F1: 0.86
Case Insensitive : P: 1.0 || R: 0.774 || F1: 0.873
2485 Peraturan_BPOM_2013_29
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2486 PP_1961_166
Case Sensitive   : P: 0.333 || R: 0.667 || F1: 0.444
Case Insensitive : P: 0.333 || R: 0.667 || F1: 0.444
2487 Permen_Humham_2016_66
Case Sensitive   : P: 0.962 || R: 0.806 || F1: 0.877
Case Insensitive : P: 0.962 || R: 0.806 || F1: 0.877
2488 PP_2007_62
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2489 Permen_D

2549 Permen_PPPA_2015_9
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2550 PP_2005_15
Case Sensitive   : P: 0.768 || R: 0.285 || F1: 0.416
Case Insensitive : P: 0.768 || R: 0.285 || F1: 0.416
2551 Perkab_Serdang_Bedagai_2012_14
Case Sensitive   : P: 1.0 || R: 0.571 || F1: 0.727
Case Insensitive : P: 1.0 || R: 0.571 || F1: 0.727
2552 PP_2003_34
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.777 || R: 0.51 || F1: 0.616
Case Insensitive : P: 0.777 || R: 0.51 || F1: 0.616
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2555 Peraturan_OJK_2019_13
Case Sensitive   : P: 0.989 || R: 0.733 || F1: 0.842
Case Insensitive : P: 1.0 || R: 0.742 || F1: 0.852
2556 Permen_Kes_2013_75
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || 

Case Insensitive : P: 0.609 || R: 0.139 || F1: 0.226
2617 PP_1961_163
Case Sensitive   : P: 0.25 || R: 0.333 || F1: 0.286
Case Insensitive : P: 0.25 || R: 0.333 || F1: 0.286
2618 PP_2008_69
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2619 Permen_Han_2014_18
Case Sensitive   : P: 1.0 || R: 0.748 || F1: 0.856
Case Insensitive : P: 1.0 || R: 0.748 || F1: 0.856
2620 PP_2002_60
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2621 Permen_Nakertrans_2009_22
Case Sensitive   : P: 0.989 || R: 0.746 || F1: 0.85
Case Insensitive : P: 0.989 || R: 0.746 || F1: 0.85
2622 Peraturan_LAN_2017_2
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2623 Peraturan_BPJSKES_2018_6
Case Sensitive   : P: 0.615 || R: 0.413 || F1: 0.494
Case Insensitive : P: 0.615 || R: 0.413 || F1: 0.494
2624 Permen_Dikbud_2011_56
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
C

In [97]:
test_1('bcg', bc_gemma, test_body, '2', results, 'bc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.947 || R: 0.667 || F1: 0.783
Case Insensitive : P: 0.947 || R: 0.667 || F1: 0.783
1 Permen_KP_2013_5
Case Sensitive   : P: 1.0 || R: 0.658 || F1: 0.794
Case Insensitive : P: 1.0 || R: 0.658 || F1: 0.794
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.975 || R: 0.788 || F1: 0.872
Case Insensitive : P: 0.975 || R: 0.788 || F1: 0.872
3 Permen_Par_2015_14
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
4 Perpres_2019_67
Case Sensitive   : P: 1.0 || R: 0.754 || F1: 0.86
Case Insensitive : P: 1.0 || R: 0.754 || F1: 0.86
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.552 || R: 0.183 || F1: 0.275
Case Insensitive : P: 0.552 || R: 0.183 || F1: 0.275
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.939 || R: 0.66 || F1: 0.775
Case Insensitive : P: 0.939 || R: 0.66 || F1: 0.775
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.908 || R: 0.559 || F1: 0.692
Case Insensitive : P: 0.916 || R: 0.56

69 PP_2018_49
Case Sensitive   : P: 1.0 || R: 0.312 || F1: 0.476
Case Insensitive : P: 1.0 || R: 0.312 || F1: 0.476
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.848 || R: 0.629 || F1: 0.722
Case Insensitive : P: 0.848 || R: 0.629 || F1: 0.722
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.962 || R: 0.543 || F1: 0.694
Case Insensitive : P: 0.962 || R: 0.543 || F1: 0.694
73 Perpres_2008_41
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
74 Permen_PR_2009_03
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.832 || R: 0.633 || F1: 0.719
Case Insensitive : P: 0.832 || R: 0.633 || F1: 0.719
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.895 || R: 0.667 || F1: 0.764
Case Insensitive : P: 0.895 || R: 0.667 || F1:

Case Insensitive : P: 1.0 || R: 0.794 || F1: 0.885
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
140 Permen_Keu_2015_108
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
141 Permen_LHK_2019_13
Case Sensitive   : P: 0.983 || R: 0.792 || F1: 0.877
Case Insensitive : P: 1.0 || R: 0.806 || F1: 0.893
142 PP_1983_17
Case Sensitive   : P: 0.948 || R: 0.77 || F1: 0.85
Case Insensitive : P: 0.955 || R: 0.776 || F1: 0.856
143 Perpres_2015_82
Case Sensitive   : P: 0.891 || R: 0.778 || F1: 0.831
Case Insensitive : P: 0.909 || R: 0.794 || F1: 0.848
144 Permen_Naker_2016_17
Case Sensitive   : P: 0.992 || R: 0.765 || F1: 0.864
Case Insensitive : P: 0.992 || R: 0.765 || F1: 0.864
145 Permen_Hub_2015_114
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
146 Perkab_Banyuwangi_2010_8
Case Sensitive   : P: 0.978 || R: 0.781 || F1: 0.8

207 UU_2012_8
Case Sensitive   : P: 0.524 || R: 0.05 || F1: 0.091
Case Insensitive : P: 0.524 || R: 0.05 || F1: 0.091
208 Permen_Keu_2010_262
Case Sensitive   : P: 1.0 || R: 0.747 || F1: 0.855
Case Insensitive : P: 1.0 || R: 0.747 || F1: 0.855
209 PP_1998_25
Case Sensitive   : P: 1.0 || R: 0.792 || F1: 0.884
Case Insensitive : P: 1.0 || R: 0.792 || F1: 0.884
210 Perkot_Depok_2011_07
Case Sensitive   : P: 0.962 || R: 0.662 || F1: 0.784
Case Insensitive : P: 0.962 || R: 0.662 || F1: 0.784
211 PP_2012_13
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
212 Permen_Dikbud_2011_50
Case Sensitive   : P: 1.0 || R: 0.739 || F1: 0.85
Case Insensitive : P: 1.0 || R: 0.739 || F1: 0.85
213 Permen_LH_2012_10
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
214 Permen_PANRB_2015_12
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
215 Permen_KP_2016_6
Case 

Case Insensitive : P: 0.964 || R: 0.75 || F1: 0.844
275 Peraturan_BPS_2019_1
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
276 Permen_PU_2013_11
Case Sensitive   : P: 0.867 || R: 0.788 || F1: 0.826
Case Insensitive : P: 0.867 || R: 0.788 || F1: 0.826
277 Perkot_Tangerang_2009_3
Case Sensitive   : P: 0.836 || R: 0.787 || F1: 0.811
Case Insensitive : P: 0.844 || R: 0.794 || F1: 0.818
278 Permen_Hub_2018_110
Case Sensitive   : P: 0.988 || R: 0.563 || F1: 0.717
Case Insensitive : P: 0.988 || R: 0.563 || F1: 0.717
279 Peraturan_BKPM_2009_5
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
280 Permen_Dag_2012_82
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
281 Peraturan_OJK_2018_32
Case Sensitive   : P: 1.0 || R: 0.571 || F1: 0.727
Case Insensitive : P: 1.0 || R: 0.571 || F1: 0.727
282 Perkot_Binjai_2000_5
Case Sensitive   : P: 0.955 || R: 0

...

Case Insensitive : P: 1.0 || R: 0.769 || F1: 0.869
2320 Perprov_Riau_2013_15
Case Sensitive   : P: 0.444 || R: 0.192 || F1: 0.268
Case Insensitive : P: 0.444 || R: 0.192 || F1: 0.268
2321 Permen_Han_2014_19
Case Sensitive   : P: 1.0 || R: 0.567 || F1: 0.724
Case Insensitive : P: 1.0 || R: 0.567 || F1: 0.724
2322 Peraturan_BNPP_2011_1
Case Sensitive   : P: 1.0 || R: 0.69 || F1: 0.817
Case Insensitive : P: 1.0 || R: 0.69 || F1: 0.817
2323 Perkab_Cilacap_2013_11
Case Sensitive   : P: 0.891 || R: 0.788 || F1: 0.836
Case Insensitive : P: 0.891 || R: 0.788 || F1: 0.836
2324 Perprov_Jateng_2002_13
Case Sensitive   : P: 0.918 || R: 0.795 || F1: 0.852
Case Insensitive : P: 0.927 || R: 0.803 || F1: 0.861
2325 Perprov_DKI_Jakarta_2018_8
Case Sensitive   : P: 0.4 || R: 0.615 || F1: 0.485
Case Insensitive : P: 0.4 || R: 0.615 || F1: 0.485
2326 Permen_Dagri_2016_31
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2327 Perkab_Garut_2009_5
Case Sensitiv

2386 Permen_Hub_2017_68
Case Sensitive   : P: 0.895 || R: 0.783 || F1: 0.835
Case Insensitive : P: 0.895 || R: 0.783 || F1: 0.835
2387 PP_2010_50
Case Sensitive   : P: 0.833 || R: 0.667 || F1: 0.741
Case Insensitive : P: 0.833 || R: 0.667 || F1: 0.741
2388 Peraturan_PPATK_2017_20
Case Sensitive   : P: 1.0 || R: 0.778 || F1: 0.875
Case Insensitive : P: 1.0 || R: 0.778 || F1: 0.875
2389 Perkab_Sleman_2001_15
Case Sensitive   : P: 0.933 || R: 0.563 || F1: 0.702
Case Insensitive : P: 0.933 || R: 0.563 || F1: 0.702
2390 Peraturan_BNN_2017_2
Case Sensitive   : P: 0.395 || R: 0.423 || F1: 0.409
Case Insensitive : P: 0.395 || R: 0.423 || F1: 0.409
2391 UU_1957_53
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2392 Peraturan_BNPB_2010_15
Case Sensitive   : P: 0.071 || R: 0.333 || F1: 0.117
Case Insensitive : P: 0.071 || R: 0.333 || F1: 0.117
2393 Permen_Han_2014_56
Case Sensitive   : P: 0.886 || R: 0.765 || F1: 0.821
Case Insensitive : P: 0.886

Case Insensitive : P: 0.755 || R: 0.72 || F1: 0.737
2454 Perkab_Banyuwangi_2011_3
Case Sensitive   : P: 0.713 || R: 0.359 || F1: 0.478
Case Insensitive : P: 0.713 || R: 0.359 || F1: 0.478
2455 Permen_Ristekdikti_2019_7
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2456 Perkab_Bantul_2008_18
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2457 Perkot_Bekasi_2013_09
Case Sensitive   : P: 0.971 || R: 0.573 || F1: 0.721
Case Insensitive : P: 0.971 || R: 0.573 || F1: 0.721
2458 Permen_Hut_2012_42
Case Sensitive   : P: 0.906 || R: 0.725 || F1: 0.805
Case Insensitive : P: 0.906 || R: 0.725 || F1: 0.805
2459 Permen_Keu_2019_118
Case Sensitive   : P: 0.933 || R: 0.667 || F1: 0.778
Case Insensitive : P: 0.933 || R: 0.667 || F1: 0.778
2460 Permen_Naker_2018_2
Case Sensitive   : P: 1.0 || R: 0.812 || F1: 0.896
Case Insensitive : P: 1.0 || R: 0.812 || F1: 0.896
2461 Perkab_Way_Kanan_2001_4
Case Sensitive  

2520 Permen_Keu_2016_231
Case Sensitive   : P: 0.838 || R: 0.733 || F1: 0.782
Case Insensitive : P: 0.848 || R: 0.742 || F1: 0.791
2521 Peraturan_BMKG_2015_23
Case Sensitive   : P: 0.781 || R: 0.684 || F1: 0.729
Case Insensitive : P: 0.781 || R: 0.684 || F1: 0.729
2522 Permen_Keu_2018_34
Case Sensitive   : P: 0.891 || R: 0.628 || F1: 0.737
Case Insensitive : P: 0.899 || R: 0.634 || F1: 0.744
2523 Permen_Dag_2019_41
Case Sensitive   : P: 1.0 || R: 0.738 || F1: 0.849
Case Insensitive : P: 1.0 || R: 0.738 || F1: 0.849
2524 Permen_Dag_2019_16
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2525 Permen_Keu_2015_237
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2526 Perprov_Riau_2013_17
Case Sensitive   : P: 0.818 || R: 0.281 || F1: 0.418
Case Insensitive : P: 0.818 || R: 0.281 || F1: 0.418
2527 Permen_PPPA_2010_10
Case Sensitive   : P: 0.625 || R: 0.667 || F1: 0.645
Case Insensitive : P: 0.

2590 Perkab_Sleman_2001_8
Case Sensitive   : P: 0.985 || R: 0.678 || F1: 0.803
Case Insensitive : P: 0.985 || R: 0.678 || F1: 0.803
2591 Peraturan_LAN_2015_42
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2592 Peraturan_LAN_2016_5
Case Sensitive   : P: 0.043 || R: 0.333 || F1: 0.076
Case Insensitive : P: 0.043 || R: 0.333 || F1: 0.076
2593 Permen_Dagri_2011_11
Case Sensitive   : P: 1.0 || R: 0.743 || F1: 0.853
Case Insensitive : P: 1.0 || R: 0.743 || F1: 0.853
2594 Perkab_Ponorogo_2011_4
Case Sensitive   : P: 0.965 || R: 0.784 || F1: 0.865
Case Insensitive : P: 0.965 || R: 0.784 || F1: 0.865
2595 Permen_ESDM_2009_08
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2596 UU_2010_8
Case Sensitive   : P: 0.815 || R: 0.313 || F1: 0.452
Case Insensitive : P: 0.815 || R: 0.313 || F1: 0.452
2597 Perkab_Bantul_2008_15
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0

In [100]:
test_1('bcl', bc_llama, test_body, '1', results, 'bc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
1 Permen_KP_2013_5
Case Sensitive   : P: 0.829 || R: 0.482 || F1: 0.61
Case Insensitive : P: 0.829 || R: 0.482 || F1: 0.61
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.797 || R: 0.596 || F1: 0.682
Case Insensitive : P: 0.797 || R: 0.596 || F1: 0.682
3 Permen_Par_2015_14
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
4 Perpres_2019_67
Case Sensitive   : P: 1.0 || R: 0.754 || F1: 0.86
Case Insensitive : P: 1.0 || R: 0.754 || F1: 0.86
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.633 || R: 0.218 || F1: 0.324
Case Insensitive : P: 0.633 || R: 0.218 || F1: 0.324
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.574 || R: 0.287 || F1: 0.383
Case Insensitive : P: 0.574 || R: 0.287 || F1: 0.383
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.727 || R: 0.3 || F1: 0.425
Case Insensitive : P: 0.727 || R: 0.3 || F1: 0.425
8 Permen_

69 PP_2018_49
Case Sensitive   : P: 0.341 || R: 0.032 || F1: 0.059
Case Insensitive : P: 0.341 || R: 0.032 || F1: 0.059
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.416 || R: 0.258 || F1: 0.318
Case Insensitive : P: 0.416 || R: 0.258 || F1: 0.318
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.813 || R: 0.372 || F1: 0.51
Case Insensitive : P: 0.813 || R: 0.372 || F1: 0.51
73 Perpres_2008_41
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
74 Permen_PR_2009_03
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.629 || R: 0.433 || F1: 0.513
Case Insensitive : P: 0.629 || R: 0.433 || F1: 0.513
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
77 Perkab_Sleman_2012_9
Case Se

146 Perkab_Banyuwangi_2010_8
Case Sensitive   : P: 0.782 || R: 0.509 || F1: 0.617
Case Insensitive : P: 0.782 || R: 0.509 || F1: 0.617
147 PP_1985_33
Case Sensitive   : P: 0.968 || R: 0.606 || F1: 0.745
Case Insensitive : P: 0.968 || R: 0.606 || F1: 0.745
148 Permen_Keu_2012_89
Case Sensitive   : P: 0.944 || R: 0.739 || F1: 0.829
Case Insensitive : P: 0.944 || R: 0.739 || F1: 0.829
149 Permen_Hut_2011_26
Case Sensitive   : P: 0.974 || R: 0.714 || F1: 0.824
Case Insensitive : P: 0.974 || R: 0.714 || F1: 0.824
150 Peraturan_BKPM_2011_11
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
151 Permen_PDT_2014_5
Case Sensitive   : P: 1.0 || R: 0.74 || F1: 0.851
Case Insensitive : P: 1.0 || R: 0.74 || F1: 0.851
152 Permen_Hub_2016_100
Case Sensitive   : P: 1.0 || R: 0.688 || F1: 0.815
Case Insensitive : P: 1.0 || R: 0.688 || F1: 0.815
153 Perpres_2013_74
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
154 Permen_

Case Insensitive : P: 0.99 || R: 0.589 || F1: 0.739
218 Peraturan_BPOM_2013_24
Case Sensitive   : P: 0.977 || R: 0.717 || F1: 0.827
Case Insensitive : P: 0.977 || R: 0.717 || F1: 0.827
219 PP_1980_40
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
220 PP_1984_27
Case Sensitive   : P: 0.512 || R: 0.301 || F1: 0.379
Case Insensitive : P: 0.512 || R: 0.301 || F1: 0.379
221 PP_1981_7
Case Sensitive   : P: 1.0 || R: 0.788 || F1: 0.881
Case Insensitive : P: 1.0 || R: 0.788 || F1: 0.881
222 Permen_Keu_2013_218
Case Sensitive   : P: 0.413 || R: 0.788 || F1: 0.542
Case Insensitive : P: 0.413 || R: 0.788 || F1: 0.542
223 Perkab_Garut_2008_2
Case Sensitive   : P: 0.739 || R: 0.695 || F1: 0.716
Case Insensitive : P: 0.739 || R: 0.695 || F1: 0.716
224 Permen_Humham_2012_26
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
225 Perpres_2015_22
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 

Case Insensitive : P: 0.985 || R: 0.65 || F1: 0.783
291 UU_2009_37
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
292 Permen_Keu_2010_147
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
293 Peraturan_OJK_2016_42
Case Sensitive   : P: 1.0 || R: 0.76 || F1: 0.864
Case Insensitive : P: 1.0 || R: 0.76 || F1: 0.864
294 Peraturan_BKPM_2009_1
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
295 Permen_Keu_2011_40
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
296 Permen_Dikbud_2013_52
Case Sensitive   : P: 0.977 || R: 0.578 || F1: 0.726
Case Insensitive : P: 0.977 || R: 0.578 || F1: 0.726
297 Peraturan_OJK_2017_36
Case Sensitive   : P: 0.991 || R: 0.745 || F1: 0.851
Case Insensitive : P: 0.991 || R: 0.745 || F1: 0.851
298 PP_1954_37
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
299 P

...

Case Insensitive : P: 0.811 || R: 0.235 || F1: 0.364
2315 Peraturan_LIPI_2016_4
Case Sensitive   : P: 1.0 || R: 0.747 || F1: 0.855
Case Insensitive : P: 1.0 || R: 0.747 || F1: 0.855
2316 Permen_Parekraf_2012_144
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2317 Perkab_Indragiri_Hilir_2010_21
Case Sensitive   : P: 0.958 || R: 0.532 || F1: 0.684
Case Insensitive : P: 0.958 || R: 0.532 || F1: 0.684
2318 Perpres_2019_38
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2319 Perkab_Ogan_Komering_Ilir_2010_29
Case Sensitive   : P: 1.0 || R: 0.769 || F1: 0.869
Case Insensitive : P: 1.0 || R: 0.769 || F1: 0.869
2320 Perprov_Riau_2013_15
Case Sensitive   : P: 0.473 || R: 0.149 || F1: 0.227
Case Insensitive : P: 0.473 || R: 0.149 || F1: 0.227
2321 Permen_Han_2014_19
Case Sensitive   : P: 0.973 || R: 0.433 || F1: 0.599
Case Insensitive : P: 0.973 || R: 0.433 || F1: 0.599
2322 Peraturan_BNPP_2011_1
Case Sensitive 

Case Insensitive : P: 0.972 || R: 0.258 || F1: 0.408
2382 Permen_PR_2012_24
Case Sensitive   : P: 0.876 || R: 0.464 || F1: 0.607
Case Insensitive : P: 0.876 || R: 0.464 || F1: 0.607
2383 Permen_Keu_2011_232
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2384 Perkab_Ciamis_2011_22
Case Sensitive   : P: 0.833 || R: 0.382 || F1: 0.524
Case Insensitive : P: 0.833 || R: 0.382 || F1: 0.524
2385 Permen_Humham_2019_7
Case Sensitive   : P: 1.0 || R: 0.771 || F1: 0.871
Case Insensitive : P: 1.0 || R: 0.771 || F1: 0.871
2386 Permen_Hub_2017_68
Case Sensitive   : P: 0.598 || R: 0.483 || F1: 0.534
Case Insensitive : P: 0.598 || R: 0.483 || F1: 0.534
2387 PP_2010_50
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2388 Peraturan_PPATK_2017_20
Case Sensitive   : P: 1.0 || R: 0.778 || F1: 0.875
Case Insensitive : P: 1.0 || R: 0.778 || F1: 0.875
2389 Perkab_Sleman_2001_15
Case Sensitive   : P: 0.976 || R: 0.365 || F1: 0

2451 Peraturan_BKN_2018_9
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2452 Permen_Perin_2012_102
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2453 Perkab_Bengkayang_2005_2
Case Sensitive   : P: 0.697 || R: 0.645 || F1: 0.67
Case Insensitive : P: 0.697 || R: 0.645 || F1: 0.67
2454 Perkab_Banyuwangi_2011_3
Case Sensitive   : P: 0.649 || R: 0.281 || F1: 0.392
Case Insensitive : P: 0.649 || R: 0.281 || F1: 0.392
2455 Permen_Ristekdikti_2019_7
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2456 Perkab_Bantul_2008_18
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2457 Perkot_Bekasi_2013_09
Case Sensitive   : P: 0.92 || R: 0.444 || F1: 0.599
Case Insensitive : P: 0.92 || R: 0.444 || F1: 0.599
2458 Permen_Hut_2012_42
Case Sensitive   : P: 0.905 || R: 0.475 || F1: 0.623
Case Insensitive : P: 0.905 || R: 0.475 || F1: 0.62

Case Insensitive : P: 0.726 || R: 0.508 || F1: 0.598
2522 Permen_Keu_2018_34
Case Sensitive   : P: 0.588 || R: 0.328 || F1: 0.421
Case Insensitive : P: 0.588 || R: 0.328 || F1: 0.421
2523 Permen_Dag_2019_41
Case Sensitive   : P: 0.853 || R: 0.508 || F1: 0.637
Case Insensitive : P: 0.853 || R: 0.508 || F1: 0.637
2524 Permen_Dag_2019_16
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2525 Permen_Keu_2015_237
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2526 Perprov_Riau_2013_17
Case Sensitive   : P: 0.746 || R: 0.221 || F1: 0.341
Case Insensitive : P: 0.746 || R: 0.221 || F1: 0.341
2527 Permen_PPPA_2010_10
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2528 Peraturan_BSSN_2016_16
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2529 Perkab_Musi_Rawas_2005_7
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive :

2596 UU_2010_8
Case Sensitive   : P: 0.732 || R: 0.234 || F1: 0.355
Case Insensitive : P: 0.732 || R: 0.234 || F1: 0.355
2597 Perkab_Bantul_2008_15
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2598 Permen_Desa_2018_6
Case Sensitive   : P: 0.829 || R: 0.617 || F1: 0.707
Case Insensitive : P: 0.829 || R: 0.617 || F1: 0.707
2599 Permen_Hut_2010_41
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2600 PP_2015_69
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2601 Permen_LH_2012_20
Case Sensitive   : P: 1.0 || R: 0.798 || F1: 0.888
Case Insensitive : P: 1.0 || R: 0.798 || F1: 0.888
2602 UU_1954_76
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2603 Perkab_Magelang_2010_12
Case Sensitive   : P: 0.78 || R: 0.39 || F1: 0.52
Case Insensitive : P: 0.78 || R: 0.39 || F1: 0.52
2604 Perpres_2016_68
Case Sensitive   : P: 0.0 || R:

In [101]:
test_1('bcl', bc_llama, test_body, '2', results, 'bc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
1 Permen_KP_2013_5
Case Sensitive   : P: 0.798 || R: 0.464 || F1: 0.587
Case Insensitive : P: 0.798 || R: 0.464 || F1: 0.587
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.8 || R: 0.444 || F1: 0.571
Case Insensitive : P: 0.8 || R: 0.444 || F1: 0.571
3 Permen_Par_2015_14
Case Sensitive   : P: 0.085 || R: 0.333 || F1: 0.135
Case Insensitive : P: 0.085 || R: 0.333 || F1: 0.135
4 Perpres_2019_67
Case Sensitive   : P: 1.0 || R: 0.754 || F1: 0.86
Case Insensitive : P: 1.0 || R: 0.754 || F1: 0.86
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.871 || R: 0.232 || F1: 0.366
Case Insensitive : P: 0.871 || R: 0.232 || F1: 0.366
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.604 || R: 0.34 || F1: 0.435
Case Insensitive : P: 0.604 || R: 0.34 || F1: 0.435
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.974 || R: 0.535 || F1: 0.691
Case Insensitive : P: 0.974 || R: 0.535 || F1:

Case Insensitive : P: 0.607 || R: 0.435 || F1: 0.507
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.636 || R: 0.299 || F1: 0.407
Case Insensitive : P: 0.636 || R: 0.299 || F1: 0.407
73 Perpres_2008_41
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
74 Permen_PR_2009_03
Case Sensitive   : P: 0.106 || R: 0.333 || F1: 0.161
Case Insensitive : P: 0.106 || R: 0.333 || F1: 0.161
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.684 || R: 0.433 || F1: 0.53
Case Insensitive : P: 0.684 || R: 0.433 || F1: 0.53
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
77 Perkab_Sleman_2012_9
Case Sensitive   : P: 0.931 || R: 0.32 || F1: 0.476
Case Insensitive : P: 0.931 || R: 0.32 || F1: 0.476
78 PP_1990_59
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
79 Permen_Agama_2016_21
Case Sensitive   : P: 0.8 || R: 0.103 || F1: 0.183
Case Insensitive : P: 0.8 |

Case Insensitive : P: 0.741 || R: 0.683 || F1: 0.711
144 Permen_Naker_2016_17
Case Sensitive   : P: 0.965 || R: 0.673 || F1: 0.793
Case Insensitive : P: 0.965 || R: 0.673 || F1: 0.793
145 Permen_Hub_2015_114
Case Sensitive   : P: 0.106 || R: 0.333 || F1: 0.161
Case Insensitive : P: 0.106 || R: 0.333 || F1: 0.161
146 Perkab_Banyuwangi_2010_8
Case Sensitive   : P: 0.943 || R: 0.592 || F1: 0.727
Case Insensitive : P: 0.943 || R: 0.592 || F1: 0.727
147 PP_1985_33
Case Sensitive   : P: 0.968 || R: 0.606 || F1: 0.745
Case Insensitive : P: 0.968 || R: 0.606 || F1: 0.745
148 Permen_Keu_2012_89
Case Sensitive   : P: 0.963 || R: 0.754 || F1: 0.846
Case Insensitive : P: 0.963 || R: 0.754 || F1: 0.846
149 Permen_Hut_2011_26
Case Sensitive   : P: 0.974 || R: 0.714 || F1: 0.824
Case Insensitive : P: 0.974 || R: 0.714 || F1: 0.824
150 Peraturan_BKPM_2011_11
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
151 Permen_PDT_2014_5
Case Sensitive   : P: 0.986 || R:

217 Permen_PANRB_2013_45
Case Sensitive   : P: 0.991 || R: 0.625 || F1: 0.767
Case Insensitive : P: 0.991 || R: 0.625 || F1: 0.767
218 Peraturan_BPOM_2013_24
Case Sensitive   : P: 0.827 || R: 0.717 || F1: 0.768
Case Insensitive : P: 0.827 || R: 0.717 || F1: 0.768
219 PP_1980_40
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
220 PP_1984_27
Case Sensitive   : P: 0.659 || R: 0.123 || F1: 0.207
Case Insensitive : P: 0.659 || R: 0.123 || F1: 0.207
221 PP_1981_7
Case Sensitive   : P: 1.0 || R: 0.788 || F1: 0.881
Case Insensitive : P: 1.0 || R: 0.788 || F1: 0.881
222 Permen_Keu_2013_218
Case Sensitive   : P: 0.413 || R: 0.788 || F1: 0.542
Case Insensitive : P: 0.413 || R: 0.788 || F1: 0.542
223 Perkab_Garut_2008_2
Case Sensitive   : P: 0.685 || R: 0.627 || F1: 0.655
Case Insensitive : P: 0.685 || R: 0.627 || F1: 0.655
224 Permen_Humham_2012_26
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
225 Perpres_2015_2

286 Perkab_Jayapura_2001_3
Case Sensitive   : P: 0.748 || R: 0.714 || F1: 0.731
Case Insensitive : P: 0.748 || R: 0.714 || F1: 0.731
287 PP_2009_62
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
288 Permen_Hub_2018_12
Case Sensitive   : P: 1.0 || R: 0.765 || F1: 0.867
Case Insensitive : P: 1.0 || R: 0.765 || F1: 0.867
289 Permen_LHK_2017_9
Case Sensitive   : P: 0.106 || R: 0.208 || F1: 0.14
Case Insensitive : P: 0.106 || R: 0.208 || F1: 0.14
290 Perkab_Temanggung_2011_7
Case Sensitive   : P: 0.851 || R: 0.63 || F1: 0.724
Case Insensitive : P: 0.851 || R: 0.63 || F1: 0.724
291 UU_2009_37
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
292 Permen_Keu_2010_147
Case Sensitive   : P: 0.043 || R: 0.333 || F1: 0.076
Case Insensitive : P: 0.043 || R: 0.333 || F1: 0.076
293 Peraturan_OJK_2016_42
Case Sensitive   : P: 1.0 || R: 0.76 || F1: 0.864
Case Insensitive : P: 1.0 || R: 0.76 || F1: 0.864
294 Peraturan_BKP

...

Case Insensitive : P: 0.585 || R: 0.182 || F1: 0.278
2359 Permen_Hut_2010_16
Case Sensitive   : P: 0.106 || R: 0.278 || F1: 0.153
Case Insensitive : P: 0.106 || R: 0.278 || F1: 0.153
2360 Permen_Agama_2014_38
Case Sensitive   : P: 0.575 || R: 0.131 || F1: 0.213
Case Insensitive : P: 0.575 || R: 0.131 || F1: 0.213
2361 Permen_Keu_2013_44
Case Sensitive   : P: 0.106 || R: 0.333 || F1: 0.161
Case Insensitive : P: 0.106 || R: 0.333 || F1: 0.161
2362 Perkab_Mamuju_Utara_2006_18
Case Sensitive   : P: 0.636 || R: 0.417 || F1: 0.504
Case Insensitive : P: 0.636 || R: 0.417 || F1: 0.504
2363 Permen_Hut_2014_38
Case Sensitive   : P: 0.893 || R: 0.794 || F1: 0.841
Case Insensitive : P: 0.893 || R: 0.794 || F1: 0.841
2364 Peraturan_Baznas_2019_3
Case Sensitive   : P: 0.726 || R: 0.458 || F1: 0.562
Case Insensitive : P: 0.726 || R: 0.458 || F1: 0.562
2365 Permen_Ristekdikti_2016_109
Case Sensitive   : P: 0.106 || R: 0.238 || F1: 0.147
Case Insensitive : P: 0.106 || R: 0.238 || F1: 0.147
2366 UU_2013

2425 Perkot_Depok_2008_11
Case Sensitive   : P: 0.242 || R: 0.013 || F1: 0.025
Case Insensitive : P: 0.242 || R: 0.013 || F1: 0.025
2426 Permen_Hub_2014_20
Case Sensitive   : P: 0.968 || R: 0.713 || F1: 0.821
Case Insensitive : P: 0.968 || R: 0.713 || F1: 0.821
2427 Perkab_Pacitan_2010_6
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2428 Perkab_Bengkulu_Tengah_2011_12
Case Sensitive   : P: 0.615 || R: 0.286 || F1: 0.39
Case Insensitive : P: 0.615 || R: 0.286 || F1: 0.39
2429 Permen_KP_2018_64
Case Sensitive   : P: 0.984 || R: 0.713 || F1: 0.827
Case Insensitive : P: 0.984 || R: 0.713 || F1: 0.827
2430 Perprov_Kaltim_2011_08
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2431 Perkab_Jembrana_2011_4
Case Sensitive   : P: 0.789 || R: 0.62 || F1: 0.694
Case Insensitive : P: 0.789 || R: 0.62 || F1: 0.694
2432 PP_2016_59
Case Sensitive   : P: 0.895 || R: 0.644 || F1: 0.749
Case Insensitive : P: 0.895 || R:

2494 Perkot_Samarinda_2008_18
Case Sensitive   : P: 0.759 || R: 0.552 || F1: 0.639
Case Insensitive : P: 0.759 || R: 0.552 || F1: 0.639
2495 UU_1974_4
Case Sensitive   : P: 1.0 || R: 0.75 || F1: 0.857
Case Insensitive : P: 1.0 || R: 0.75 || F1: 0.857
2496 Peraturan_BPKP_2017_6
Case Sensitive   : P: 0.972 || R: 0.767 || F1: 0.857
Case Insensitive : P: 0.972 || R: 0.767 || F1: 0.857
2497 Permen_Perin_2019_35
Case Sensitive   : P: 0.106 || R: 0.333 || F1: 0.161
Case Insensitive : P: 0.106 || R: 0.333 || F1: 0.161
2498 PP_2007_35
Case Sensitive   : P: 0.926 || R: 0.758 || F1: 0.834
Case Insensitive : P: 0.926 || R: 0.758 || F1: 0.834
2499 Permen_Dagri_2016_75
Case Sensitive   : P: 0.917 || R: 0.569 || F1: 0.702
Case Insensitive : P: 0.917 || R: 0.569 || F1: 0.702
2500 Permen_ESDM_2014_36
Case Sensitive   : P: 0.085 || R: 0.333 || F1: 0.135
Case Insensitive : P: 0.085 || R: 0.333 || F1: 0.135
2501 Peraturan_Polri_2015_18
Case Sensitive   : P: 0.966 || R: 0.521 || F1: 0.677
Case Insensitive 

Case Insensitive : P: 0.857 || R: 0.684 || F1: 0.761
2565 Permen_Keu_2015_229
Case Sensitive   : P: 1.0 || R: 0.806 || F1: 0.893
Case Insensitive : P: 1.0 || R: 0.806 || F1: 0.893
2566 Peraturan_BPH_Migas_2018_10
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2567 UU_1957_49
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2568 Permen_Dagri_2011_41
Case Sensitive   : P: 0.944 || R: 0.675 || F1: 0.787
Case Insensitive : P: 0.944 || R: 0.675 || F1: 0.787
2569 Permen_Agama_2016_2
Case Sensitive   : P: 0.485 || R: 0.032 || F1: 0.06
Case Insensitive : P: 0.485 || R: 0.032 || F1: 0.06
2570 Permenko_Kesra_2014_9
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2571 Peraturan_Basarnas_2016_2
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2572 Peraturan_Bapeten_2011_7
Case Sensitive   : P: 1.0 || R: 0.717 || F1: 0.835
Case Insens

2637 Peraturan_MA_2017_4
Case Sensitive   : P: 0.918 || R: 0.703 || F1: 0.796
Case Insensitive : P: 0.918 || R: 0.703 || F1: 0.796
2638 Perpres_2014_108
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2639 Perppu_2017_1
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0

####################################################

bcl 2 Shot

Case Sensitive
Precision: 0.657
Recall: 0.375
F1 Score: 0.477

Case Insensitive
Precision: 0.657
Recall: 0.375
F1 Score: 0.477


In [102]:
test_1('bcp', bc_phi, test_body, '1', results, 'bc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.45 || R: 0.333 || F1: 0.383
Case Insensitive : P: 0.45 || R: 0.333 || F1: 0.383
1 Permen_KP_2013_5
Case Sensitive   : P: 0.769 || R: 0.419 || F1: 0.542
Case Insensitive : P: 0.769 || R: 0.419 || F1: 0.542
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.537 || R: 0.434 || F1: 0.48
Case Insensitive : P: 0.537 || R: 0.434 || F1: 0.48
3 Permen_Par_2015_14
Case Sensitive   : P: 0.4 || R: 0.333 || F1: 0.363
Case Insensitive : P: 0.4 || R: 0.333 || F1: 0.363
4 Perpres_2019_67
Case Sensitive   : P: 1.0 || R: 0.754 || F1: 0.86
Case Insensitive : P: 1.0 || R: 0.754 || F1: 0.86
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.344 || R: 0.12 || F1: 0.178
Case Insensitive : P: 0.344 || R: 0.12 || F1: 0.178
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.667 || R: 0.298 || F1: 0.412
Case Insensitive : P: 0.667 || R: 0.298 || F1: 0.412
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.616 || R: 0.423 || F1: 0.502
Case Insensitive : P: 0.616 || R: 

69 PP_2018_49
Case Sensitive   : P: 0.703 || R: 0.263 || F1: 0.383
Case Insensitive : P: 0.703 || R: 0.263 || F1: 0.383
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 0.429 || R: 0.333 || F1: 0.375
Case Insensitive : P: 0.429 || R: 0.333 || F1: 0.375
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.845 || R: 0.573 || F1: 0.683
Case Insensitive : P: 0.845 || R: 0.573 || F1: 0.683
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.456 || R: 0.154 || F1: 0.23
Case Insensitive : P: 0.456 || R: 0.154 || F1: 0.23
73 Perpres_2008_41
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
74 Permen_PR_2009_03
Case Sensitive   : P: 0.417 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.557 || R: 0.356 || F1: 0.434
Case Insensitive : P: 0.557 || R: 0.356 || F1: 0.434
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.425 || R: 0.333 || F1: 0.373
Case Insensitive : P: 

136 Peraturan_BNPB_2016_02
Case Sensitive   : P: 0.345 || R: 0.11 || F1: 0.167
Case Insensitive : P: 0.345 || R: 0.11 || F1: 0.167
137 Peraturan_Perpusnas_2018_8
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
138 PP_1998_77
Case Sensitive   : P: 1.0 || R: 0.794 || F1: 0.885
Case Insensitive : P: 1.0 || R: 0.794 || F1: 0.885
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 0.333 || R: 0.333 || F1: 0.333
Case Insensitive : P: 0.333 || R: 0.333 || F1: 0.333
140 Permen_Keu_2015_108
Case Sensitive   : P: 0.417 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
141 Permen_LHK_2019_13
Case Sensitive   : P: 0.898 || R: 0.611 || F1: 0.727
Case Insensitive : P: 0.898 || R: 0.611 || F1: 0.727
142 PP_1983_17
Case Sensitive   : P: 0.812 || R: 0.63 || F1: 0.71
Case Insensitive : P: 0.812 || R: 0.63 || F1: 0.71
143 Perpres_2015_82
Case Sensitive   : P: 0.943 || R: 0.794 || F1: 0.862
Case Insensitive : P: 0.943 || R: 0.7

Case Insensitive : P: 0.8 || R: 0.598 || F1: 0.684
206 Permen_Dagri_2017_3
Case Sensitive   : P: 0.583 || R: 0.45 || F1: 0.508
Case Insensitive : P: 0.583 || R: 0.45 || F1: 0.508
207 UU_2012_8
Case Sensitive   : P: 0.563 || R: 0.078 || F1: 0.137
Case Insensitive : P: 0.563 || R: 0.078 || F1: 0.137
208 Permen_Keu_2010_262
Case Sensitive   : P: 1.0 || R: 0.701 || F1: 0.824
Case Insensitive : P: 1.0 || R: 0.701 || F1: 0.824
209 PP_1998_25
Case Sensitive   : P: 1.0 || R: 0.792 || F1: 0.884
Case Insensitive : P: 1.0 || R: 0.792 || F1: 0.884
210 Perkot_Depok_2011_07
Case Sensitive   : P: 0.942 || R: 0.649 || F1: 0.769
Case Insensitive : P: 0.942 || R: 0.649 || F1: 0.769
211 PP_2012_13
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
212 Permen_Dikbud_2011_50
Case Sensitive   : P: 1.0 || R: 0.722 || F1: 0.839
Case Insensitive : P: 1.0 || R: 0.722 || F1: 0.839
213 Permen_LH_2012_10
Case Sensitive   : P: 0.458 || R: 0.333 || F1: 0.386
Cas

271 Peraturan_BKN_2019_16
Case Sensitive   : P: 0.496 || R: 0.245 || F1: 0.328
Case Insensitive : P: 0.496 || R: 0.245 || F1: 0.328
272 Permen_Humham_2015_45
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
273 Permen_KP_2018_13
Case Sensitive   : P: 0.828 || R: 0.547 || F1: 0.659
Case Insensitive : P: 0.828 || R: 0.547 || F1: 0.659
274 UU_1999_11
Case Sensitive   : P: 0.963 || R: 0.722 || F1: 0.825
Case Insensitive : P: 0.963 || R: 0.722 || F1: 0.825
275 Peraturan_BPS_2019_1
Case Sensitive   : P: 0.438 || R: 0.333 || F1: 0.378
Case Insensitive : P: 0.438 || R: 0.333 || F1: 0.378
276 Permen_PU_2013_11
Case Sensitive   : P: 0.867 || R: 0.788 || F1: 0.826
Case Insensitive : P: 0.867 || R: 0.788 || F1: 0.826
277 Perkot_Tangerang_2009_3
Case Sensitive   : P: 0.541 || R: 0.441 || F1: 0.486
Case Insensitive : P: 0.541 || R: 0.441 || F1: 0.486
278 Permen_Hub_2018_110
Case Sensitive   : P: 0.986 || R: 0.483 || F1: 0.648
Case Insensitive : P: 0.986 || R:

...

Case Insensitive : P: 0.442 || R: 0.199 || F1: 0.274
2352 UU_2002_27
Case Sensitive   : P: 0.745 || R: 0.651 || F1: 0.695
Case Insensitive : P: 0.745 || R: 0.651 || F1: 0.695
2353 Permen_PUPR_2015_01
Case Sensitive   : P: 0.384 || R: 0.276 || F1: 0.321
Case Insensitive : P: 0.384 || R: 0.276 || F1: 0.321
2354 PP_2019_28
Case Sensitive   : P: 0.462 || R: 0.333 || F1: 0.387
Case Insensitive : P: 0.462 || R: 0.333 || F1: 0.387
2355 Perkot_Depok_2003_10
Case Sensitive   : P: 1.0 || R: 0.797 || F1: 0.887
Case Insensitive : P: 1.0 || R: 0.797 || F1: 0.887
2356 Permen_Hub_2013_16
Case Sensitive   : P: 0.909 || R: 0.682 || F1: 0.779
Case Insensitive : P: 0.909 || R: 0.682 || F1: 0.779
2357 Perpres_2009_42
Case Sensitive   : P: 0.429 || R: 0.333 || F1: 0.375
Case Insensitive : P: 0.429 || R: 0.333 || F1: 0.375
2358 Permen_Ristekdikti_2017_75
Case Sensitive   : P: 0.516 || R: 0.124 || F1: 0.2
Case Insensitive : P: 0.516 || R: 0.124 || F1: 0.2
2359 Permen_Hut_2010_16
Case Sensitive   : P: 0.429 |

Case Insensitive : P: 0.457 || R: 0.412 || F1: 0.433
2417 Permen_Hub_2018_27
Case Sensitive   : P: 0.392 || R: 0.142 || F1: 0.208
Case Insensitive : P: 0.392 || R: 0.142 || F1: 0.208
2418 PP_1996_14
Case Sensitive   : P: 0.96 || R: 0.571 || F1: 0.716
Case Insensitive : P: 0.96 || R: 0.571 || F1: 0.716
2419 Peraturan_LKPP_2018_11
Case Sensitive   : P: 0.292 || R: 0.141 || F1: 0.19
Case Insensitive : P: 0.292 || R: 0.141 || F1: 0.19
2420 PP_1980_51
Case Sensitive   : P: 0.429 || R: 0.333 || F1: 0.375
Case Insensitive : P: 0.429 || R: 0.333 || F1: 0.375
2421 Permen_Keu_2014_100
Case Sensitive   : P: 0.464 || R: 0.333 || F1: 0.388
Case Insensitive : P: 0.464 || R: 0.333 || F1: 0.388
2422 Perkot_Tasikmalaya_2004_16
Case Sensitive   : P: 0.942 || R: 0.77 || F1: 0.847
Case Insensitive : P: 0.942 || R: 0.77 || F1: 0.847
2423 Perkot_Binjai_2001_26
Case Sensitive   : P: 0.983 || R: 0.75 || F1: 0.851
Case Insensitive : P: 0.983 || R: 0.75 || F1: 0.851
2424 PP_1986_23
Case Sensitive   : P: 0.455 |

Case Insensitive : P: 1.0 || R: 0.765 || F1: 0.867
2482 PP_1978_10
Case Sensitive   : P: 0.92 || R: 0.767 || F1: 0.837
Case Insensitive : P: 0.92 || R: 0.767 || F1: 0.837
2483 PP_1981_6
Case Sensitive   : P: 0.389 || R: 0.333 || F1: 0.359
Case Insensitive : P: 0.389 || R: 0.333 || F1: 0.359
2484 Permen_Keu_2014_59
Case Sensitive   : P: 1.0 || R: 0.774 || F1: 0.873
Case Insensitive : P: 1.0 || R: 0.774 || F1: 0.873
2485 Peraturan_BPOM_2013_29
Case Sensitive   : P: 0.429 || R: 0.333 || F1: 0.375
Case Insensitive : P: 0.429 || R: 0.333 || F1: 0.375
2486 PP_1961_166
Case Sensitive   : P: 0.125 || R: 0.333 || F1: 0.182
Case Insensitive : P: 0.125 || R: 0.333 || F1: 0.182
2487 Permen_Humham_2016_66
Case Sensitive   : P: 0.68 || R: 0.548 || F1: 0.607
Case Insensitive : P: 0.68 || R: 0.548 || F1: 0.607
2488 PP_2007_62
Case Sensitive   : P: 0.28 || R: 0.333 || F1: 0.304
Case Insensitive : P: 0.28 || R: 0.333 || F1: 0.304
2489 Permen_Dikbud_2013_1
Case Sensitive   : P: 0.646 || R: 0.474 || F1: 0

Case Insensitive : P: 0.228 || R: 0.062 || F1: 0.097
2551 Perkab_Serdang_Bedagai_2012_14
Case Sensitive   : P: 0.333 || R: 0.286 || F1: 0.308
Case Insensitive : P: 0.333 || R: 0.286 || F1: 0.308
2552 PP_2003_34
Case Sensitive   : P: 0.444 || R: 0.333 || F1: 0.381
Case Insensitive : P: 0.444 || R: 0.333 || F1: 0.381
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.331 || R: 0.202 || F1: 0.251
Case Insensitive : P: 0.331 || R: 0.202 || F1: 0.251
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 0.444 || R: 0.333 || F1: 0.381
Case Insensitive : P: 0.444 || R: 0.333 || F1: 0.381
2555 Peraturan_OJK_2019_13
Case Sensitive   : P: 0.988 || R: 0.683 || F1: 0.808
Case Insensitive : P: 0.988 || R: 0.683 || F1: 0.808
2556 Permen_Kes_2013_75
Case Sensitive   : P: 0.438 || R: 0.333 || F1: 0.378
Case Insensitive : P: 0.438 || R: 0.333 || F1: 0.378
2557 Permen_Dagri_2012_16
Case Sensitive   : P: 0.417 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
2558 Perkot_Bogor_201

Case Insensitive : P: 0.591 || R: 0.134 || F1: 0.218
2617 PP_1961_163
Case Sensitive   : P: 0.25 || R: 0.333 || F1: 0.286
Case Insensitive : P: 0.25 || R: 0.333 || F1: 0.286
2618 PP_2008_69
Case Sensitive   : P: 0.333 || R: 0.333 || F1: 0.333
Case Insensitive : P: 0.333 || R: 0.333 || F1: 0.333
2619 Permen_Han_2014_18
Case Sensitive   : P: 0.681 || R: 0.474 || F1: 0.559
Case Insensitive : P: 0.681 || R: 0.474 || F1: 0.559
2620 PP_2002_60
Case Sensitive   : P: 0.333 || R: 0.333 || F1: 0.333
Case Insensitive : P: 0.333 || R: 0.333 || F1: 0.333
2621 Permen_Nakertrans_2009_22
Case Sensitive   : P: 0.978 || R: 0.722 || F1: 0.831
Case Insensitive : P: 0.978 || R: 0.722 || F1: 0.831
2622 Peraturan_LAN_2017_2
Case Sensitive   : P: 0.417 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
2623 Peraturan_BPJSKES_2018_6
Case Sensitive   : P: 0.277 || R: 0.139 || F1: 0.185
Case Insensitive : P: 0.277 || R: 0.139 || F1: 0.185
2624 Permen_Dikbud_2011_56
Case Sensitive   : P: 

In [103]:
test_1('bcp', bc_phi, test_body, '2', results, 'bc')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
1 Permen_KP_2013_5
Case Sensitive   : P: 0.571 || R: 0.342 || F1: 0.428
Case Insensitive : P: 0.571 || R: 0.342 || F1: 0.428
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.613 || R: 0.465 || F1: 0.529
Case Insensitive : P: 0.613 || R: 0.465 || F1: 0.529
3 Permen_Par_2015_14
Case Sensitive   : P: 0.4 || R: 0.333 || F1: 0.363
Case Insensitive : P: 0.4 || R: 0.333 || F1: 0.363
4 Perpres_2019_67
Case Sensitive   : P: 1.0 || R: 0.754 || F1: 0.86
Case Insensitive : P: 1.0 || R: 0.754 || F1: 0.86
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.33 || R: 0.106 || F1: 0.16
Case Insensitive : P: 0.33 || R: 0.106 || F1: 0.16
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.622 || R: 0.298 || F1: 0.403
Case Insensitive : P: 0.622 || R: 0.298 || F1: 0.403
7 Permen_Humham_2016_16
Case Sensitive   : P: 0.587 || R: 0.38 || F1: 0.461
Case Insensitive : P: 0.587 || R: 0.38 || F1: 0.4

Case Insensitive : P: 0.577 || R: 0.175 || F1: 0.269
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 0.429 || R: 0.333 || F1: 0.375
Case Insensitive : P: 0.429 || R: 0.333 || F1: 0.375
71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.412 || R: 0.282 || F1: 0.335
Case Insensitive : P: 0.412 || R: 0.282 || F1: 0.335
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.384 || R: 0.205 || F1: 0.267
Case Insensitive : P: 0.384 || R: 0.205 || F1: 0.267
73 Perpres_2008_41
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
74 Permen_PR_2009_03
Case Sensitive   : P: 0.417 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.559 || R: 0.344 || F1: 0.426
Case Insensitive : P: 0.559 || R: 0.344 || F1: 0.426
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.415 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.415 || R: 0.333 || F1: 0.37
77 Perkab_Sleman_2012_9
Case Sensiti

136 Peraturan_BNPB_2016_02
Case Sensitive   : P: 0.375 || R: 0.128 || F1: 0.191
Case Insensitive : P: 0.375 || R: 0.128 || F1: 0.191
137 Peraturan_Perpusnas_2018_8
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
138 PP_1998_77
Case Sensitive   : P: 1.0 || R: 0.794 || F1: 0.885
Case Insensitive : P: 1.0 || R: 0.794 || F1: 0.885
139 Peraturan_BKN_2014_6
Case Sensitive   : P: 0.333 || R: 0.333 || F1: 0.333
Case Insensitive : P: 0.333 || R: 0.333 || F1: 0.333
140 Permen_Keu_2015_108
Case Sensitive   : P: 0.417 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
141 Permen_LHK_2019_13
Case Sensitive   : P: 0.804 || R: 0.514 || F1: 0.627
Case Insensitive : P: 0.804 || R: 0.514 || F1: 0.627
142 PP_1983_17
Case Sensitive   : P: 0.413 || R: 0.303 || F1: 0.35
Case Insensitive : P: 0.413 || R: 0.303 || F1: 0.35
143 Perpres_2015_82
Case Sensitive   : P: 0.604 || R: 0.508 || F1: 0.552
Case Insensitive : P: 0.604 || R:

205 Permen_PANRB_2013_32
Case Sensitive   : P: 0.739 || R: 0.506 || F1: 0.601
Case Insensitive : P: 0.739 || R: 0.506 || F1: 0.601
206 Permen_Dagri_2017_3
Case Sensitive   : P: 0.587 || R: 0.411 || F1: 0.483
Case Insensitive : P: 0.587 || R: 0.411 || F1: 0.483
207 UU_2012_8
Case Sensitive   : P: 0.324 || R: 0.025 || F1: 0.046
Case Insensitive : P: 0.324 || R: 0.025 || F1: 0.046
208 Permen_Keu_2010_262
Case Sensitive   : P: 1.0 || R: 0.747 || F1: 0.855
Case Insensitive : P: 1.0 || R: 0.747 || F1: 0.855
209 PP_1998_25
Case Sensitive   : P: 1.0 || R: 0.792 || F1: 0.884
Case Insensitive : P: 1.0 || R: 0.792 || F1: 0.884
210 Perkot_Depok_2011_07
Case Sensitive   : P: 0.638 || R: 0.291 || F1: 0.4
Case Insensitive : P: 0.638 || R: 0.291 || F1: 0.4
211 PP_2012_13
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
212 Permen_Dikbud_2011_50
Case Sensitive   : P: 1.0 || R: 0.687 || F1: 0.814
Case Insensitive : P: 1.0 || R: 0.687 || F1: 0.814


277 Perkot_Tangerang_2009_3
Case Sensitive   : P: 0.523 || R: 0.419 || F1: 0.465
Case Insensitive : P: 0.523 || R: 0.419 || F1: 0.465
278 Permen_Hub_2018_110
Case Sensitive   : P: 0.986 || R: 0.483 || F1: 0.648
Case Insensitive : P: 0.986 || R: 0.483 || F1: 0.648
279 Peraturan_BKPM_2009_5
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
280 Permen_Dag_2012_82
Case Sensitive   : P: 0.472 || R: 0.333 || F1: 0.39
Case Insensitive : P: 0.472 || R: 0.333 || F1: 0.39
281 Peraturan_OJK_2018_32
Case Sensitive   : P: 0.758 || R: 0.361 || F1: 0.489
Case Insensitive : P: 0.758 || R: 0.361 || F1: 0.489
282 Perkot_Binjai_2000_5
Case Sensitive   : P: 0.886 || R: 0.759 || F1: 0.818
Case Insensitive : P: 0.886 || R: 0.759 || F1: 0.818
283 Peraturan_BKN_2015_47
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
284 Peraturan_BPIP_2018_3
Case Sensitive   : P: 0.812 || R: 0.722 || F1: 0.764
Cas

...

2327 Perkab_Garut_2009_5
Case Sensitive   : P: 0.964 || R: 0.806 || F1: 0.878
Case Insensitive : P: 0.964 || R: 0.806 || F1: 0.878
2328 Permen_Han_2015_16
Case Sensitive   : P: 1.0 || R: 0.778 || F1: 0.875
Case Insensitive : P: 1.0 || R: 0.778 || F1: 0.875
2329 UU_2003_7
Case Sensitive   : P: 0.839 || R: 0.754 || F1: 0.794
Case Insensitive : P: 0.839 || R: 0.754 || F1: 0.794
2330 PP_1981_17
Case Sensitive   : P: 0.966 || R: 0.778 || F1: 0.862
Case Insensitive : P: 0.966 || R: 0.778 || F1: 0.862
2331 Permen_Keu_2014_252
Case Sensitive   : P: 0.349 || R: 0.088 || F1: 0.141
Case Insensitive : P: 0.349 || R: 0.088 || F1: 0.141
2332 Permen_Hub_2016_144
Case Sensitive   : P: 0.79 || R: 0.5 || F1: 0.612
Case Insensitive : P: 0.79 || R: 0.5 || F1: 0.612
2333 Permen_Parekraf_2013_07
Case Sensitive   : P: 0.4 || R: 0.333 || F1: 0.363
Case Insensitive : P: 0.4 || R: 0.333 || F1: 0.363
2334 Peraturan_Polri_2013_2
Case Sensitive   : P: 1.0 || R: 0.759 || F1: 0.863
Case Insensitive : P: 1.0 || R: 0.

Case Insensitive : P: 0.79 || R: 0.56 || F1: 0.655
2398 UU_2009_24
Case Sensitive   : P: 0.437 || R: 0.237 || F1: 0.307
Case Insensitive : P: 0.437 || R: 0.237 || F1: 0.307
2399 Permen_Dagri_2012_60
Case Sensitive   : P: 1.0 || R: 0.754 || F1: 0.86
Case Insensitive : P: 1.0 || R: 0.754 || F1: 0.86
2400 Permen_ESDM_2013_19
Case Sensitive   : P: 0.976 || R: 0.651 || F1: 0.781
Case Insensitive : P: 0.976 || R: 0.651 || F1: 0.781
2401 Peraturan_LKPP_2019_14
Case Sensitive   : P: 0.967 || R: 0.728 || F1: 0.831
Case Insensitive : P: 0.967 || R: 0.728 || F1: 0.831
2402 Permen_Hub_2017_87
Case Sensitive   : P: 0.876 || R: 0.606 || F1: 0.716
Case Insensitive : P: 0.876 || R: 0.606 || F1: 0.716
2403 Peraturan_Batan_2016_4
Case Sensitive   : P: 0.462 || R: 0.333 || F1: 0.387
Case Insensitive : P: 0.462 || R: 0.333 || F1: 0.387
2404 PP_1957_13
Case Sensitive   : P: 0.006 || R: 0.333 || F1: 0.012
Case Insensitive : P: 0.006 || R: 0.333 || F1: 0.012
2405 Peraturan_BPJSTK_2018_1
Case Sensitive   : P:

2464 Perpres_2015_161
Case Sensitive   : P: 0.444 || R: 0.333 || F1: 0.381
Case Insensitive : P: 0.444 || R: 0.333 || F1: 0.381
2465 Peraturan_Bawaslu_2012_7
Case Sensitive   : P: 0.812 || R: 0.59 || F1: 0.683
Case Insensitive : P: 0.812 || R: 0.59 || F1: 0.683
2466 Permen_ESDM_2016_02
Case Sensitive   : P: 0.417 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
2467 Perkot_Binjai_2001_5
Case Sensitive   : P: 0.902 || R: 0.761 || F1: 0.826
Case Insensitive : P: 0.902 || R: 0.761 || F1: 0.826
2468 Permenko_Polhukam_2016_4
Case Sensitive   : P: 0.4 || R: 0.333 || F1: 0.363
Case Insensitive : P: 0.4 || R: 0.333 || F1: 0.363
2469 UU_1998_13
Case Sensitive   : P: 0.913 || R: 0.737 || F1: 0.816
Case Insensitive : P: 0.913 || R: 0.737 || F1: 0.816
2470 Peraturan_BNPP_2012_3
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2471 Permen_KP_2016_30
Case Sensitive   : P: 1.0 || R: 0.75 || F1: 0.857
Case Insensitive : P: 1.0 || R: 0

2532 Perkab_Tanggamus_2012_01
Case Sensitive   : P: 0.738 || R: 0.571 || F1: 0.644
Case Insensitive : P: 0.738 || R: 0.571 || F1: 0.644
2533 Permen_Dag_2015_104
Case Sensitive   : P: 0.4 || R: 0.333 || F1: 0.363
Case Insensitive : P: 0.4 || R: 0.333 || F1: 0.363
2534 Peraturan_BNP2TKI_2017_06
Case Sensitive   : P: 0.375 || R: 0.333 || F1: 0.353
Case Insensitive : P: 0.375 || R: 0.333 || F1: 0.353
2535 Permen_Dagri_2013_18
Case Sensitive   : P: 0.417 || R: 0.333 || F1: 0.37
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
2536 Permen_Tan_2013_50
Case Sensitive   : P: 0.4 || R: 0.333 || F1: 0.363
Case Insensitive : P: 0.4 || R: 0.333 || F1: 0.363
2537 Perprov_Jabar_2002_7
Case Sensitive   : P: 0.1 || R: 0.1 || F1: 0.1
Case Insensitive : P: 0.1 || R: 0.1 || F1: 0.1
2538 Peraturan_OJK_2016_13
Case Sensitive   : P: 0.438 || R: 0.333 || F1: 0.378
Case Insensitive : P: 0.438 || R: 0.333 || F1: 0.378
2539 PP_1961_127
Case Sensitive   : P: 0.391 || R: 0.521 || F1: 0.447
Case Insensitive : P:

2600 PP_2015_69
Case Sensitive   : P: 0.455 || R: 0.333 || F1: 0.385
Case Insensitive : P: 0.455 || R: 0.333 || F1: 0.385
2601 Permen_LH_2012_20
Case Sensitive   : P: 0.952 || R: 0.526 || F1: 0.678
Case Insensitive : P: 0.952 || R: 0.526 || F1: 0.678
2602 UU_1954_76
Case Sensitive   : P: 1.0 || R: 0.667 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2603 Perkab_Magelang_2010_12
Case Sensitive   : P: 0.505 || R: 0.46 || F1: 0.481
Case Insensitive : P: 0.505 || R: 0.46 || F1: 0.481
2604 Perpres_2016_68
Case Sensitive   : P: 0.333 || R: 0.333 || F1: 0.333
Case Insensitive : P: 0.333 || R: 0.333 || F1: 0.333
2605 Permen_Agama_2015_41
Case Sensitive   : P: 1.0 || R: 0.75 || F1: 0.857
Case Insensitive : P: 1.0 || R: 0.75 || F1: 0.857
2606 Peraturan_BKN_2012_16
Case Sensitive   : P: 0.611 || R: 0.365 || F1: 0.457
Case Insensitive : P: 0.611 || R: 0.365 || F1: 0.457
2607 Permen_Kes_2016_56
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
26

# Contoh

In [105]:
print(cc_gemma.at[0, '2'])

lexid:Permen_Ristekdikti_2017_20 lexid-s:hasPromulgationPlace lexid:Berita_Negara_Republik_Indonesia .
lexid:Permen_Ristekdikti_2017_20 lexid-s:hasEnactionDate "2017-01-27"^^xsd:date .
lexid:Permen_Ristekdikti_2017_20 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:Permen_Ristekdikti_2017_20 lexid-s:hasEnactionOfficial lexid:Person_Mohamad_Nasir .
lexid:Person_Mohamad_Nasir rdf:type lexid-s:Person .
lexid:Person_Mohamad_Nasir rdfs:label "Mohamad Nasir"^^xsd:string .
lexid:Permen_Ristekdikti_2017_20 lexid-s:hasEnactionOffice lexid:Position_Menteri_Riset_Teknologi_Dan_Pendidikan_Tinggi_Republik_Indonesia .
lexid:Position_Menteri_Riset_Teknologi_Dan_Pendidikan_Tinggi_Republik_Indonesia rdf:type lexid-s:Position .
lexid:Position_Menteri_Riset_Teknologi_Dan_Pendidikan_Tinggi_Republik_Indonesia rdfs:label "Menteri Riset, Teknologi, dan Pendidikan Tinggi Republik Indonesia"^^xsd:string .
le